In [1]:
import re
import pandas as pd
import numpy as np
import joblib

import warnings
warnings.filterwarnings('ignore')

import matplotlib.pyplot as plt
import gensim
import nltk

from nltk.stem.snowball import SnowballStemmer

from gensim.corpora import Dictionary, MmCorpus
from gensim.models import ldamodel

from sklearn.cluster import KMeans
from sklearn.manifold import MDS
from sklearn.decomposition import PCA

PATH = "D:/Repository/PetaKabar/what/"
prebandingan_path = "D:/Repository/PetaKabar/perbandingan/"
bencana = "bencana/"
ekonomi = "ekonomi/"
kecelakaan = "kecelakaan/"
kesehatan = "kesehatan/"
kriminalitas = "kriminalitas/"
olahraga = "olahraga/"

In [6]:
old = pd.read_csv('perbandingan/berita-24-5.csv')
# print(old)
new = pd.read_csv('perbandingan/berita-24-5.csv') # need changes
# print(new)

In [3]:
# old.columns
old.columns

Index(['ID', 'berita_title', 'berita_date', 'berita_qdate', 'berita_desc',
       'berita_source', 'created_at', 'berita_topik_id', 'qe_what', 'ner_when',
       'ner_who', 'ner_prov', 'ner_kab', 'ner_kec', 'ner_neg', 'sev_death',
       'sev_injury', 'sev_lost', 'sev_sink', 'sev_plane', 'sev_moneyUSD',
       'sev_moneyIDR', 'sev_persen', 'sev_inflasi', 'sev_internasional',
       'sev_nasional', 'sev_provkota', 'sev_lost_items', 'sev_lost_money',
       'sev_rape', 'sev_house', 'sev_person', 'class_classification',
       'berita_summary'],
      dtype='object')

# Bencana

In [243]:
# Bencana Section (Topic id = 1)
old_bencana = old[old['berita_topik_id'] == 1]
old_bencana = old_bencana[['berita_title', 'berita_date', 'berita_desc', 'berita_source']]
old_bencana.rename(columns = {'berita_title':'title', 'berita_date':'date', 'berita_desc':'desc', 'berita_source':'source'}, inplace=True)
print(old_bencana.shape)
old_bencana.head(1)

(2773, 4)


title                          date  \
0  Bagaimana Proses Terjadinya Gempa Bumi?  Kamis, 15 Des 2022 17:02 WIB   

                                                desc          source  
0  \- Saat gempa bumi terjadi, tanah dan apa saja...  www.kompas.com

## Preprocess

In [244]:
from keybert import KeyBERT
from sentence_transformers import SentenceTransformer
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.metrics.pairwise import cosine_similarity

In [245]:
# previous way

# nltk.download('punkt')
# nltk.download('stopwords')

excluded_words = ["tempat", "waktu", "hari"]
# for lda ----
excluded_words = []
# ------------
NLTK_StopWords = stopwords.words('indonesian')
# print(NLTK_StopWords)
NLTK_StopWords.extend(["detik", "detikjatim", "detikjateng", "detikjabar", "detiksulsel", "detiksumbar", "detikbali",
                      "detikpapua", "detiksulteng", "detikmaluku", "detjatim", "detikcom", "allahumma", "aamiin", "allah", "bismillah"])
NLTK_StopWords.extend(["yg", "dg", "rt", "dgn", "ny", "d", 'klo',
                       'kalo', 'amp', 'biar', 'bikin', 'bilang',
                       'gak', 'ga', 'krn', 'nya', 'nih', 'sih',
                       'si', 'tau', 'tdk', 'tuh', 'utk', 'ya',
                       'jd', 'jgn', 'sdh', 'aja', 'n', 't',
                       'nyg', 'hehe', 'pen', 'u', 'nan', 'loh', 'rt',
                       '&amp', 'yah'])
# txt_stopword = pd.read_csv(PATH + bencana + "stopwords.txt", names= ["stopwords"], header = None)
# NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
# for lda ----
txt_stopword = pd.read_csv(PATH + bencana + "stopwords_add_v1.txt", names= ["stopwords"], header = None)
NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
txt_stopword = pd.read_csv(PATH + bencana + "stopwords_add_v2.txt", names= ["stopwords"], header = None)
NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
txt_stopword = pd.read_csv(PATH + bencana + "stopwords_add_v3.txt", names= ["stopwords"], header = None)
NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
# ------------

# convert stopword string to list & append additional stopword
NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
NLTK_StopWords = set(NLTK_StopWords)

In [246]:
def preprocessing(berita):
        s = str(berita)
        s = s.lower()
        s = s.replace('\n', ' ')
        s = s.replace('\r', ' ')
        # s = re.sub(r'[^a-zA-Z0-9\s]', ' ', s)
        # for lda ----
        s = re.sub(r'[^a-zA-Z\s]', ' ', s)
        # ------------
        tokens = [token for token in s.split(" ") if token != ""]
        T = [t for t in tokens if (
            (t in excluded_words) or (t not in NLTK_StopWords))]
        return T

In [247]:
old_bencana = old_bencana.dropna(subset=['desc'])
old_bencana.sort_values('desc', inplace=True)
old_bencana.drop_duplicates(subset='desc', keep=False, inplace=True)
df_train, df_test = train_test_split(old_bencana,test_size=0.1)
print(len(df_train))

old_bencana.head()

2495


title  \
9646  Imbas Banjir di Semarang, KA Tujuan Jakarta An...   
648   5 Titik Banjir di Tangerang Selatan Pagi Ini, ...   
47    Si Jago Merah Menyala di Balikpapan, Dua Rumah...   
1784  Banjir-Tanah Longsor Berulang hingga Menggenan...   
585   Banjir Natuna, Pemprov Kepri Bantu Rp 300 Juta...   

                              date  \
9646  Sabtu, 31 Des 2022 23:39 WIB   
648   Jumat, 02 Des 2022 09:04 WIB   
47    Senin, 28 Nov 2022 13:41 WIB   
1784   Rabu, 07 Des 2022 11:50 WIB   
585   Sabtu, 17 Des 2022 09:15 WIB   

                                                   desc              source  
9646    \r\n  \r\n\- Imbas banjir yang menggenangi h...  www.tribunnews.com  
648     \r\n\- Banjir masih menggenangi sejumlah dae...      www.kompas.com  
47     Api mendadak muncul dari salah satu rumah war...      www.kompas.com  
1784   Badan Penanggulangan Bencana Daerah (BPBD) Ku...      www.kompas.com  
585    Banjir bandang melanda Kabupatan Natuna dan P...      www.kompas.com

In [19]:
df_train.to_csv(PATH + bencana + "corpus/df_train_unprerocessed.csv" , index = None, header=True)
df_test.to_csv(PATH + bencana + "corpus/df_test_unprerocessed.csv" , index = None, header=True)

In [21]:
desc_text_train_unpreprocessed = []
desc_text_test_unpreprocessed = []

for x in range(0, df_train.shape[0]):
  desc_text_train_unpreprocessed.append(df_train.iloc[x, -2])

for x in range(0, df_test.shape[0]):
  desc_text_test_unpreprocessed.append(df_test.iloc[x, -2])

In [22]:
# Simpan teks asli dokumen
joblib.dump(desc_text_test_unpreprocessed, PATH + bencana + "corpus/model/desc_text_test_unpreprocessed.pkl")
joblib.dump(desc_text_train_unpreprocessed, PATH + bencana + "corpus/model/desc_text_train_unpreprocessed.pkl")

# Simpan dataframe hasil text processing sebelum TF-IDF Vectorizer
old_bencana.to_csv(PATH + bencana + 'corpus/dataset/df_total_unpreprocessed.csv', index=False)
df_test.to_csv(PATH + bencana + 'corpus/dataset/df_test_unpreprocessed.csv', index=False)
df_train.to_csv(PATH + bencana + 'corpus/dataset/df_train_unpreprocessed.csv', index=False)

In [248]:
for x in range(0, old_bencana.shape[0]):
    text = preprocessing(old_bencana.iloc[x, -2])
    old_bencana.iloc[x, -2] = (' '.join(text))

for x in range(0, old_bencana.shape[0]):
    text = preprocessing(old_bencana.iloc[x, -4])
    old_bencana.iloc[x, -4] = (' '.join(text)) 
old_bencana.head()

title  \
9646  imbas banjir semarang tujuan jakarta antre men...   
648     titik banjir tangerang puri bintaro indah bulak   
47        jago merah menyala balikpapan hangus terbakar   
1784  banjir tanah longsor berulang menggenangi nasi...   
585     banjir natuna pemprov kepri bantu juta logistik   

                              date  \
9646  Sabtu, 31 Des 2022 23:39 WIB   
648   Jumat, 02 Des 2022 09:04 WIB   
47    Senin, 28 Nov 2022 13:41 WIB   
1784   Rabu, 07 Des 2022 11:50 WIB   
585   Sabtu, 17 Des 2022 09:15 WIB   

                                                   desc              source  
9646  imbas banjir menggenangi semarang jawa stasiun...  www.tribunnews.com  
648   banjir menggenangi tangerang provinsi banten b...      www.kompas.com  
47    api mendadak muncul karang jati balikpapan bal...      www.kompas.com  
1784  badan penanggulangan bpbd kulon progo istimewa...      www.kompas.com  
585   banjir bandang melanda kabupatan natuna pulau ...      www.kompas.com

In [25]:
desc_text_train = []
desc_text_test = []

for x in range(0, df_train.shape[0]):
  desc_text_train.append(df_train.iloc[x, -2])

for x in range(0, df_test.shape[0]):
  desc_text_test.append(df_test.iloc[x, -2])

# print(df_test.info())
print("Panjang Dokumen Test : ", len(desc_text_test))

print ('-'*90)

# print(df_train.info())
print("Panjang Dokumen Train : ", len(desc_text_train))

In [27]:
# Simpan teks asli dokumen
joblib.dump(desc_text_test, PATH + bencana + "corpus/model/desc_text_test.pkl")
joblib.dump(desc_text_train, PATH + bencana + "corpus/model/desc_text_train_new.pkl") #INI

# Simpan dataframe hasil text processing sebelum TF-IDF Vectorizer
old_bencana.to_csv(PATH + bencana + 'corpus/dataset/df_total_new.csv', index=False) #INI
df_test.to_csv(PATH + bencana + 'corpus/dataset/df_test.csv', index=False)
df_train.to_csv(PATH + bencana + 'corpus/dataset/df_train.csv', index=False)

In [28]:
# Fit transform menggunakan TF-IDF Vectorizer
tfidf_vectorizer = TfidfVectorizer()
tfidf_test_matrix = tfidf_vectorizer.fit_transform(desc_text_test)
tfidf_train_matrix = tfidf_vectorizer.fit_transform(desc_text_train)

print('tfidf_test_matrix')
print(tfidf_test_matrix.shape)
print('tfidf_train_matrix')
print(tfidf_train_matrix.shape)

tfidf_test_matrix
(278, 9398)
tfidf_train_matrix
(2495, 29277)


In [29]:
joblib.dump(tfidf_vectorizer, PATH + bencana + "corpus/vectorizer/vectorizer_new.pkl") #INI
joblib.dump(tfidf_test_matrix, PATH + bencana + "corpus/matrix/tfidf_test.pkl")
joblib.dump(tfidf_train_matrix, PATH + bencana + "corpus/matrix/tfidf_train_new.pkl") #INI

['D:/Repository/PetaKabar/what/bencana/corpus/matrix/tfidf_train_new.pkl']

## Pencarian

In [93]:
df_total = pd.read_csv(PATH + bencana + 'corpus/dataset/df_total_new.csv')
df_total = df_total[pd.notnull(df_total['desc'])]
print(df_total.info())
print ('-'*90)

document_text_train= joblib.load(PATH + bencana + 'corpus/model/desc_text_train_new.pkl')
document_text_test= joblib.load(PATH + bencana + 'corpus/model/desc_text_test.pkl')
print(len(document_text_test))
print(len(document_text_train))

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2773 entries, 0 to 2772
Data columns (total 4 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   title   2773 non-null   object
 1   date    2773 non-null   object
 2   desc    2773 non-null   object
 3   source  2773 non-null   object
dtypes: object(4)
memory usage: 86.8+ KB
None
------------------------------------------------------------------------------------------
278
2495


In [94]:
kueri='gempa'
kueri=preprocessing(kueri)
kueri= [" ".join (kueri)]
print (kueri)

tfidf_matrix =joblib.load(PATH + bencana + "corpus/matrix/tfidf_train_new.pkl" )
tfidf_vectorizer = joblib.load(PATH + bencana + "corpus/vectorizer/vectorizer_new.pkl" ) 
query_vec= tfidf_vectorizer.transform(kueri)
results=cosine_similarity(tfidf_matrix, query_vec).reshape((-1))
#print (results)
print("\n======================\n")
print("Top 10 most similar documents in corpus:")

j = 1

for i in results.argsort()[-10:][::-1]:
    print("No ID Dokumen  : ", i)
    print("Tanggal        : ", df_total.iloc[i,1])
    print("Isi berita     : ", df_total.iloc[i,2])
    print("(Score: %.4f) " % results[i])

['gempa']


Top 10 most similar documents in corpus:
No ID Dokumen  :  9
Tanggal        :  Minggu, 25 Des 2022 20:20 WIB
Isi berita     :  100 kapal pinisi kapal wisata jenis labuan bajo berlindung gugusan pulau menghindari gelombang melanda perairan labuan bajo pantauan lokasi minggu 25 12 2022 sore kapal kapal wisata menumpuk perairan sisi utara hotel meruorah labuan bajo kapal kapal wisata terlindung pulau depannya kepala kantor kesyahbandaran otoritas pelabuhan ksop kelas iii labuan bajo hasan sadili membenarkan kapal kapal wisata berlindung cuaca buruk melanda labuan bajo hasan sadili membenarkan kapal kapal wisata berlindung pulau cuaca buruk kapal kapal wisata diaz berlindung pulau sabtu 24 12 2022 hari cuaca buruk melanda labuan bajo hujan lebat disertai angin kencang gelombang perairan labuan bajo prakiraan badan meteorologi klimatologi geofisika bmkg besok cuaca buruk angkutan sungai danau penyeberangan asdp indonesia ferry cabang labuan bajo manggarai barat nusa tenggara tim

## YAKE TFIDF BERT

In [30]:
import gensim
# import pandas as pd
import csv
from yake import KeywordExtractor
import math
from operator import itemgetter
from nltk import tokenize
from nltk.tokenize import word_tokenize
kw_extractor = KeyBERT('distilbert-base-nli-mean-tokens')
embedder = SentenceTransformer('xlm-r-distilroberta-base-paraphrase-v1')
import scipy.sparse


In [31]:
df_total = pd.read_csv(PATH + bencana + 'corpus/dataset/df_total_new.csv')
df_total = df_total[pd.notnull(df_total['desc'])]
print(df_total.info())
print ('-'*90)
document_text= joblib.load(PATH + bencana + 'corpus/model/desc_text_train_new.pkl')
print(len(document_text))

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2773 entries, 0 to 2772
Data columns (total 4 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   title   2773 non-null   object
 1   date    2773 non-null   object
 2   desc    2773 non-null   object
 3   source  2773 non-null   object
dtypes: object(4)
memory usage: 86.8+ KB
None
------------------------------------------------------------------------------------------
2495


In [32]:
df_test = pd.read_csv(PATH + bencana + 'corpus/dataset/df_test.csv')
df_test = df_test[pd.notnull(df_test['desc'])]
print(df_test.info())
print ('-'*90)
document_text_test= joblib.load(PATH + bencana + 'corpus/model/desc_text_test.pkl')
print(len(document_text_test))

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 278 entries, 0 to 277
Data columns (total 4 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   title   278 non-null    object
 1   date    278 non-null    object
 2   desc    278 non-null    object
 3   source  278 non-null    object
dtypes: object(4)
memory usage: 8.8+ KB
None
------------------------------------------------------------------------------------------
278


In [33]:
df_train = pd.read_csv(PATH + bencana + 'corpus/dataset/df_train.csv')
df_train = df_train[pd.notnull(df_train['desc'])]
print(df_train.info())
print ('-'*90)
document_text_train= joblib.load(PATH + bencana + 'corpus/model/desc_text_train_new.pkl')
print(len(document_text_train))

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2495 entries, 0 to 2494
Data columns (total 4 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   title   2495 non-null   object
 1   date    2495 non-null   object
 2   desc    2495 non-null   object
 3   source  2495 non-null   object
dtypes: object(4)
memory usage: 78.1+ KB
None
------------------------------------------------------------------------------------------
2495


In [35]:
paths = PATH + bencana + 'idwiki_word2vec_300.model'

# maximal value dari cosine similarity dalah 1

def similar(kata, proseske):
    most_similars = id_w2v.wv.most_similar(kata)
    arr = []

    # proses masukin ke csv
    f = open(PATH + bencana + 'bow_what_hapus.csv', 'a', encoding='UTF8', newline='')

    # f1 = open(PATH + bencana + "less_or_equal_62.csv", "a", encoding='UTF8', newline='')
    # f2 = open(PATH + bencana + "more_62.csv", "a", encoding='UTF8', newline='')

    for x in range(len(most_similars)):
        words = most_similars[x][0]
        similarity = most_similars[x][1]
        # print(words)
        # print(similarity)
        result = [words, similarity]
        # if similarity > maxDistance:
        #     maxDistance = similarity
        # elif similarity < minDistance:
        #     minDistance = similarity

        # if round(similarity, 2) <= 0.62:
        #     f1writer = csv.writer(f1)
        #     f1writer.writerow(result)
        # else:
        #     f2writer = csv.writer(f2)
        #     f2writer.writerow(result)
        
        arr.append((words, similarity))

    writer = csv.writer(f)
    writer.writerow([str(proseske), kata, most_similars])

    f.close()
    # f1.close()
    # f2.close()

    return(arr)


def tree(arr, proseske):
    hasil = []
    for x in range(len(arr)):
        for y in range(10):
            words = arr[x][y][0]
            similarity = arr[x][y][1]
            # if round(similarity, 2) <= 0.62:
            tes = similar(words, proseske)
            hasil.append(tes)
    return(hasil)

id_w2v = gensim.models.word2vec.Word2Vec.load(paths)

f = open(PATH + bencana + 'bow_what_hapus.csv', 'w', encoding='UTF8')
writer = csv.writer(f)
writer.writerow(['tingkat setelah parent', 'parent', 'similarity'])

# f1 = open(PATH + bencana + "less_or_equal_62.csv", "w", encoding='UTF8', newline='')
# writer = csv.writer(f1)
# writer.writerow(['Word', 'Similarity'])
# f1.close()

# f2 = open(PATH + bencana + "more_62.csv", "w", encoding='UTF8', newline='')
# writer = csv.writer(f2)
# writer.writerow(['Word', 'Similarity'])
# f2.close()

f.close()
x = 0

tes = similar('bencana', x)
data = []
data.append(tes)

while(True):
    if(x <= 3):
        x = x+1
        coba = tree(data, x)
        data = coba
        continue
    else:
        # print('maxDistance ' + str(maxDistance) + '\n')
        # print('minDistance ' + str(minDistance) + '\n')
        break

## Main Course

In [56]:
# Load bow dataset

#jika dijalankan ulang, jangan lupa untuk men-deduplikasi, menghapus kosakata selain indonesia, dan Rencana Induk Perencanaan Bencana
df_bow_what = pd.read_csv(PATH + bencana + "bow/bow_what_old.csv")
df_bow_what.head()

tingkat setelah parent      parent  \
0                     2.0      banjir   
1                     2.0   kelaparan   
2                     2.0       gempa   
3                     2.0  kekeringan   
4                     2.0   kebakaran   

                                          similarity  
0  [('longsor', 0.7020419836044312), ('kekeringan...  
1  [('wabah', 0.7254995703697205), ('epidemi', 0....  
2  [('tsunami', 0.6986302137374878), ('letusan', ...  
3  [('kelaparan', 0.6980215907096863), ('erosi', ...  
4  [('ledakan', 0.6575784087181091), ('pemadaman'...

In [57]:
# Ambil parent dari bow
bow_list_what = []

for i in range(0, df_bow_what.shape[0]):
  bow_list_what.append(df_bow_what.iloc[i, 1])

print("What ", bow_list_what[0])

print({
  'What': len(bow_list_what),
})

What  banjir
{'What': 268}


In [38]:
# Cari dok pertama Use data train
def cari_dokpertama(kueriAsli: str):
    kueriPre = preprocessing(kueriAsli)
    kueriPre = " ".join(kueriPre)
    hasilSearch = []
    
    tfidf_matrix = joblib.load(PATH + bencana + 'corpus/matrix/tfidf_train_new.pkl')
    tfidf_vectorizer = joblib.load(PATH + bencana + 'corpus/vectorizer/vectorizer_new.pkl')

    query_vec = tfidf_vectorizer.transform([kueriPre])
    results = cosine_similarity(tfidf_matrix, query_vec).reshape((-1))
    for i in results.argsort()[-5:][::-1]:
        hasilSearch.append(df_total.iloc[i,-2])
    hasilSearch=". ".join(hasilSearch)
    
    return hasilSearch

In [39]:
##Keywords Extraction with YAKE
def keyword_yake(hasilSearch: str):
    keywordYake=[]

    k_extractor = KeywordExtractor(lan="id", n=1, top=50)
    k_extractor2 = KeywordExtractor(lan="id", n=2, top=50)
    keywords = k_extractor.extract_keywords(text=hasilSearch)
    # keywords = k_extractor2.extract_keywords(text=hasilSearch)
    keywords.extend(k_extractor2.extract_keywords(text=hasilSearch))
    keywordYake = [x for x, y in keywords]
    # keywordYake.append(keywords)
    print('*'*120)
    print('*'*120)
    print("Keyword yake")
    print(keywordYake)
    print('*'*120)
    print('*'*120)
    
    return keywordYake

In [40]:
#Keywords Extraction with TFIDF
def keyword_tfidf(hasilSearch: str):

    keywordtfidf=[]
    keywordtfidf2=[]

    total_words = re.sub(r'[^\w]', ' ', hasilSearch)
    total_words = total_words.lower().split()
    #print (total_words)
    total_word_length = len(total_words)
    total_sentences = tokenize.sent_tokenize(hasilSearch)
    total_sent_len = len(total_sentences)

    tf_score = {}
    for each_word in total_words:
        #print (each_word)
        each_word = each_word.replace('.','')
        if (each_word in excluded_words) or (each_word not in NLTK_StopWords):
            if each_word in tf_score:
                tf_score[each_word] += 1
            else:
                tf_score[each_word] = 1

    # Dividing by total_word_length for each dictionary element
    tf_score.update((x, y/int(total_word_length)) for x, y in tf_score.items())
    #print(tf_score)
    def check_sent(word, sentences): 
        final = [all([w in x for w in word]) for x in sentences] 
        sent_len = [sentences[i] for i in range(0, len(final)) if final[i]]
        return int(len(sent_len))

    idf_score = {}
    for each_word in total_words:
        #print (each_word)
        each_word = each_word.replace('.','')
        if (each_word in excluded_words) or (each_word not in NLTK_StopWords):
            if each_word in idf_score:
                idf_score[each_word] = check_sent(each_word, total_sentences)
            else:
                idf_score[each_word] = 1

    # Performing a log and divide
    idf_score.update((x, math.log(int(total_sent_len)/y)) for x, y in idf_score.items())

    #print(idf_score)
    tf_idf_score = {key: tf_score[key] * idf_score.get(key, 0) for key in tf_score.keys()}
    #print(tf_idf_score)
    def get_top_n(dict_elem, n):
        result = dict(sorted(dict_elem.items(), key = itemgetter(1), reverse = True)[:n]) 
        hasil =list(result.keys())
        #print(list(result.keys()))        
        return hasil
    #print(get_top_n(tf_idf_score, 25))
    #print(len(get_top_n(tf_idf_score, 1)))
    keywordtfidf.append(get_top_n(tf_idf_score, 25))
    for i in range(len(keywordtfidf)):
        #print (i)
        totalKw=0
        totalKw=len(keywordtfidf[i])
        for j in range(totalKw):
            #print (j)
            keywordtfidf2.append(keywordtfidf[i][j])
    
    print('*'*120)
    print('*'*120)
    print("Keyword TFIDF")
    print (keywordtfidf2)
    print('*'*120)
    print('*'*120)

    return keywordtfidf2

In [41]:
#Keywords Extraction with BERT
def keyword_bert(hasilSearch: str):

    keywordbert=[]

    #for j in range(len(array_text)):
    keyword1 = kw_extractor.extract_keywords(hasilSearch, top_n=50, keyphrase_ngram_range=(1, 1))
    keyword2 = kw_extractor.extract_keywords(hasilSearch, top_n=50, keyphrase_ngram_range=(1, 2))

    #print("Keywords of article\n", keywords)
    for i in range (0,len (keyword1)):
        keywordbert.append(keyword1[i][0])
        keywordbert.append(keyword2[i][0])
    
    print('*'*120)
    print('*'*120)
    print("Keyword Bert")
    print (keywordbert)
    print('*'*120)
    print('*'*120)
    
    return keywordbert

In [42]:
# Borda rangking
def rangking (keywordGabung, kueriAsli: str):
    kandidatFinalCek=[]
    kandidatFinalFix=[]
    
    for i in keywordGabung:
        if (i not in kandidatFinalCek and i!=0):
            kandidatFinalCek.append(i)
    queries=[kueriAsli]
    query_embeddings = embedder.encode(queries)
    corpus_embeddings4 = embedder.encode(kandidatFinalCek)
    # Find the closest 5 sentences of the corpus for each query sentence based on cosine similarity
    closest_n = 80
    for query, query_embedding in zip(queries, query_embeddings):
        distances = scipy.spatial.distance.cdist([query_embedding], corpus_embeddings4, 'cosine')[0]
        results = zip(range(len(distances)), distances)
        results = sorted(results, key=lambda x: x[1])
        for idx, distance in results[0:closest_n]:
            kandidatFinalFix.append(kandidatFinalCek[idx])

    print('*'*120)
    print('*'*120)
    print ('Kandidat Final Fix Rank: ', kandidatFinalFix)
    print('*'*120)
    print('*'*120)

    return kandidatFinalFix

In [43]:
# Keyword bow
def keywordCustomBow(bowList, initialQuery: str):
    cekDuplicate = []
    kandidatFix = []

    for i in bowList:
        if(i not in cekDuplicate and i!=0):
            cekDuplicate.append(i)

    queries=[initialQuery]
    query_embeddings = embedder.encode(queries)
    corpus_embeddings4 = embedder.encode(cekDuplicate)
    
    # Find the closest 5 sentences of the corpus for each query sentence based on cosine similarity
    closest_n = 500
    for query, query_embedding in zip(queries, query_embeddings):
        distances = scipy.spatial.distance.cdist([query_embedding], corpus_embeddings4, 'cosine')[0]
        results = zip(range(len(distances)), distances)
        results = sorted(results, key=lambda x: x[1])
        for idx, distance in results[0:closest_n]:
            kandidatFix.append(cekDuplicate[idx])
    
    print('*'*120)
    print('*'*120)
    print("Keyword BoW")
    print ('Kandidat BoW: ', kandidatFix)
    print('*'*120)
    print('*'*120)

    return kandidatFix

In [58]:
# Creating query for what, when, where, who
what_initial_query = "bencana apa yang terjadi dalam berita"

what_query = preprocessing(what_initial_query)
what_query = " ".join(what_query)
print (what_query)

bencana berita


In [45]:
# Prepare w data
def prepareWData(initial_query: str, bow_list):
    hasilkandidat = []
    keywordGabung = []
    qeGabungan = []
    kueriFix = []

    hasilSearch     = cari_dokpertama(initial_query)
    # (ini yake + tfidf + bert) = qe statistik
    keywordYake     = keyword_yake(hasilSearch) # 20
    keywordtfidf2   = keyword_tfidf(hasilSearch) # 20
    keywordbert     = keyword_bert(hasilSearch) # 20
    # ini qe bow
    keywordBoW      = keywordCustomBow(bow_list, initial_query)

    for keyword1 in keywordYake:
        keywordGabung.append(keyword1)
    for keyword2 in keywordtfidf2:
        keywordGabung.append(keyword2)
    for keyword3 in keywordbert:
        keywordGabung.append(keyword3)  

    # hasilrank = qe statistik
    hasilrank = rangking(keywordGabung, initial_query)
    
    for word1 in hasilrank:
        kueriFix.append(word1)

    for word2 in keywordBoW:
        kueriFix.append(word2)

    for word3 in kueriFix:
        hasilkandidat.append(word3)

    kueriFix = [preprocessing(i) for i in kueriFix]
    
    qeGabunganDelimiter = []

    for word4 in kueriFix:
        for subWord in word4:
            qeGabungan.append(subWord)
            qeGabunganDelimiter.append(subWord)

    qeGabunganDelimiter = list(dict.fromkeys(qeGabunganDelimiter))
    qeGabungan = list(dict.fromkeys(qeGabungan))

    # (hasil ranking + bow) = kandidat final
    qeGabungan = [" ".join(qeGabungan)]

    print('*'*120)
    qeStatistik = hasilrank
    qeBoW = keywordBoW

    return [qeGabungan, qeStatistik, qeBoW, qeGabunganDelimiter]

In [59]:
whatResultList = prepareWData(what_query, bow_list_what)
print("What")
print()
qeGabunganWhat = whatResultList[0]
qeStatistikWhat = whatResultList[1]
qeBoWWhat = whatResultList[2]
qeGabunganDelimiterWhat = whatResultList[3]

************************************************************************************************************************
************************************************************************************************************************
Keyword yake
['sungai', 'mencapai', 'kebakaran', 'hutan', 'ciujung', 'air', 'lebak', 'febby', 'siaga', 'longsor', 'tma', 'hujan', 'warga', 'deras', 'debit', 'hari', 'rumah', 'rusak', 'edy', 'bencana', 'sentimeter', 'ciberang', 'sumut', 'tanah', 'duddy', 'pupr', 'jembatan', 'rahmayadi', 'berstatus', 'kepala', 'status', 'kecamatan', 'jalan', 'tercatat', 'cuaca', 'aman', 'relawan', 'daerah', 'upt', 'dinas', 'pembangunan', 'kehutanan', 'dampri', 'kabupaten', 'video', 'lokasi', 'bantaran', 'wilayah', 'berat', 'april', 'ciberang ciujung', 'tma mencapai', 'kebakaran hutan', 'sungai ciujung', 'ciujung lebak', 'sungai', 'sungai ciberang', 'lebak febby', 'berstatus siaga', 'tercatat tma', 'sentimeter aman', 'aman debit', 'debit air', 'febby cuaca', 'ciujung 

In [60]:
print(qeGabunganDelimiterWhat)
print(qeGabunganWhat)
print(qeBoWWhat)
print(qeStatistikWhat)

['bencana', 'kebencanaan', 'penanggulangan', 'febby', 'cuaca', 'hulu', 'ekstrem', 'rusak', 'meluap', 'kehutanan', 'kedungsumber', 'ciberang', 'dampri', 'menghancurkan', 'kesiapsiagaan', 'mengguyur', 'siaga', 'kebakaran', 'sindangkerta', 'pengecekan', 'kesatuan', 'terpantau', 'pembangunan', 'keterangan', 'gununghalu', 'langganan', 'pratama', 'menimbun', 'deras', 'ciujung', 'wilayah', 'mengakibatkan', 'bantaran', 'pemukiman', 'tma', 'pepohonan', 'jati', 'temayang', 'lingkungan', 'manusia', 'hutan', 'mengimbau', 'lebak', 'kabupaten', 'pengendalian', 'daerah', 'diguyur', 'banten', 'kecamatan', 'kemiringannya', 'hujan', 'hari', 'status', 'tanah', 'upt', 'menyebabkan', 'menyiagakan', 'wib', 'sambungnya', 'warga', 'debit', 'airnya', 'pencegahan', 'mengkhawatirkan', 'jalan', 'menetapkan', 'dinas', 'menargetkan', 'pengelolaan', 'air', 'tercatat', 'sekitaran', 'perkecambahan', 'letusan', 'benturan', 'gesekan', 'badai', 'gempabumi', 'kelaparan', 'rawan', 'penghujan', 'banjir', 'letusannya', 'pela

In [65]:
# df_test_unpreprocessed = pd.read_csv(PATH + bencana + "corpus/df_test_unprerocessed.csv")

# hasil_test_what = []

# for i in range(0, len(df_test_unpreprocessed)):
#     hasilWhat = []

#     for key in qeGabunganDelimiterWhat:
#         cariW = re.findall(key, df_test_unpreprocessed['desc'].iloc[i])

#         if cariW:
#             hasilWhat.append(key)
#     hasil_test_what.append(hasilWhat)

# hasil_test_what

df_test = pd.read_csv(PATH + bencana + "df_test_results.csv")

hasil_test_what = []

for i in range(0, len(df_test)):
    hasilWhat = []

    for key in qeGabunganDelimiterWhat:
        cariW = re.findall(key, df_test['desc'].iloc[i])

        if cariW:
            hasilWhat.append(key)
    hasil_test_what.append(hasilWhat)

hasil_test_what

[['bencana',
  'wilayah',
  'menyebabkan',
  'air',
  'banjir',
  'genangan',
  'menggenangi'],
 ['hulu', 'kebakaran', 'keterangan', 'warga', 'terbakar'],
 ['bencana',
  'cuaca',
  'ekstrem',
  'rusak',
  'daerah',
  'kecamatan',
  'hari',
  'warga',
  'tercatat',
  'rawan',
  'banjir',
  'diterjang',
  'longsor',
  'kencang',
  'angin'],
 ['kebakaran', 'hujan', 'warga', 'nyambar', 'petir', 'terbakar', 'angin'],
 ['bencana',
  'cuaca',
  'ekstrem',
  'mengguyur',
  'deras',
  'wilayah',
  'hujan',
  'hari',
  'tanah',
  'jalan',
  'banjir',
  'genangan',
  'kilat',
  'meteor',
  'petir',
  'longsor',
  'kencang',
  'angin'],
 ['bencana',
  'kebakaran',
  'keterangan',
  'manusia',
  'daerah',
  'hujan',
  'tanah',
  'jalan',
  'banjir',
  'erupsi',
  'gempa',
  'tertimpa',
  'bumi',
  'getaran',
  'terjal',
  'longsor',
  'kencang',
  'angin'],
 ['wilayah', 'air', 'banjir'],
 ['terpantau',
  'warga',
  'debit',
  'jalan',
  'air',
  'banjir',
  'kemacetan',
  'bahaya'],
 ['meluap',
  '

In [67]:
# df_test_unpreprocessed['qe_what_old']=hasil_test_what
# df_test_unpreprocessed

df_test['qe_what_new']=hasil_test_what

df_test['tp_old'] = 0
df_test['tn_old'] = 0
df_test['tp_new'] = 0
df_test['tn_new'] = 0

df_test


title  \
0    BPBD Waspadai Gelombang Pasang Air Laut di Pes...   
1    Bar Bekas Holywings di Tanjung Duren Terbakar,...   
2    Angin Kencang Terjang Permukiman di Sidrap, 35...   
3    Kondisi Terkini 52 Rumah di Manggarai Hangus T...   
4    BMKG Rilis Peringatan Dini, Hujan Deras dan An...   
..                                                 ...   
273  Geolog UPN soal Dentuman Misterius di Gunungki...   
274  Mangsa Ayam, Piton 2,5 Meter 'Ditaklukan' Petu...   
275  Jokowi Resmikan Bendungan Ciawi dan Sukamahi, ...   
276  Cerita Siswa Terdampak Rob di Bonang Demak, ke...   
277  Ibu dan Anak Korban Banjir Bandang di Tuban Di...   

                              date  \
0      Rabu, 21 Des 2022 14:30 WIB   
1     Senin, 05 Des 2022 20:19 WIB   
2    Selasa, 03 Jan 2023 19:43 WIB   
3    Minggu, 18 Des 2022 11:42 WIB   
4     Jumat, 09 Des 2022 13:44 WIB   
..                             ...   
273   Jumat, 23 Des 2022 15:30 WIB   
274   Kamis, 22 Des 2022 22:31 WIB   
275   Jumat, 23 Des 2022 10:00 WIB   
276  Selasa, 13 Des 2022 10:23 WIB   
277    Rabu, 21 Des 2022 23:33 WIB   

                                                  desc          source  \
0    \-\r\n\r\nBPBD Lamongan mewaspadai pasang air ...   www.detik.com   
1    \- Helen's Bar yang dahulu bernama Holywings T...  www.kompas.com   
2    \-\r\n\r\n35 rumah di Kabupaten Sidrap, Sulawe...   www.detik.com   
3    \-\r\n\r\nSebanyak 52 rumah dilanda kebakaran ...   www.detik.com   
4    \- Badan Meteorologi, Klimatologi dan Geofisik...  www.kompas.com   
..                                                 ...             ...   
273  \-\r\n\r\nSuara dentuman misterius terdengar d...   www.detik.com   
274  \-\r\n\r\nKampung Babakanbaru RT 03/06 Desa Pa...   www.detik.com   
275  Presiden Joko Widodo meresmikan Bendungan Ciaw...  www.kompas.com   
276  \-\r\n\r\nBanjir rob yang terjadi di Kecamatan...   www.detik.com   
277  \-\r\n\r\nIbu dan anak yang hilang saat tersap...   www.detik.com   

                                           qe_what_old  \
0    ['bencana', 'banjir', 'desa', 'pesisir', 'pung...   
1    ['kebakaran', 'akibat', 'mengerahkan', 'warga'...   
2    ['bencana', 'cuaca', 'banjir', 'kencang', 'kec...   
3    ['kebakaran', 'bantuan', 'mengungsi', 'jam', '...   
4    ['bencana', 'cuaca', 'banjir', 'meteorologi', ...   
..                                                 ...   
273  ['wilayah', 'gempa', 'runtuh', 'terkikis', 'fe...   
274  ['kebakaran', 'wilayah', 'lokasi', 'warga', 'd...   
275                   ['banjir', 'terdampak', 'waduk']   
276  ['banjir', 'wilayah', 'kabupaten', 'hari', 'lo...   
277  ['banjir', 'lokasi', 'jalan', 'musibah', 'keja...   

                                           qe_what_new  tp_old  tn_old  \
0    [bencana, wilayah, menyebabkan, air, banjir, g...       0       0   
1       [hulu, kebakaran, keterangan, warga, terbakar]       0       0   
2    [bencana, cuaca, ekstrem, rusak, daerah, kecam...       0       0   
3    [kebakaran, hujan, warga, nyambar, petir, terb...       0       0   
4    [bencana, cuaca, ekstrem, mengguyur, deras, wi...       0       0   
..                                                 ...     ...     ...   
273  [wilayah, tanah, menyebabkan, air, gempa, bumi...       0       0   
274  [kebakaran, wilayah, pemukiman, warga, kelapar...       0       0   
275     [pembangunan, langganan, air, banjir, tanggul]       0       0   
276  [wilayah, kabupaten, hari, tanah, sambungnya, ...       0       0   
277  [jalan, banjir, tersapu, terseret, tersangkut,...       0       0   

     tp_new  tn_new  
0         0       0  
1         0       0  
2         0       0  
3         0       0  
4         0       0  
..      ...     ...  
273       0       0  
274       0       0  
275       0       0  
276       0       0  
277       0       0  

[278 rows x 10 columns]

In [78]:
# df_test_unpreprocessed.to_csv(PATH + bencana + "df_test_results.csv" , index = None, header=True)
df_test = df_test.drop(['source'], axis=1)
df_test.to_csv(PATH + bencana + "df_test_results_appended.csv" , index = None, header=True)

## LDA

In [251]:
import gensim
from gensim import corpora
from collections import Counter
import pyLDAvis.gensim
import pickle 
import pyLDAvis
from nltk.tokenize import word_tokenize 
from nltk.probability import FreqDist

def remove_number(text):
    return  re.sub(r"\d+", "", text)

In [252]:
new_bencana = old_bencana[['title', 'desc']]
new_bencana['desc'] = new_bencana['desc'].apply(remove_number)
new_bencana['desc'] = new_bencana['desc'].apply(word_tokenize)
new_bencana['desc'] = [[token for token in doc if len(token) > 2] for doc in new_bencana['desc']]
new_bencana['title'] = new_bencana['title'].apply(remove_number)
new_bencana['title'] = new_bencana['title'].apply(word_tokenize)
new_bencana['title'] = [[token for token in doc if len(token) > 2] for doc in new_bencana['title']]
new_bencana['fdist'] = new_bencana['desc'].apply(FreqDist)

print(len(new_bencana))
print(new_bencana.head(2))

print('Frequency Tokens : \n') 
print(new_bencana['fdist'].head().apply(lambda x : x.most_common()))

2773
                                                  title  \
9646  [imbas, banjir, semarang, tujuan, jakarta, ant...   
648   [titik, banjir, tangerang, puri, bintaro, inda...   

                                                   desc  \
9646  [imbas, banjir, menggenangi, semarang, jawa, s...   
648   [banjir, menggenangi, tangerang, provinsi, ban...   

                                                  fdist  
9646  {'imbas': 1, 'banjir': 1, 'menggenangi': 1, 's...  
648   {'banjir': 9, 'menggenangi': 2, 'tangerang': 4...  
Frequency Tokens : 

9646    [(stasiun, 8), (semarang, 6), (kereta, 6), (ap...
648     [(banjir, 9), (pondok, 9), (sentimeter, 7), (s...
47      [(kebakaran, 8), (api, 3), (balikpapan, 3), (r...
1784    [(banjir, 13), (sungai, 7), (hujan, 4), (goron...
585     [(banjir, 7), (ansar, 7), (terdampak, 6), (bun...
Name: fdist, dtype: object


In [253]:
from gensim.models import Phrases
bigram = Phrases(new_bencana['desc'], min_count=20)
for idx in range(len(new_bencana['desc'])):
    for token in bigram[new_bencana['desc'].iloc[idx]]:
        if '_' in token:
            # Token is a bigram, add to document.
            new_bencana['desc'].iloc[idx].append(token)
            word1, word2 = token.split("_")
            if word1 not in ('kebakaran', 'banjir', 'gempa', 'longsor', 'banjir', 'angin'):
                new_bencana['desc'].iloc[idx].remove(word1)
            if word2 not in ('kebakaran', 'banjir', 'gempa', 'longsor', 'banjir', 'angin'):
                new_bencana['desc'].iloc[idx].remove(word2)
            # print(token)

In [491]:
dictionary = corpora.Dictionary(new_bencana['desc'])
dictionary.filter_extremes(no_below=30, no_above=0.5)
print(dictionary)

corpus = [dictionary.doc2bow(berita) for berita in new_bencana['desc']]

Dictionary<1656 unique tokens: ['api', 'arah', 'banjir', 'banjir_menggenangi', 'depannya']...>


In [492]:
# Creating the object for LDA model using gensim library
Lda = gensim.models.ldamodel.LdaModel

total_topics = 4 # jumlah topik yang akan di extract
number_words = 30 # jumlah kata per topik

In [493]:
import os
from gensim.test.utils import datapath
the_path = PATH + bencana + "model/lda_model" + "_" + str(total_topics) + "_" + str(number_words)
if not os.path.exists(the_path):
    os.mkdir(the_path)
temp_file = datapath(the_path + "/lda_model")
#if new
# lda_model = Lda(corpus, num_topics=total_topics, id2word=dictionary, passes=50, random_state=1)
# lda_model.save(temp_file)
# load
from gensim import models
lda_model = models.ldamodel.LdaModel.load(temp_file)

lda_model.show_topics(num_topics=total_topics, num_words=number_words)

[(0,
  '0.029*"kebakaran" + 0.018*"longsor" + 0.009*"terbakar" + 0.009*"ditemukan" + 0.009*"api" + 0.007*"mobil" + 0.007*"pencarian" + 0.007*"peristiwa" + 0.006*"bangunan" + 0.006*"damkar" + 0.006*"polisi" + 0.005*"diduga" + 0.005*"tanah" + 0.005*"pasar" + 0.005*"tim" + 0.005*"jakarta" + 0.005*"meninggal" + 0.004*"unit" + 0.004*"rumahnya" + 0.004*"saksi" + 0.004*"berhasil" + 0.004*"pohon" + 0.004*"pria" + 0.004*"personel" + 0.004*"listrik" + 0.004*"jenazah" + 0.004*"pemadam_kebakaran" + 0.004*"sampah" + 0.004*"mengaku" + 0.004*"pelaku"'),
 (1,
  '0.088*"banjir" + 0.016*"sungai" + 0.016*"jakarta" + 0.014*"semarang" + 0.009*"genangan" + 0.008*"bpbd" + 0.008*"jembatan" + 0.008*"titik" + 0.007*"ketinggian" + 0.007*"surut" + 0.006*"bandung" + 0.006*"terendam_banjir" + 0.006*"terdampak" + 0.006*"terdampak_banjir" + 0.006*"kali" + 0.006*"banjir_bandang" + 0.006*"hujan" + 0.006*"akses" + 0.005*"mengungsi" + 0.005*"pembangunan" + 0.005*"dki_jakarta" + 0.005*"jawa" + 0.005*"kemarin" + 0.005*"rob

In [494]:
# Word Count of Topic Keywords

from collections import Counter
topics = lda_model.show_topics(formatted=False, num_topics=total_topics, num_words=number_words)
# topic = lda_model.show_topics(num_topics=total_topics, num_words=number_words)
# print((topics[0]))
# print((topic[0]))
data_flat = [w for w_list in new_bencana['desc'] for w in w_list]
counter = Counter(data_flat)

out = []
for i, topic in topics:
    for word, weight in topic:
        out.append([word, i , weight, counter[word]])

df_imp_wcount = pd.DataFrame(out, columns=['word', 'id', 'importance', 'word_count']) 
print(df_imp_wcount)

          word  id  importance  word_count
0    kebakaran   0    0.029152        1595
1      longsor   0    0.017610        1358
2     terbakar   0    0.008810         435
3    ditemukan   0    0.008799         427
4          api   0    0.008587         509
..         ...  ..         ...         ...
115     wisata   3    0.005074         269
116   lumajang   3    0.005073         176
117      natal   3    0.005014         170
118    tanggal   3    0.005009         248
119   makassar   3    0.004645         463

[120 rows x 4 columns]


In [258]:
def format_topics_sentences(ldamodel=None, corpus=corpus, texts=new_bencana['desc']):
    # Init output
    sent_topics_df = pd.DataFrame()
    # print(len(ldamodel[corpus]))

    dom = []
    perc = []
    keywords = []
    # Get main topic in each document
    for i, row_list in enumerate(ldamodel[corpus]):
        row = row_list[0] if ldamodel.per_word_topics else row_list            
        row = sorted(row, key=lambda x: (x[1]), reverse=True)
        # print(len(row))

        # Get the Dominant topic, Perc Contribution and Keywords for each document
        for j, (topic_num, prop_topic) in enumerate(row):
            if j == 0:  # => dominant topic
                wp = ldamodel.show_topic(topic_num, topn=number_words)
                topic_keywords = ", ".join([word for word, prop in wp])
                dom.append(int(topic_num))
                perc.append(round(prop_topic,4))
                keywords.append(topic_keywords)
                # sent_topics_df = pd.concat([sent_topics_df, pd.DataFrame([pd.Series([int(topic_num), round(prop_topic,4), topic_keywords])])], ignore_index=True)
                # sent_topics_df = sent_topics_df.append(pd.Series([int(topic_num), round(prop_topic,4), topic_keywords]), ignore_index=True)
            else:
                break
    # print(len(sent_topics_df))
    sent_topics_df['Dominant_Topic'] = dom
    sent_topics_df['Perc_Contribution'] = perc
    sent_topics_df['Topic_Keywords'] = keywords
    # sent_topics_df.columns = ['Dominant_Topic', 'Perc_Contribution', 'Topic_Keywords']

    # Add original text to the end of the output
    # sent_topics_df['Texts']= texts
    # print(len(sent_topics_df))
    return(sent_topics_df)

In [495]:
df_topic_sents_keywords = format_topics_sentences(ldamodel=lda_model, corpus=corpus, texts=new_bencana['desc'])
df_topic_sents_keywords['Texts'] = 0
df_topic_sents_keywords['Title'] = 0

In [496]:
df_dominant_topic = df_topic_sents_keywords.reset_index()
# texts = []
for i in range(len(new_bencana['desc'])):
    # print(new_bencana['desc'].iloc[i])
    # texts.append(new_bencana['desc'].iloc[i])
    df_dominant_topic['Texts'].iloc[i] = new_bencana['desc'].iloc[i]
    df_dominant_topic['Title'].iloc[i] = new_bencana['title'].iloc[i]
# df_dominant_topic['Texts'] = texts
df_dominant_topic.columns = ['Document_No', 'Dominant_Topic', 'Topic_Perc_Contrib', 'Keywords', 'Text', 'Title']

# df_topic_sents_keywords['Texts'].isna().value_counts()
df_dominant_topic.head(5)
df_dominant_topic.tail(5)

Document_No  Dominant_Topic  Topic_Perc_Contrib  \
2768         2768               1              0.9957   
2769         2769               1              0.8189   
2770         2770               2              0.9927   
2771         2771               2              0.8773   
2772         2772               0              0.7579   

                                               Keywords  \
2768  banjir, sungai, jakarta, semarang, genangan, b...   
2769  banjir, sungai, jakarta, semarang, genangan, b...   
2770  gempa, gempa_bumi, cianjur, bantuan, bmkg, ban...   
2771  gempa, gempa_bumi, cianjur, bantuan, bmkg, ban...   
2772  kebakaran, longsor, terbakar, ditemukan, api, ...   

                                                   Text  \
2768  [pantai, jawa, pantura, jawa, banjir, perganti...   
2769  [semarang, kaline, banjir, lirik, lagu, berjud...   
2770  [memperbarui, laporan, gempa, mengguncang, gem...   
2771  [gempa, magnitudo, dilaporkan, gempa, puluhan,...   
2772  [mahasiswa, melintasi, banjir, merayakan, acar...   

                                                  Title  
2768  [bpbd, laporkan, jateng, tergenang, banjir, te...  
2769                     [banjir, semarang, dipisahkan]  
2770                [jayapura, rasakan, gempa, susulan]  
2771  [breaking, news, gempa, guncang, jayapura, pap...  
2772  [mahasiswa, semarang, tersengat, listrik, lint...

In [189]:
df_dominant_topic.to_csv(PATH + bencana + 'df_dominant_topic.csv')

In [200]:
pyLDAvis.enable_notebook()

In [194]:
from datetime import datetime
now = datetime.now() # current date and time
date_time = now.strftime("%m-%d-%Y_%H-%M-%S")
print("date and time:",date_time)
LDAvis_html = 'ldavis_prepared_'+ str(total_topics)+"_"+str(number_words)+"_"+str(date_time)
LDAvis_prepared = pyLDAvis.gensim.prepare(lda_model, corpus, dictionary)
with open(PATH + bencana + LDAvis_html, 'wb') as f:
        pickle.dump(LDAvis_prepared, f)

date and time: 06-23-2023_14-30-24


In [195]:
with open(PATH + bencana + LDAvis_html, 'rb') as f:
    LDAvis_prepared = pickle.load(f)

In [196]:
pyLDAvis.save_html(LDAvis_prepared, PATH + bencana + LDAvis_html +'.html')

In [423]:
# df_imp_wcount.sort_values(by=['word_count'], ascending=False)
# df_dominant_topic['Keywords'].iloc[2771]
# lda_model.show_topic(1, topn=15)

In [261]:
lda_what_bencana = []
word_topics = set(df_imp_wcount['word'].values)
for i in range(len(df_dominant_topic)):
    val = []
    for n, key in enumerate(word_topics):
        if key in df_dominant_topic['Text'].iloc[i]:
            val.append(key)
    lda_what_bencana.append(val)

print(lda_what_bencana)

[['jalur', 'genangan', 'api', 'banjir', 'semarang', 'jawa', 'jakarta', 'pasar'], ['kemarin', 'ketinggian', 'genangan', 'surut', 'banjir', 'terendam_banjir', 'terdampak_banjir', 'gunung', 'bpbd', 'mengungsi', 'titik'], ['aktivitas', 'kebakaran', 'rumahnya', 'unit', 'ketinggian', 'api', 'listrik', 'pemadam_kebakaran', 'terbakar', 'bpbd', 'peristiwa', 'sekolah', 'diduga'], ['jembatan', 'kemarin', 'sampah', 'kali', 'ketinggian', 'genangan', 'potensi', 'banjir', 'rusak', 'terendam_banjir', 'pohon', 'pemerintah', 'bpbd', 'longsor', 'sungai'], ['rumahnya', 'unit', 'melanda', 'penanganan', 'laut', 'banjir', 'bantuan', 'banjir_bandang', 'terendam_banjir', 'terdampak', 'terdampak_banjir', 'bpbd', 'mengaku', 'alam', 'sungai', 'titik'], ['jembatan', 'sampah', 'kali', 'jalur', 'genangan', 'surut', 'hujan', 'polisi', 'banjir', 'kendaraan', 'sungai', 'titik'], ['bangunan', 'aktivitas', 'banjir_rob', 'kali', 'ketinggian', 'surut', 'laut', 'rob', 'banjir', 'terendam_banjir', 'terdampak', 'terdampak_ban

In [262]:
lda_title_what = []
word_topics = set(df_imp_wcount['word'].values)
for i in range(len(df_dominant_topic)):
    val = []
    for n, key in enumerate(word_topics):
        if key in df_dominant_topic['Title'].iloc[i]:
            val.append(key)
    lda_title_what.append(val)

print(lda_title_what)

[['banjir', 'semarang', 'jakarta'], ['banjir', 'titik'], ['terbakar'], ['banjir', 'bpbd', 'longsor', 'tanah'], ['banjir'], ['banjir', 'kendaraan'], ['ketinggian', 'rob', 'banjir'], ['garut', 'rusak', 'magnitudo', 'gempa', 'cianjur'], ['magnitudo', 'berpotensi', 'gempa'], [], ['hujan', 'banjir'], ['damkar'], ['damkar', 'terbakar', 'personel'], ['banjir', 'jakarta'], ['hujan', 'gempa', 'cianjur'], ['terbakar', 'pasar'], ['bantuan', 'gempa', 'cianjur'], ['bantuan', 'gempa', 'cianjur'], ['banjir'], ['bantuan', 'gempa', 'cianjur'], ['kebakaran', 'tim', 'pasar'], ['banjir'], ['angin', 'rusak'], ['kebakaran', 'tim', 'pasar'], ['kebakaran', 'damkar', 'mobil'], ['terbakar'], ['terbakar'], ['angin', 'kencang'], ['angin', 'kencang'], ['banjir', 'ditemukan'], ['hujan', 'cuaca', 'potensi', 'angin', 'bmkg', 'kencang'], ['banjir'], ['hujan', 'cuaca', 'angin', 'kencang', 'jakarta'], ['hujan', 'angin', 'kencang', 'jakarta'], ['hujan', 'cuaca', 'angin', 'kencang', 'jakarta'], ['hujan', 'cuaca', 'angin',

In [263]:
for n, word_list in enumerate(lda_title_what):
    val = []
    for word in word_list:
        if word in lda_what_bencana[n]:
            continue
        val.append(word)
    lda_what_bencana[n].extend(val)
    # if val:
    #     print(n)
    #     print(val)

print(lda_what_bencana)

[['jalur', 'genangan', 'api', 'banjir', 'semarang', 'jawa', 'jakarta', 'pasar'], ['kemarin', 'ketinggian', 'genangan', 'surut', 'banjir', 'terendam_banjir', 'terdampak_banjir', 'gunung', 'bpbd', 'mengungsi', 'titik'], ['aktivitas', 'kebakaran', 'rumahnya', 'unit', 'ketinggian', 'api', 'listrik', 'pemadam_kebakaran', 'terbakar', 'bpbd', 'peristiwa', 'sekolah', 'diduga'], ['jembatan', 'kemarin', 'sampah', 'kali', 'ketinggian', 'genangan', 'potensi', 'banjir', 'rusak', 'terendam_banjir', 'pohon', 'pemerintah', 'bpbd', 'longsor', 'sungai', 'tanah'], ['rumahnya', 'unit', 'melanda', 'penanganan', 'laut', 'banjir', 'bantuan', 'banjir_bandang', 'terendam_banjir', 'terdampak', 'terdampak_banjir', 'bpbd', 'mengaku', 'alam', 'sungai', 'titik'], ['jembatan', 'sampah', 'kali', 'jalur', 'genangan', 'surut', 'hujan', 'polisi', 'banjir', 'kendaraan', 'sungai', 'titik'], ['bangunan', 'aktivitas', 'banjir_rob', 'kali', 'ketinggian', 'surut', 'laut', 'rob', 'banjir', 'terendam_banjir', 'terdampak', 'terd

In [408]:
idxs = []
idxs_tp = []
idxs_tn = []
total = 0
total_tp = 0
total_tn = 0
for i in range(len(lda_what_bencana)):
    flag = True
    deflag = True
    for token in lda_what_bencana[i]:
        if token in ('kebakaran', 'banjir', 'gempa', 'gempa_bumi', 'longsor', 'banjir_rob', 'angin_kencang', 'angin', 'cuaca_ekstrem', 'hujan'):
            flag = False
    for token in df_dominant_topic['Text'].iloc[i]:
        if token in ('kebakaran', 'banjir', 'gempa', 'gempa_bumi', 'longsor', 'banjir_rob', 'angin_kencang', 'angin', 'cuaca_ekstrem', 'hujan'):
            deflag = False
    for token in df_dominant_topic['Title'].iloc[i]:
        if token in ('kebakaran', 'banjir', 'gempa', 'gempa_bumi', 'longsor', 'banjir_rob', 'angin_kencang', 'angin', 'cuaca_ekstrem', 'hujan'):
            deflag = False
    if flag != deflag:
        total += 1
        idxs.append(i)
    elif flag == deflag and flag == False:
        total_tp += 1
        idxs_tp.append(i)
    elif flag == deflag and flag == True:
        total_tn += 1
        idxs_tn.append(i)
print(len(df_dominant_topic))
print(total)
print(total_tp)
print(total_tn)

2773
0
2679
94


In [178]:
lda_check = []
for word in ('kebakaran', 'banjir', 'gempa', 'gempa_bumi', 'longsor', 'banjir_rob', 'angin_kencang', 'angin', 'cuaca_ekstrem', 'hujan'):
    if word not in df_imp_wcount['word'].values:
        lda_check.append(word)
print(lda_check)

[]


In [156]:
print(idxs_tn)

[11, 137, 138, 140, 141, 152, 156, 216, 279, 352, 454, 535, 536, 716, 753, 755, 760, 775, 835, 840, 867, 869, 888, 893, 894, 895, 906, 1114, 1123, 1133, 1254, 1259, 1267, 1284, 1339, 1416, 1417, 1424, 1455, 1464, 1473, 1496, 1535, 1603, 1607, 1612, 1624, 1631, 1640, 1660, 1681, 1714, 1729, 1764, 1765, 1776, 1777, 1825, 1829, 1834, 1863, 1912, 1938, 1975, 1976, 1988, 2008, 2022, 2028, 2031, 2037, 2068, 2075, 2077, 2083, 2112, 2139, 2212, 2232, 2240, 2325, 2417, 2423, 2448, 2449, 2454, 2462, 2629, 2652, 2670, 2680, 2733, 2748, 2754]


In [179]:
# text  = preprocessing(old_bencana['desc'][old_bencana['desc'].str.find('hari') != -1].iloc[0])
# text
i = idxs_tn[0]
print(df_dominant_topic['Keywords'].iloc[i])
print(type(df_dominant_topic['Keywords'].iloc[i]))
print(df_dominant_topic['Text'].iloc[i])
print(type(df_dominant_topic['Text'].iloc[i]))
print(df_dominant_topic['Keywords'].iloc[i].split(", "))
print(lda_what_bencana[i])


kebakaran, longsor, terbakar, ditemukan, api, mobil, pencarian, peristiwa, bangunan, damkar, polisi, diduga, tanah, pasar, tim, jakarta, meninggal, unit, rumahnya, saksi, berhasil, pohon, pria, personel, listrik, jenazah, pemadam_kebakaran, sampah, mengaku, pelaku
<class 'str'>
['kebonsari', 'sumbersari', 'rumahnya', 'balita', 'terpeleset', 'bermain', 'terjatuh', 'damkar', 'pencarian', 'komandan', 'regu', 'damkar', 'jember', 'dwi', 'atmoko', 'via', 'telepon', 'laporan', 'dwi', 'mengirim', 'personel', 'pencarian', 'mencari', 'balita', 'menyisir', 'selokan', 'digenangi', 'selokan', 'ketemu', 'selokan', 'saluran', 'perumahan', 'berbeda', 'kebingungan', 'mencari', 'lakukan', 'pengecekan', 'damkar', 'pencarian', 'menemukan', 'menyusuri', 'akhirya', 'mencoba', 'mencari', 'waduk', 'persawahan', 'bermuara', 'dibantu', 'pencarian', 'menjelang', 'pencarian', 'membuahkan', 'hasil', 'beristirahat', 'berselang', 'menemukan', 'saluran', 'ditemukan', 'bernyawa', 'jenazah', 'nyangkut', 'rerumputan', '

In [410]:
before_what_bencana = old[old['berita_topik_id'] == 1]
before_what_bencana = before_what_bencana[['berita_title', 'qe_what', 'berita_desc']]
before_what_bencana = before_what_bencana.dropna(subset=['berita_desc'])
before_what_bencana.sort_values('berita_desc', inplace=True)
before_what_bencana.drop_duplicates(subset='berita_desc', keep=False, inplace=True)
# print(before_what_bencana)
# print(before_what_bencana['qe_what'].iloc[i])
# print(before_what_bencana['berita_title'].iloc[i])
# print(before_what_bencana['berita_desc'].iloc[i])

In [414]:
total_empty = 0
empty_val = []
idxs_total = []
idxs_total.extend(idxs_tp)
idxs_total.extend(idxs_tn)
idxs_total = set(idxs_total)
with open(PATH + bencana + 'ture_negative_4.txt', 'w', encoding='UTF8') as f:
    nl = "\n"
    dashes = '--------------------------------------'
    for x in idxs_total:
        f.write(dashes + nl)
        f.write(before_what_bencana['berita_title'].iloc[x] + nl)
        f.write(str(before_what_bencana['qe_what'].iloc[x]) + nl)
        f.write(str(lda_what_bencana[x]) + nl)
        # print(before_what_bencana['berita_title'].iloc[x])
        # print(before_what_bencana['qe_what'].iloc[x])
        # print(lda_what_bencana[x])

        if len(lda_what_bencana[x])<4:
            total_empty += 1
            empty_val.append(x)

print(total_empty)
print(empty_val)


83
[118, 146, 198, 209, 352, 356, 553, 692, 716, 775, 798, 830, 869, 893, 894, 895, 897, 923, 935, 1030, 1078, 1120, 1142, 1259, 1290, 1323, 1334, 1342, 1416, 1424, 1437, 1440, 1450, 1455, 1464, 1483, 1504, 1505, 1509, 1530, 1563, 1564, 1586, 1612, 1618, 1619, 1655, 1697, 1708, 1729, 1740, 1744, 1755, 1777, 1789, 1790, 1829, 1863, 1869, 1873, 1912, 1916, 1956, 2021, 2058, 2070, 2213, 2224, 2252, 2328, 2336, 2363, 2367, 2388, 2422, 2423, 2463, 2548, 2629, 2652, 2748, 2754, 2763]


In [416]:
hitung = Counter()
for i in empty_val:
    hitung.update(lda_what_bencana[i])
    # hitung.update(lda_title_what[i])

In [183]:
hitung

Counter({'tanah': 10,
         'rusak': 6,
         'potensi': 5,
         'wisata': 4,
         'diduga': 3,
         'waspada': 3,
         'garut': 3,
         'jakarta': 3,
         'terbakar': 3,
         'pria': 2,
         'bpbd': 2,
         'makassar': 2,
         'meninggal': 2,
         'kapal': 2,
         'natal': 2,
         'pantai': 2,
         'sungai': 2,
         'pesisir': 2,
         'mobil': 2,
         'damkar': 1,
         'sampah': 1,
         'penanganan': 1,
         'fenomena': 1,
         'genangan': 1,
         'bumi': 1,
         'laut': 1,
         'rob': 1,
         'pasar': 1,
         'cuaca': 1,
         'bandung': 1,
         'gelombang': 1,
         'terdampak': 1,
         'kali': 1,
         'jenazah': 1,
         'tim': 1,
         'bali': 1,
         'ditemukan': 1,
         'berpotensi': 1,
         'jembatan': 1})

In [497]:
df_result_lda = df_dominant_topic[['Title', 'Text']]
df_result_lda['what_lda'] = lda_what_bencana
df_result_lda['what_qe'] = 0
df_result_lda['title_old'] = 0
df_result_lda['desc_old'] = 0
for i in range(len(df_result_lda)):
    df_result_lda['what_qe'].iloc[i] = before_what_bencana['qe_what'].iloc[i]
    df_result_lda['title_old'].iloc[i] = before_what_bencana['berita_title'].iloc[i]
    df_result_lda['desc_old'].iloc[i] = before_what_bencana['berita_desc'].iloc[i]

# df_result_lda.to_csv(PATH + bencana + 'df_result_lda.csv')   
df_result_lda.to_excel(PATH + bencana + 'df_result_lda.xlsx', index=None) 
df_result_lda
# print(before_what_bencana['qe_what'].iloc[0])

Title  \
0     [imbas, banjir, semarang, tujuan, jakarta, ant...   
1     [titik, banjir, tangerang, puri, bintaro, inda...   
2     [jago, merah, menyala, balikpapan, hangus, ter...   
3     [banjir, tanah, longsor, berulang, menggenangi...   
4     [banjir, natuna, pemprov, kepri, bantu, juta, ...   
...                                                 ...   
2768  [bpbd, laporkan, jateng, tergenang, banjir, te...   
2769                     [banjir, semarang, dipisahkan]   
2770                [jayapura, rasakan, gempa, susulan]   
2771  [breaking, news, gempa, guncang, jayapura, pap...   
2772  [mahasiswa, semarang, tersengat, listrik, lint...   

                                                   Text  \
0     [imbas, banjir, jawa, tawang, lintas, mengalam...   
1     [banjir, tangerang, provinsi, banten, bidang, ...   
2     [api, mendadak, muncul, karang, jati, balikpap...   
3     [bpbd, menerbitkan, surat, edaran, panewu, cam...   
4     [banjir, melanda, kabupatan, natuna, pulau, ta...   
...                                                 ...   
2768  [pantai, jawa, pantura, jawa, banjir, perganti...   
2769  [semarang, kaline, banjir, lirik, lagu, berjud...   
2770  [memperbarui, laporan, gempa, mengguncang, gem...   
2771  [gempa, magnitudo, dilaporkan, gempa, puluhan,...   
2772  [mahasiswa, melintasi, banjir, merayakan, acar...   

                                               what_lda  \
0     [jalur, genangan, api, banjir, semarang, jawa,...   
1     [kemarin, ketinggian, genangan, surut, banjir,...   
2     [aktivitas, kebakaran, rumahnya, unit, ketingg...   
3     [jembatan, kemarin, sampah, kali, ketinggian, ...   
4     [rumahnya, unit, melanda, penanganan, laut, ba...   
...                                                 ...   
2768  [tim, unit, melanda, penanganan, pantai, api, ...   
2769  [bandung, bumi, jembatan, melanda, banjir_rob,...   
2770  [bangunan, pusat_gempa, kali, tanggal, laut, k...   
2771  [bangunan, pusat_gempa, surut, laut, bmkg, dir...   
2772  [rumahnya, saksi, tanggal, genangan, mobil, li...   

                                                what_qe  \
0     wilayah, jalan, waktu, genangan, banjir, mengg...   
1     tim, wilayah, warga, genangan, banjir, menggen...   
2     akibat, peristiwa, warga, lokasi, kebakaran, t...   
3     bencana, akibat, curah, tim, wilayah, bali, ja...   
4     korban, bencana, kelurahan, akibat, curah, kec...   
...                                                 ...   
2768  korban, kelurahan, akibat, curah, tim, wilayah...   
2769  korban, akibat, tanah, curah, tim, wilayah, ma...   
2770  akibat, gempa, kerusakan, wilayah, menimbulkan...   
2771  gempa, kerusakan, bali, keterangan, warga, get...   
2772  korban, peristiwa, acara, jalan, mobil, warga,...   

                                              title_old  \
0     Imbas Banjir di Semarang, KA Tujuan Jakarta An...   
1     5 Titik Banjir di Tangerang Selatan Pagi Ini, ...   
2     Si Jago Merah Menyala di Balikpapan, Dua Rumah...   
3     Banjir-Tanah Longsor Berulang hingga Menggenan...   
4     Banjir Natuna, Pemprov Kepri Bantu Rp 300 Juta...   
...                                                 ...   
2768  BPBD Laporkan Wilayah di Jateng yang Tergenang...   
2769       Banjir dan Semarang yang Tak Bisa Dipisahkan   
2770  Warga Jayapura Sudah Rasakan 279 Gempa Susulan...   
2771  BREAKING NEWS Gempa M 5,2 Guncang Kota Jayapur...   
2772  Malam Tahun Baru, 2 Mahasiswa di Semarang Tewa...   

                                               desc_old  
0       \r\n  \r\n\- Imbas banjir yang menggenangi h...  
1       \r\n\- Banjir masih menggenangi sejumlah dae...  
2      Api mendadak muncul dari salah satu rumah war...  
3      Badan Penanggulangan Bencana Daerah (BPBD) Ku...  
4      Banjir bandang melanda Kabupatan Natuna dan P...  
...                                                 ...  
2768  \- Wilayah Pantai Utara Jawa (Pantura) di Jawa...  
2769  \- _"Semarang Kaline Banjir...."_\r

# Ekonomi

In [219]:
old_ekonomi = old[old['berita_topik_id'] == 2]
old_ekonomi = old_ekonomi[['berita_title', 'berita_date', 'berita_desc', 'berita_source']]
old_ekonomi.rename(columns = {'berita_title':'title', 'berita_date':'date', 'berita_desc':'desc', 'berita_source':'source'}, inplace=True)
print(old_ekonomi.shape)
old_ekonomi.head(2)

(3141, 4)


title  \
2005  UMKM Binaan BUMN Kolaborasi Beri Bantuan hingg...   
2006  Program Desa Brilian Diharapkan Menjadi Inspir...   

                              date  \
2005  Sabtu, 24 Des 2022 08:17 WIB   
2006  Kamis, 22 Des 2022 11:44 WIB   

                                                   desc              source  
2005  \- Guna memperkenalkan pelayanan sosial berupa...  www.tribunnews.com  
2006   Pemberdayaan wilayah pedesaan menjadi isu yan...  www.tribunnews.com

## Preprocess

In [220]:
from keybert import KeyBERT
from sentence_transformers import SentenceTransformer
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.metrics.pairwise import cosine_similarity

In [221]:
# previous way

# nltk.download('punkt')
# nltk.download('stopwords')

excluded_words = ["tempat", "waktu", "hari"]
# for lda ----
excluded_words = []
# ------------
NLTK_StopWords = stopwords.words('indonesian')
# print(NLTK_StopWords)
NLTK_StopWords.extend(["detik", "detikjatim", "detikjateng", "detikjabar", "detiksulsel", "detiksumbar", "detikbali",
                      "detikpapua", "detiksulteng", "detikmaluku", "detjatim", "detikcom", "allahumma", "aamiin", "allah", "bismillah"])
NLTK_StopWords.extend(["yg", "dg", "rt", "dgn", "ny", "d", 'klo',
                       'kalo', 'amp', 'biar', 'bikin', 'bilang',
                       'gak', 'ga', 'krn', 'nya', 'nih', 'sih',
                       'si', 'tau', 'tdk', 'tuh', 'utk', 'ya',
                       'jd', 'jgn', 'sdh', 'aja', 'n', 't',
                       'nyg', 'hehe', 'pen', 'u', 'nan', 'loh', 'rt',
                       '&amp', 'yah'])
# txt_stopword = pd.read_csv(PATH + ekonomi + "stopwords.txt", names= ["stopwords"], header = None)
# NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
# for lda ----
txt_stopword = pd.read_csv(PATH + ekonomi + "stopwords_add_v1.txt", names= ["stopwords"], header = None)
NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
# txt_stopword = pd.read_csv(PATH + ekonomi + "stopwords_add_v2.txt", names= ["stopwords"], header = None)
# NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
# txt_stopword = pd.read_csv(PATH + ekonomi + "stopwords_add_v3.txt", names= ["stopwords"], header = None)
# NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
# ------------
# convert stopword string to list & append additional stopword
# NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))

NLTK_StopWords = set(NLTK_StopWords)

In [222]:
def preprocessing(berita):
        s = str(berita)
        s = s.lower()
        s = s.replace('\n', ' ')
        s = s.replace('\r', ' ')
        # s = re.sub(r'[^a-zA-Z0-9\s]', ' ', s)
        # for lda ----
        s = re.sub(r'[^a-zA-Z\s]', ' ', s)
        # ------------
        tokens = [token for token in s.split(" ") if token != ""]
        T = [t for t in tokens if (
            (t in excluded_words) or (t not in NLTK_StopWords))]
        return T

In [223]:
old_ekonomi = old_ekonomi.dropna(subset=['desc'])
old_ekonomi.sort_values('desc', inplace=True)
old_ekonomi.drop_duplicates(subset='desc', keep=False, inplace=True)
df_train, df_test = train_test_split(old_ekonomi,test_size=0.1)
print(len(df_train))

old_ekonomi.head()

2826


title  \
10619  Anggota Komisi XI DPR Dorong Pemerintah Lebih ...   
4285   Analis Perkirakan Ekonomi China akan Bangkit L...   
4266   Ekonom Prediksi Jepang Bisa Masuk ke Jurang Re...   
9981   KSP Klaim Perppu Cipta Kerja Dibuat atas Kepen...   
4257   Cerita Heni, Ibu Rumah Tangga yang Buka Kursus...   

                                date  \
10619   Senin, 02 Jan 2023 20:59 WIB   
4285    Kamis, 22 Des 2022 19:24 WIB   
4266     Rabu, 07 Des 2022 16:19 WIB   
9981    Kamis, 05 Jan 2023 15:21 WIB   
4257   Minggu, 25 Des 2022 13:07 WIB   

                                                    desc              source  
10619    \r\n  \r\n  \r\n\- Anggota Komisi XI Dewan P...  www.tribunnews.com  
4285     \r\n  \r\nPerekonomian China pada 2023 kemun...  www.tribunnews.com  
4266     \r\n  \r\nPerusahaan riset ekonomi Capital E...  www.tribunnews.com  
9981     \r\nKantor Staf Presiden (KSP) membantah ang...      www.kompas.com  
4257     \r\nPerempuan yang telah menikah dan memilik...      www.kompas.com

In [ ]:
df_train.to_csv(PATH + ekonomi + "corpus/df_train_unprerocessed.csv" , index = None, header=True)
df_test.to_csv(PATH + ekonomi + "corpus/df_test_unprerocessed.csv" , index = None, header=True)

In [ ]:
desc_text_train_unpreprocessed = []
desc_text_test_unpreprocessed = []

for x in range(0, df_train.shape[0]):
  desc_text_train_unpreprocessed.append(df_train.iloc[x, -2])

for x in range(0, df_test.shape[0]):
  desc_text_test_unpreprocessed.append(df_test.iloc[x, -2])

In [ ]:
# Simpan teks asli dokumen
joblib.dump(desc_text_test_unpreprocessed, PATH + ekonomi + "corpus/model/desc_text_test_unpreprocessed.pkl")
joblib.dump(desc_text_train_unpreprocessed, PATH + ekonomi + "corpus/model/desc_text_train_unpreprocessed.pkl")

# Simpan dataframe hasil text processing sebelum TF-IDF Vectorizer
old_ekonomi.to_csv(PATH + ekonomi + 'corpus/dataset/df_total_unpreprocessed.csv', index=False)
df_test.to_csv(PATH + ekonomi + 'corpus/dataset/df_test_unpreprocessed.csv', index=False)
df_train.to_csv(PATH + ekonomi + 'corpus/dataset/df_train_unpreprocessed.csv', index=False)

In [224]:
for x in range(0, old_ekonomi.shape[0]):
    text = preprocessing(old_ekonomi.iloc[x, -2])
    old_ekonomi.iloc[x, -2] = (' '.join(text))

for x in range(0, old_ekonomi.shape[0]):
    text = preprocessing(old_ekonomi.iloc[x, -4])
    old_ekonomi.iloc[x, -4] = (' '.join(text)) 
old_ekonomi.head()

title  \
10619  anggota komisi xi dpr dorong pemerintah perhat...   
4285   analis perkirakan ekonomi china bangkit cepat ...   
4266   ekonom prediksi jepang masuk jurang resesi did...   
9981   ksp klaim perppu cipta kerja kepentingan peker...   
4257   cerita heni rumah tangga buka kursus online ba...   

                                date  \
10619   Senin, 02 Jan 2023 20:59 WIB   
4285    Kamis, 22 Des 2022 19:24 WIB   
4266     Rabu, 07 Des 2022 16:19 WIB   
9981    Kamis, 05 Jan 2023 15:21 WIB   
4257   Minggu, 25 Des 2022 13:07 WIB   

                                                    desc              source  
10619  anggota komisi xi dewan perwakilan rakyat dpr ...  www.tribunnews.com  
4285   perekonomian china perekonomian negara beijing...  www.tribunnews.com  
4266   perusahaan riset ekonomi capital economics per...  www.tribunnews.com  
9981   kantor staf presiden ksp membantah anggapan pe...      www.kompas.com  
4257   perempuan menikah memiliki seringkali memilih ...      www.kompas.com

In [ ]:
desc_text_train = []
desc_text_test = []

for x in range(0, df_train.shape[0]):
  desc_text_train.append(df_train.iloc[x, -2])

for x in range(0, df_test.shape[0]):
  desc_text_test.append(df_test.iloc[x, -2])

# print(df_test.info())
print("Panjang Dokumen Test : ", len(desc_text_test))

print ('-'*90)

# print(df_train.info())
print("Panjang Dokumen Train : ", len(desc_text_train))

In [ ]:
# Simpan teks asli dokumen
joblib.dump(desc_text_test, PATH + ekonomi + "corpus/model/desc_text_test.pkl")
joblib.dump(desc_text_train, PATH + ekonomi + "corpus/model/desc_text_train_new.pkl") #INI

# Simpan dataframe hasil text processing sebelum TF-IDF Vectorizer
old_ekonomi.to_csv(PATH + ekonomi + 'corpus/dataset/df_total_new.csv', index=False) #INI
df_test.to_csv(PATH + ekonomi + 'corpus/dataset/df_test.csv', index=False)
df_train.to_csv(PATH + ekonomi + 'corpus/dataset/df_train.csv', index=False)

In [ ]:
# Fit transform menggunakan TF-IDF Vectorizer
tfidf_vectorizer = TfidfVectorizer()
tfidf_test_matrix = tfidf_vectorizer.fit_transform(desc_text_test)
tfidf_train_matrix = tfidf_vectorizer.fit_transform(desc_text_train)

print('tfidf_test_matrix')
print(tfidf_test_matrix.shape)
print('tfidf_train_matrix')
print(tfidf_train_matrix.shape)

In [ ]:
joblib.dump(tfidf_vectorizer, PATH + ekonomi + "corpus/vectorizer/vectorizer_new.pkl") #INI
joblib.dump(tfidf_test_matrix, PATH + ekonomi + "corpus/matrix/tfidf_test.pkl")
joblib.dump(tfidf_train_matrix, PATH + ekonomi + "corpus/matrix/tfidf_train_new.pkl") #INI

## YAKE BERT TFIDF

## MAIN COURSE

## LDA

In [225]:
import gensim
from gensim import corpora
from collections import Counter
import pyLDAvis.gensim
import pickle 
import pyLDAvis
from nltk.tokenize import word_tokenize 
from nltk.probability import FreqDist

def remove_number(text):
    return  re.sub(r"\d+", "", text)

In [226]:
new_ekonomi = old_ekonomi[['title', 'desc']]
new_ekonomi['desc'] = new_ekonomi['desc'].apply(remove_number)
new_ekonomi['desc'] = new_ekonomi['desc'].apply(word_tokenize)
new_ekonomi['desc'] = [[token for token in doc if len(token) > 2] for doc in new_ekonomi['desc']]
new_ekonomi['title'] = new_ekonomi['title'].apply(remove_number)
new_ekonomi['title'] = new_ekonomi['title'].apply(word_tokenize)
new_ekonomi['title'] = [[token for token in doc if len(token) > 2] for doc in new_ekonomi['title']]
new_ekonomi['fdist'] = new_ekonomi['desc'].apply(FreqDist)

print(len(new_ekonomi))
print(new_ekonomi.head(2))

print('Frequency Tokens : \n') 
print(new_ekonomi['fdist'].head().apply(lambda x : x.most_common()))

3141
                                                   title  \
10619  [anggota, komisi, dpr, dorong, pemerintah, per...   
4285   [analis, perkirakan, ekonomi, china, bangkit, ...   

                                                    desc  \
10619  [anggota, komisi, dewan, perwakilan, rakyat, d...   
4285   [perekonomian, china, perekonomian, negara, be...   

                                                   fdist  
10619  {'anggota': 1, 'komisi': 1, 'dewan': 1, 'perwa...  
4285   {'perekonomian': 2, 'china': 20, 'negara': 12,...  
Frequency Tokens : 

10619    [(umkm, 21), (aday, 14), (pemerintah, 7), (ind...
4285     [(china, 20), (negara, 12), (persen, 10), (eko...
4266     [(persen, 10), (jepang, 8), (resesi, 6), (thie...
9981     [(pemerintah, 12), (perppu, 12), (kerja, 10), ...
4257     [(heni, 14), (kursus, 10), (teknologi, 9), (on...
Name: fdist, dtype: object


In [227]:
from gensim.models import Phrases
bigram = Phrases(new_ekonomi['desc'], min_count=20)
for idx in range(len(new_ekonomi['desc'])):
    for token in bigram[new_ekonomi['desc'].iloc[idx]]:
        if '_' in token:
            # Token is a bigram, add to document.
            new_ekonomi['desc'].iloc[idx].append(token)
            word1, word2 = token.split("_")
            # if word1 not in ('kebakaran', 'banjir', 'gempa', 'longsor', 'banjir', 'angin'):
            #     new_ekonomi['desc'].iloc[idx].remove(word1)
            # if word2 not in ('kebakaran', 'banjir', 'gempa', 'longsor', 'banjir', 'angin'):
            #     new_ekonomi['desc'].iloc[idx].remove(word2)
            # print(token)

In [483]:
dictionary = corpora.Dictionary(new_ekonomi['desc'])
dictionary.filter_extremes(no_below=35, no_above=0.5)
print(dictionary)

corpus = [dictionary.doc2bow(berita) for berita in new_ekonomi['desc']]

Dictionary<2555 unique tokens: ['acara', 'achmad', 'akrab', 'akses', 'anggota']...>


In [484]:
# Creating the object for LDA model using gensim library
Lda = gensim.models.ldamodel.LdaModel

total_topics = 5 # jumlah topik yang akan di extract
number_words = 30 # jumlah kata per topik

In [485]:
import os
from gensim.test.utils import datapath
the_path = PATH + ekonomi + "model/lda_model" + "_" + str(total_topics) + "_" + str(number_words)
if not os.path.exists(the_path):
    os.mkdir(the_path)
temp_file = datapath(the_path + "/lda_model")
#if new
# lda_model = Lda(corpus, num_topics=total_topics, id2word=dictionary, passes=50, random_state=1)
# lda_model.save(temp_file)
# load
from gensim import models
lda_model = models.ldamodel.LdaModel.load(temp_file)

lda_model.show_topics(num_topics=total_topics, num_words=number_words)

[(0,
  '0.010*"pendidikan" + 0.010*"memiliki" + 0.009*"warga" + 0.009*"rumah" + 0.008*"universitas" + 0.007*"sosial" + 0.007*"keluarga" + 0.006*"program" + 0.006*"kegiatan" + 0.006*"politik" + 0.005*"dunia" + 0.005*"fakultas" + 0.005*"kondisi" + 0.005*"korban" + 0.005*"jalan" + 0.005*"ilmu" + 0.004*"sekolah" + 0.004*"kerja" + 0.004*"kesehatan" + 0.004*"hidup" + 0.004*"hukum" + 0.004*"manusia" + 0.004*"perempuan" + 0.004*"jokowi" + 0.004*"bali" + 0.003*"bidang" + 0.003*"mahasiswa" + 0.003*"pelaku" + 0.003*"negara" + 0.003*"uang"'),
 (1,
  '0.011*"pemerintah" + 0.010*"negara" + 0.009*"pembangunan" + 0.009*"daerah" + 0.008*"jakarta" + 0.007*"jalan" + 0.007*"kementerian" + 0.006*"program" + 0.006*"kepala" + 0.006*"menteri" + 0.005*"jokowi" + 0.005*"kawasan" + 0.005*"presiden" + 0.005*"kerja" + 0.005*"pusat" + 0.005*"terkait" + 0.005*"bidang" + 0.005*"jawa" + 0.004*"pasal" + 0.004*"kegiatan" + 0.004*"nasional" + 0.004*"energi" + 0.004*"lingkungan" + 0.004*"investasi" + 0.004*"listrik" + 0.0

In [486]:
# Word Count of Topic Keywords

from collections import Counter
topics = lda_model.show_topics(formatted=False, num_topics=total_topics, num_words=number_words)
# topic = lda_model.show_topics(num_topics=total_topics, num_words=number_words)
# print((topics[0]))
# print((topic[0]))
data_flat = [w for w_list in new_ekonomi['desc'] for w in w_list]
counter = Counter(data_flat)

out = []
for i, topic in topics:
    for word, weight in topic:
        out.append([word, i , weight, counter[word]])

df_imp_wcount = pd.DataFrame(out, columns=['word', 'id', 'importance', 'word_count']) 
print(df_imp_wcount)

            word  id  importance  word_count
0     pendidikan   0    0.010043        1012
1       memiliki   0    0.010020        2383
2          warga   0    0.009444         961
3          rumah   0    0.009422        1208
4    universitas   0    0.007799         732
..           ...  ..         ...         ...
145       pemilu   4    0.005040         338
146        nomor   4    0.005031         815
147     provinsi   4    0.004759         741
148      pekerja   4    0.004701         367
149         juta   4    0.004677        1656

[150 rows x 4 columns]


In [487]:
def format_topics_sentences(ldamodel=None, corpus=corpus, texts=new_ekonomi['desc']):
    # Init output
    sent_topics_df = pd.DataFrame()
    # print(len(ldamodel[corpus]))

    dom = []
    perc = []
    keywords = []
    # Get main topic in each document
    for i, row_list in enumerate(ldamodel[corpus]):
        row = row_list[0] if ldamodel.per_word_topics else row_list            
        row = sorted(row, key=lambda x: (x[1]), reverse=True)
        # print(len(row))

        # Get the Dominant topic, Perc Contribution and Keywords for each document
        for j, (topic_num, prop_topic) in enumerate(row):
            if j == 0:  # => dominant topic
                wp = ldamodel.show_topic(topic_num, topn=number_words)
                topic_keywords = ", ".join([word for word, prop in wp])
                dom.append(int(topic_num))
                perc.append(round(prop_topic,4))
                keywords.append(topic_keywords)
                # sent_topics_df = pd.concat([sent_topics_df, pd.DataFrame([pd.Series([int(topic_num), round(prop_topic,4), topic_keywords])])], ignore_index=True)
                # sent_topics_df = sent_topics_df.append(pd.Series([int(topic_num), round(prop_topic,4), topic_keywords]), ignore_index=True)
            else:
                break
    # print(len(sent_topics_df))
    sent_topics_df['Dominant_Topic'] = dom
    sent_topics_df['Perc_Contribution'] = perc
    sent_topics_df['Topic_Keywords'] = keywords
    # sent_topics_df.columns = ['Dominant_Topic', 'Perc_Contribution', 'Topic_Keywords']

    # Add original text to the end of the output
    # sent_topics_df['Texts']= texts
    # print(len(sent_topics_df))
    return(sent_topics_df)

In [488]:
df_topic_sents_keywords = format_topics_sentences(ldamodel=lda_model, corpus=corpus, texts=new_ekonomi['desc'])
df_topic_sents_keywords['Texts'] = 0
df_topic_sents_keywords['Title'] = 0

In [489]:
df_dominant_topic = df_topic_sents_keywords.reset_index()
# texts = []
for i in range(len(new_ekonomi['desc'])):
    # print(new_ekonomi['desc'].iloc[i])
    # texts.append(new_ekonomi['desc'].iloc[i])
    df_dominant_topic['Texts'].iloc[i] = new_ekonomi['desc'].iloc[i]
    df_dominant_topic['Title'].iloc[i] = new_ekonomi['title'].iloc[i]
# df_dominant_topic['Texts'] = texts
df_dominant_topic.columns = ['Document_No', 'Dominant_Topic', 'Topic_Perc_Contrib', 'Keywords', 'Text', 'Title']

# df_topic_sents_keywords['Texts'].isna().value_counts()
df_dominant_topic.head(5)
df_dominant_topic.tail(5)

Document_No  Dominant_Topic  Topic_Perc_Contrib  \
3136         3136               0              0.5679   
3137         3137               3              0.9189   
3138         3138               1              0.5546   
3139         3139               3              0.3292   
3140         3140               2              0.8154   

                                               Keywords  \
3136  pendidikan, memiliki, warga, rumah, universita...   
3137  bank, syariah, bsi, negara, keuangan, pertumbu...   
3138  pemerintah, negara, pembangunan, daerah, jakar...   
3139  bank, syariah, bsi, negara, keuangan, pertumbu...   
3140  umkm, usaha, produk, pelaku, bisnis, pasar, pr...   

                                                   Text  \
3136  [menjelang, petang, aktivitas, pengungsian, la...   
3137  [pelaku, ekonomi, dunia, usaha, pebisnis, eval...   
3138  [transisi, energi, misi, pengurangan, emisi, k...   
3139  [tua, mpr, bambang, soesatyo, asumsi, eksisten...   
3140  [tua, mpr, bambang, soesatyo, digitalisasi, um...   

                                                  Title  
3136  [dapur, kreasi, upaya, kemensos, pulihkan, per...  
3137                                 [outlook, ekonomi]  
3138  [tantangan, transisi, energi, peluang, pertumb...  
3139  [bamsoet, dorong, koperasi, sokoguru, perekono...  
3140            [bamsoet, tegaskan, digitalisasi, umkm]

In [397]:
df_dominant_topic.to_csv(PATH + ekonomi + 'df_dominant_topic.csv')

In [34]:
pyLDAvis.enable_notebook()

In [151]:
from datetime import datetime
now = datetime.now() # current date and time
date_time = now.strftime("%m-%d-%Y_%H-%M-%S")
print("date and time:",date_time)
LDAvis_html = 'ldavis_prepared_'+ str(total_topics)+"_"+str(number_words)+"_"+str(date_time)
LDAvis_prepared = pyLDAvis.gensim.prepare(lda_model, corpus, dictionary)
with open(PATH + ekonomi + LDAvis_html, 'wb') as f:
        pickle.dump(LDAvis_prepared, f)

date and time: 06-23-2023_21-00-13


In [70]:
# LDAvis_html = 'ldavis_prepared_4_30_06-23-2023_19-01-24'

In [152]:
with open(PATH + ekonomi + LDAvis_html, 'rb') as f:
    LDAvis_prepared = pickle.load(f)

In [153]:
pyLDAvis.save_html(LDAvis_prepared, PATH + ekonomi + LDAvis_html +'.html')

In [43]:
# pyLDAvis.show(LDAvis_prepared)
# pyLDAvis.display(LDAvis_prepared, template_type='notebook')

In [289]:
lda_what_ekonomi = []
word_topics = set(df_imp_wcount['word'].values)
for i in range(len(df_dominant_topic)):
    val = []
    for n, key in enumerate(word_topics):
        if key in df_dominant_topic['Text'].iloc[i]:
            val.append(key)
    lda_what_ekonomi.append(val)

print(lda_what_ekonomi)

[['pelatihan', 'memiliki', 'umkm', 'bank', 'pelaku_umkm', 'meningkatkan', 'mikro', 'menengah', 'pelaku', 'persen', 'ekspor', 'daerah', 'kerja', 'mendorong', 'perekonomian', 'pusat', 'pemerintah', 'acara', 'perbankan', 'juta', 'usaha', 'produk', 'nasional'], ['kepala', 'digital', 'dunia', 'membantu', 'perusahaan', 'miliar', 'pertumbuhan', 'bank', 'meningkatkan', 'menengah', 'pertumbuhan_ekonomi', 'persen', 'listrik', 'negara', 'global', 'kelas', 'ekspor', 'lokal', 'perekonomian', 'terkait', 'pemerintah', 'perbankan', 'kebijakan', 'rumah', 'triliun', 'mencapai', 'sektor', 'juta', 'kesehatan', 'pasar', 'industri', 'investasi', 'produk'], ['kenaikan', 'negeri', 'gubernur', 'perusahaan', 'miliar', 'pertumbuhan', 'bank', 'pertumbuhan_ekonomi', 'impor', 'persen', 'negara', 'ekspor', 'upah', 'inflasi', 'perekonomian', 'kebijakan', 'rumah', 'mencapai', 'lingkungan', 'produk', 'nasional'], ['memiliki', 'keuangan', 'umkm', 'presiden', 'nomor', 'pelaku_umkm', 'hukum', 'mikro', 'menengah', 'kondisi

In [290]:
lda_title_what = []
word_topics = set(df_imp_wcount['word'].values)
for i in range(len(df_dominant_topic)):
    val = []
    for n, key in enumerate(word_topics):
        if key in df_dominant_topic['Title'].iloc[i]:
            val.append(key)
    lda_title_what.append(val)

print(lda_title_what)

[['umkm', 'pemerintah'], [], ['ekspor'], ['umkm', 'pelaku', 'kerja', 'pekerja'], ['keluarga', 'rumah'], ['kebijakan'], ['nasabah'], ['umkm', 'kerja', 'menteri'], ['umkm', 'kelas'], ['digital', 'sandiaga', 'global', 'mendorong', 'rumah'], ['persen', 'inflasi'], ['digital'], ['negara', 'ekspor'], ['gubernur', 'pertumbuhan', 'persen'], ['jokowi', 'kegiatan'], [], [], [], ['kondisi', 'global', 'perekonomian'], ['ekspor'], ['jokowi', 'ekspor', 'juta'], ['bisnis'], ['umkm', 'miliar', 'pekerja'], ['impor', 'pemerintah'], ['umkm', 'kelas', 'bali'], ['umkm'], ['umkm'], ['umkm'], ['bri', 'ekspor', 'kerja'], ['umkm'], ['dunia', 'umkm', 'pelaku', 'pasar'], ['umkm', 'bri'], ['pelatihan', 'bri'], [], ['dunia', 'minyak', 'persen', 'harga'], ['impor'], ['korupsi', 'ekspor'], ['bri'], ['impor', 'pemerintah', 'juta'], ['pelaku', 'sektor'], ['digital', 'kementerian', 'pembangunan'], ['umkm', 'koperasi'], ['umkm', 'pelaku', 'negara', 'kelas', 'perekonomian'], ['juta'], ['bisnis'], ['umkm', 'perekonomian',

In [238]:
for n, word_list in enumerate(lda_title_what):
    val = []
    for word in word_list:
        if word in lda_what_ekonomi[n]:
            continue
        val.append(word)
    lda_what_ekonomi[n].extend(val)
    # if val:
    #     print(n)
    #     print(val)

print(lda_what_ekonomi)

[['pelatihan', 'memiliki', 'umkm', 'bank', 'pelaku_umkm', 'meningkatkan', 'mikro', 'menengah', 'pelaku', 'persen', 'ekspor', 'daerah', 'kerja', 'mendorong', 'perekonomian', 'pusat', 'pemerintah', 'acara', 'perbankan', 'juta', 'usaha', 'produk', 'nasional'], ['kepala', 'digital', 'dunia', 'membantu', 'perusahaan', 'miliar', 'pertumbuhan', 'bank', 'meningkatkan', 'menengah', 'pertumbuhan_ekonomi', 'persen', 'listrik', 'negara', 'global', 'kelas', 'ekspor', 'lokal', 'perekonomian', 'terkait', 'pemerintah', 'perbankan', 'kebijakan', 'rumah', 'triliun', 'mencapai', 'sektor', 'juta', 'kesehatan', 'pasar', 'industri', 'investasi', 'produk'], ['kenaikan', 'negeri', 'gubernur', 'perusahaan', 'miliar', 'pertumbuhan', 'bank', 'pertumbuhan_ekonomi', 'impor', 'persen', 'negara', 'ekspor', 'upah', 'inflasi', 'perekonomian', 'kebijakan', 'rumah', 'mencapai', 'lingkungan', 'produk', 'nasional'], ['memiliki', 'keuangan', 'umkm', 'presiden', 'nomor', 'pelaku_umkm', 'hukum', 'mikro', 'menengah', 'kondisi

In [398]:
idxs = []
idxs_tp = []
idxs_tn = []
idxs_lda = [] #not in lda words
total = 0
total_tp = 0
total_tn = 0
total_lda = 0
check_lda = ('umkm', 'harga', 'bank', 'pemerintah', 'negara', 'inflasi', 'pertumbuhan', 'bisnis', 'pariwisata', 'ekspor', 
             'impor', 'uang', 'keuangan', 'usaha', 'kebijakan', 'syariah', 'pasar', 'industri', 'investasi', 'program',
             'kenaikan', 'wisatawan', 'perusahaan', 'wisata', 'sektor', 'transaksi', 'mikro', 'digital')
for i in range(len(lda_what_ekonomi)):
    flag = True
    deflag = True
    ldaf = True
    for token in lda_what_ekonomi[i]:
        if token in check_lda:
            flag = False
        if token in df_imp_wcount['word'].values:
            ldaf = False
    for token in df_dominant_topic['Text'].iloc[i]:
        if token in check_lda:
            deflag = False
    for token in df_dominant_topic['Title'].iloc[i]:
        if token in check_lda:
            deflag = False
    if flag != deflag:
        total += 1
        idxs.append(i)
    elif flag == deflag and flag == False:
        total_tp += 1
        idxs_tp.append(i)
    elif flag == deflag and flag == True:
        total_tn += 1
        idxs_tn.append(i)
    if ldaf:
        total_lda += 1
        idxs_lda.append(i)
print(len(df_dominant_topic))
print(total)
print(total_tp)
print(total_tn)
print(total_lda)


3141
0
2990
151
0


In [201]:
lda_check = []
for word in check_lda:
    if word not in df_imp_wcount['word'].values:
        lda_check.append(word)
print(lda_check)

[]


In [164]:
print(idxs_tn)

[43, 47, 62, 77, 89, 90, 124, 183, 184, 187, 189, 197, 199, 207, 208, 210, 213, 221, 228, 232, 233, 267, 282, 308, 317, 357, 409, 417, 424, 425, 427, 430, 438, 440, 442, 443, 447, 454, 470, 496, 507, 509, 512, 518, 519, 520, 556, 562, 564, 566, 581, 583, 585, 606, 614, 615, 621, 622, 629, 630, 632, 633, 634, 635, 636, 639, 643, 644, 645, 646, 647, 648, 651, 656, 657, 661, 670, 673, 686, 687, 696, 706, 708, 710, 716, 717, 732, 737, 741, 750, 751, 753, 775, 777, 784, 786, 789, 792, 793, 797, 808, 811, 815, 819, 828, 839, 842, 861, 862, 864, 872, 878, 881, 901, 905, 921, 924, 931, 932, 938, 939, 940, 941, 998, 1005, 1007, 1009, 1010, 1015, 1019, 1033, 1035, 1038, 1039, 1048, 1049, 1055, 1068, 1069, 1070, 1075, 1077, 1087, 1091, 1092, 1096, 1101, 1103, 1108, 1116, 1131, 1136, 1155, 1162, 1166, 1169, 1174, 1176, 1186, 1187, 1190, 1200, 1203, 1205, 1212, 1223, 1252, 1255, 1274, 1282, 1286, 1297, 1300, 1307, 1320, 1323, 1334, 1335, 1342, 1351, 1354, 1355, 1361, 1369, 1370, 1371, 1378, 1381, 1

In [77]:
# text  = preprocessing(old_ekonomi['desc'][old_ekonomi['desc'].str.find('hari') != -1].iloc[0])
# text
i = idxs_tn[0]
print(df_dominant_topic['Keywords'].iloc[i])
print(type(df_dominant_topic['Keywords'].iloc[i]))
print(df_dominant_topic['Text'].iloc[i])
print(type(df_dominant_topic['Text'].iloc[i]))
print(df_dominant_topic['Keywords'].iloc[i].split(", "))
print(lda_what_ekonomi[i])


umkm, bank, usaha, syariah, produk, bsi, digital, bisnis, pelaku, layanan, keuangan, bank_syariah, memiliki, perbankan, program, pasar, nasabah, salah, teknologi, perusahaan, meningkatkan, juta, transaksi, pelaku_umkm, pembiayaan, industri, pelaku_usaha, mikro, mendorong, sektor
<class 'str'>
['anggota', 'komisi', 'dewan', 'perwakilan', 'rakyat', 'dpr', 'andi', 'achmad', 'dara', 'mendorong', 'pemerintah', 'memperhatikan', 'usaha', 'mikro', 'menengah', 'umkm', 'perhatian', 'bentuk', 'sungguh', 'sungguh', 'kongkrit', 'modal', 'ventura', 'mempermudah', 'umkm', 'mengakses', 'modal', 'bunga', 'ringan', 'terjangkau', 'aday', 'panggilan', 'akrab', 'andi', 'achmad', 'dara', 'acara', 'kunjungan', 'kerjanya', 'sepatan', 'kresek', 'tangerang', 'pekan', 'tangerang', 'aday', 'kunjungan', 'kerja', 'cipondoh', 'tangerang', 'aday', 'ekonomi', 'rakyat', 'indonesia', 'identik', 'umkm', 'sebarannya', 'indonesia', 'acara', 'kunjungan', 'kerja', 'aday', 'disertai', 'pembagian', 'sembako', 'pelaku', 'umkm',

In [292]:
before_what_ekonomi = old[old['berita_topik_id'] == 2]
before_what_ekonomi = before_what_ekonomi[['berita_title', 'qe_what', 'berita_desc']]
before_what_ekonomi = before_what_ekonomi.dropna(subset=['berita_desc'])
before_what_ekonomi.sort_values('berita_desc', inplace=True)
before_what_ekonomi.drop_duplicates(subset='berita_desc', keep=False, inplace=True)
# print(before_what_ekonomi)
# print(before_what_ekonomi['qe_what'].iloc[i])
# print(before_what_ekonomi['berita_title'].iloc[i])
# print(before_what_ekonomi['berita_desc'].iloc[i])

In [401]:
total_empty = 0
empty_val = []
idxs_total = []
idxs_total.extend(idxs_tp)
idxs_total.extend(idxs_tn)
idxs_total = set(idxs_total)
with open(PATH + ekonomi + 'true_negative_5.txt', 'w', encoding='UTF8') as f:
    nl = "\n"
    dashes = '--------------------------------------'
    for x in idxs_total:
        f.write(dashes + nl)
        f.write(before_what_ekonomi['berita_title'].iloc[x] + nl)
        f.write(str(before_what_ekonomi['qe_what'].iloc[x]) + nl)
        f.write(str(lda_what_ekonomi[x]) + nl)
        # print(before_what_ekonomi['berita_title'].iloc[x])
        # print(before_what_ekonomi['qe_what'].iloc[x])
        # print(lda_what_ekonomi[x])

        if len(lda_what_ekonomi[x])<5:
            total_empty += 1
            empty_val.append(x)

print(total_empty)
print(empty_val)


74
[77, 183, 274, 275, 276, 277, 400, 401, 436, 442, 520, 566, 647, 648, 656, 657, 673, 686, 706, 717, 732, 741, 751, 792, 797, 819, 897, 941, 947, 1020, 1039, 1095, 1369, 1370, 1376, 1404, 1405, 1430, 1439, 1463, 1672, 1780, 1815, 1887, 1932, 2040, 2041, 2042, 2070, 2095, 2108, 2121, 2143, 2166, 2177, 2180, 2182, 2267, 2314, 2356, 2357, 2406, 2466, 2480, 2493, 2555, 2622, 2670, 2704, 2799, 2892, 2927, 2943, 3060]


In [203]:
hitung = Counter()
for i in idxs_tn:
    hitung.update(lda_what_ekonomi[i])
    # hitung.update(lda_title_what[i])
    # print('--------------------------------------')
    # print(before_what_ekonomi['berita_title'].iloc[i])
    # print(before_what_ekonomi['qe_what'].iloc[i])
    # print(lda_what_ekonomi[i])
hitung

Counter({'warga': 40,
         'kondisi': 39,
         'memiliki': 39,
         'jalan': 38,
         'ketua': 37,
         'sosial': 36,
         'rumah': 36,
         'jakarta': 36,
         'jawa': 34,
         'terkait': 31,
         'daerah': 30,
         'dunia': 28,
         'kepala': 27,
         'presiden': 27,
         'keluarga': 23,
         'politik': 23,
         'kegiatan': 22,
         'bidang': 22,
         'korban': 22,
         'nasional': 21,
         'pelaku': 20,
         'kerja': 19,
         'hidup': 19,
         'kesehatan': 18,
         'partai': 18,
         'pendidikan': 17,
         'pusat': 17,
         'hukum': 17,
         'jokowi': 17,
         'acara': 15,
         'negeri': 14,
         'lingkungan': 14,
         'mencapai': 14,
         'kementerian': 14,
         'pembangunan': 14,
         'menteri': 14,
         'meningkatkan': 13,
         'kawasan': 13,
         'pemilu': 13,
         'universitas': 12,
         'pasal': 12,
         'perempuan'

In [490]:
df_result_lda = df_dominant_topic[['Title', 'Text']]
df_result_lda['what_lda'] = lda_what_ekonomi
df_result_lda['what_qe'] = 0
df_result_lda['title_old'] = 0
df_result_lda['desc_old'] = 0
for i in range(len(df_result_lda)):
    df_result_lda['what_qe'].iloc[i] = before_what_ekonomi['qe_what'].iloc[i]
    df_result_lda['title_old'].iloc[i] = before_what_ekonomi['berita_title'].iloc[i]
    df_result_lda['desc_old'].iloc[i] = before_what_ekonomi['berita_desc'].iloc[i]

# df_result_lda.to_csv(PATH + ekonomi + 'df_result_lda.csv')   
df_result_lda.to_excel(PATH + ekonomi + 'df_result_lda.xlsx', index=None) 
df_result_lda
# print(before_what_ekonomi['qe_what'].iloc[0])

Title  \
0     [anggota, komisi, dpr, dorong, pemerintah, per...   
1     [analis, perkirakan, ekonomi, china, bangkit, ...   
2     [ekonom, prediksi, jepang, masuk, jurang, rese...   
3     [ksp, klaim, perppu, cipta, kerja, kepentingan...   
4     [cerita, heni, rumah, tangga, buka, kursus, on...   
...                                                 ...   
3136  [dapur, kreasi, upaya, kemensos, pulihkan, per...   
3137                                 [outlook, ekonomi]   
3138  [tantangan, transisi, energi, peluang, pertumb...   
3139  [bamsoet, dorong, koperasi, sokoguru, perekono...   
3140            [bamsoet, tegaskan, digitalisasi, umkm]   

                                                   Text  \
0     [anggota, komisi, dewan, perwakilan, rakyat, d...   
1     [perekonomian, china, perekonomian, negara, be...   
2     [perusahaan, riset, ekonomi, capital, economic...   
3     [kantor, staf, presiden, ksp, membantah, angga...   
4     [perempuan, menikah, memiliki, seringkali, mem...   
...                                                 ...   
3136  [menjelang, petang, aktivitas, pengungsian, la...   
3137  [pelaku, ekonomi, dunia, usaha, pebisnis, eval...   
3138  [transisi, energi, misi, pengurangan, emisi, k...   
3139  [tua, mpr, bambang, soesatyo, asumsi, eksisten...   
3140  [tua, mpr, bambang, soesatyo, digitalisasi, um...   

                                               what_lda  \
0     [pelatihan, memiliki, umkm, bank, pelaku_umkm,...   
1     [kepala, digital, dunia, membantu, perusahaan,...   
2     [kenaikan, negeri, gubernur, perusahaan, milia...   
3     [memiliki, keuangan, umkm, presiden, nomor, pe...   
4     [memiliki, keluarga, digital, dunia, membantu,...   
...                                                 ...   
3136  [uang, memiliki, keluarga, keuangan, provinsi,...   
3137  [uang, kenaikan, dunia, membantu, kawasan, keu...   
3138  [memiliki, negeri, dunia, keuangan, pertumbuha...   
3139  [memiliki, dunia, pasal, umkm, pertumbuhan, no...   
3140  [kur, pelatihan, digital, negeri, gubernur, me...   

                                                what_qe  \
0     persen, ekspor, pusat, pemerintah, memilik, ke...   
1     pt, dagang, persen, kuartal, catatan, informas...   
2     pt, dagang, persen, kuartal, impor, ekspor, ha...   
3     pt, terkait, pemerintah, memilik, kritik, baha...   
4     resmi, hari, waktu, mengalami, memilik, kurs, ...   
...                                                 ...   
3136  pt, dagang, hari, kekuatan, memilik, bahan, sa...   
3137  pt, bergelombang, dagang, persen, bps, lembaga...   
3138  persen, prediksi, mengalami, minus, pemerintah...   
3139  resesi, memilik, pemerataan, publik, sk, faktu...   
3140  dagang, persen, lembaga, pemerintah, bahan, pe...   

                                              title_old  \
0     Anggota Komisi XI DPR Dorong Pemerintah Lebih ...   
1     Analis Perkirakan Ekonomi China akan Bangkit L...   
2     Ekonom Prediksi Jepang Bisa Masuk ke Jurang Re...   
3     KSP Klaim Perppu Cipta Kerja Dibuat atas Kepen...   
4     Cerita Heni, Ibu Rumah Tangga yang Buka Kursus...   
...                                                 ...   
3136  Dapur Kreasi, Upaya Kemensos Pulihkan Perekono...   
3137                               Outlook Ekonomi 2023   
3138  Tak Hanya Tantangan, Transisi Energi Peluang P...   
3139  Bamsoet Dorong Koperasi Jadi Sokoguru Perekono...   
3140      Bamsoet Tegaskan Pentingnya Digitalisasi UMKM   

                                               desc_old  
0       \r\n  \r\n  \r\n\- Anggota Komisi XI Dewan P...  
1       \r\n  \r\nPerekonomian China pada 2023 kemun...  
2       \r\n  \r\nPerusahaan riset ekonomi Capital E...  
3       \r\nKantor Staf Presiden (KSP) membantah ang...  
4       \r\nPerempuan yang telah menikah dan memilik...  
...                                                 ...  
3136  ri menjelang petang. Aktivitas di lokasi pengu...  
3137  setiap bulan Desember biasanya pela

# Kecelakaan

In [177]:
old_kecelakaan = old[old['berita_topik_id'] == 3]
old_kecelakaan = old_kecelakaan[['berita_title', 'berita_date', 'berita_desc', 'berita_source']]
old_kecelakaan.rename(columns = {'berita_title':'title', 'berita_date':'date', 'berita_desc':'desc', 'berita_source':'source'}, inplace=True)
print(old_kecelakaan.shape)
old_kecelakaan.head(2)

(2102, 4)


title  \
4333  Bus Wisata Terjun ke Jurang Sedalam 30 Meter d...   
4334  Kronologi Minibus Rombongan Pelayat Masuk Jura...   

                               date  \
4333   Senin, 05 Des 2022 10:44 WIB   
4334  Selasa, 29 Nov 2022 10:05 WIB   

                                                   desc              source  
4333  Bus wisata yang berangkat dari Semarang kecela...  www.tribunnews.com  
4334  \- Kecelakaan maut minibus rombongan pelayat m...  www.tribunnews.com

## Preprocess

In [178]:
from keybert import KeyBERT
from sentence_transformers import SentenceTransformer
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.metrics.pairwise import cosine_similarity

In [179]:
# previous way

# nltk.download('punkt')
# nltk.download('stopwords')

excluded_words = ["tempat", "waktu", "hari"]
# for lda ----
excluded_words = []
# ------------
NLTK_StopWords = stopwords.words('indonesian')
# print(NLTK_StopWords)
NLTK_StopWords.extend(["detik", "detikjatim", "detikjateng", "detikjabar", "detiksulsel", "detiksumbar", "detikbali",
                      "detikpapua", "detiksulteng", "detikmaluku", "detjatim", "detikcom", "allahumma", "aamiin", "allah", "bismillah"])
NLTK_StopWords.extend(["yg", "dg", "rt", "dgn", "ny", "d", 'klo',
                       'kalo', 'amp', 'biar', 'bikin', 'bilang',
                       'gak', 'ga', 'krn', 'nya', 'nih', 'sih',
                       'si', 'tau', 'tdk', 'tuh', 'utk', 'ya',
                       'jd', 'jgn', 'sdh', 'aja', 'n', 't',
                       'nyg', 'hehe', 'pen', 'u', 'nan', 'loh', 'rt',
                       '&amp', 'yah'])
# txt_stopword = pd.read_csv(PATH + kecelakaan + "stopwords.txt", names= ["stopwords"], header = None)
# NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
# for lda ----
txt_stopword = pd.read_csv(PATH + kecelakaan + "stopwords_add_v1.txt", names= ["stopwords"], header = None)
NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
# txt_stopword = pd.read_csv(PATH + kecelakaan + "stopwords_add_v2.txt", names= ["stopwords"], header = None)
# NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
# txt_stopword = pd.read_csv(PATH + kecelakaan + "stopwords_add_v3.txt", names= ["stopwords"], header = None)
# NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
# ------------
# convert stopword string to list & append additional stopword
# NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))

NLTK_StopWords = set(NLTK_StopWords)

In [180]:
def preprocessing(berita):
        s = str(berita)
        s = s.lower()
        s = s.replace('\n', ' ')
        s = s.replace('\r', ' ')
        # s = re.sub(r'[^a-zA-Z0-9\s]', ' ', s)
        # for lda ----
        s = re.sub(r'[^a-zA-Z\s]', ' ', s)
        # ------------
        tokens = [token for token in s.split(" ") if token != ""]
        T = [t for t in tokens if (
            (t in excluded_words) or (t not in NLTK_StopWords))]
        return T

In [181]:
old_kecelakaan = old_kecelakaan.dropna(subset=['desc'])
old_kecelakaan.sort_values('desc', inplace=True)
old_kecelakaan.drop_duplicates(subset='desc', keep=False, inplace=True)
df_train, df_test = train_test_split(old_kecelakaan,test_size=0.1)
print(len(df_train))

old_kecelakaan.head()

1891


title  \
4546   10 Korban Ledakan di Sawahlunto Dapat Manfaat ...   
4448   BPJS Ketenagakerjaan Luncurkan Fitur e-Klaim u...   
4951   Ahli Waris Terima Santunan dari Asabri, Briptu...   
10674  Penyidikan Kasus Kecelakaan Muara Rapak Balikp...   
10694  Truk Oleng Tabrak Motor dan Tiang Listrik di B...   

                               date  \
4546   Kamis, 15 Des 2022 21:03 WIB   
4448   Kamis, 15 Des 2022 18:08 WIB   
4951    Rabu, 30 Nov 2022 17:33 WIB   
10674   Rabu, 28 Des 2022 17:16 WIB   
10694  Jumat, 06 Jan 2023 12:52 WIB   

                                                    desc          source  
4546    Badan Penyelenggara Jaminan Sosial (BPJS) Ket...  www.kompas.com  
4448    Badan Penyelenggara Jaminan Sosial (BPJS) Ket...  www.kompas.com  
4951    Briptu Muh Khoirul Anam, mekanik atau teknisi...  www.kompas.com  
10674   Ditlantas Polda Kaltim melakukan olah Tempat ...  www.kompas.com  
10694   Dua orang tewas di tempat kejadian dalam kece...  www.kompas.com

In [182]:
for x in range(0, old_kecelakaan.shape[0]):
    text = preprocessing(old_kecelakaan.iloc[x, -2])
    old_kecelakaan.iloc[x, -2] = (' '.join(text))

for x in range(0, old_kecelakaan.shape[0]):
    text = preprocessing(old_kecelakaan.iloc[x, -4])
    old_kecelakaan.iloc[x, -4] = (' '.join(text)) 
old_kecelakaan.head()

title  \
4546   korban ledakan sawahlunto manfaat jaminan sosi...   
4448   bpjs ketenagakerjaan luncurkan fitur e klaim b...   
4951   ahli waris terima santunan asabri briptu khoir...   
10674  penyidikan kecelakaan muara rapak balikpapan d...   
10694  truk oleng tabrak motor tiang listrik blitar k...   

                               date  \
4546   Kamis, 15 Des 2022 21:03 WIB   
4448   Kamis, 15 Des 2022 18:08 WIB   
4951    Rabu, 30 Nov 2022 17:33 WIB   
10674   Rabu, 28 Des 2022 17:16 WIB   
10694  Jumat, 06 Jan 2023 12:52 WIB   

                                                    desc          source  
4546   badan penyelenggara jaminan sosial bpjs ketena...  www.kompas.com  
4448   badan penyelenggara jaminan sosial bpjs ketena...  www.kompas.com  
4951   briptu muh khoirul anam mekanik teknisi tewas ...  www.kompas.com  
10674  ditlantas polda kaltim olah kejadian perkara t...  www.kompas.com  
10694  tewas kejadian kecelakaan melibatkan truk peng...  www.kompas.com

## YAKE TFIDF BERT

## MAIN COURSE

## LDA

In [183]:
import gensim
from gensim import corpora
from collections import Counter
import pyLDAvis.gensim
import pickle 
import pyLDAvis
from nltk.tokenize import word_tokenize 
from nltk.probability import FreqDist

def remove_number(text):
    return  re.sub(r"\d+", "", text)

In [184]:
new_kecelakaan = old_kecelakaan[['title', 'desc']]
new_kecelakaan['desc'] = new_kecelakaan['desc'].apply(remove_number)
new_kecelakaan['desc'] = new_kecelakaan['desc'].apply(word_tokenize)
new_kecelakaan['desc'] = [[token for token in doc if len(token) > 2] for doc in new_kecelakaan['desc']]
new_kecelakaan['title'] = new_kecelakaan['title'].apply(remove_number)
new_kecelakaan['title'] = new_kecelakaan['title'].apply(word_tokenize)
new_kecelakaan['title'] = [[token for token in doc if len(token) > 2] for doc in new_kecelakaan['title']]
new_kecelakaan['fdist'] = new_kecelakaan['desc'].apply(FreqDist)

print(len(new_kecelakaan))
print(new_kecelakaan.head(2))

print('Frequency Tokens : \n') 
print(new_kecelakaan['fdist'].head().apply(lambda x : x.most_common()))

2102
                                                  title  \
4546  [korban, ledakan, sawahlunto, manfaat, jaminan...   
4448  [bpjs, ketenagakerjaan, luncurkan, fitur, klai...   

                                                   desc  \
4546  [badan, penyelenggara, jaminan, sosial, bpjs, ...   
4448  [badan, penyelenggara, jaminan, sosial, bpjs, ...   

                                                  fdist  
4546  {'badan': 1, 'penyelenggara': 1, 'jaminan': 12...  
4448  {'badan': 2, 'penyelenggara': 1, 'jaminan': 4,...  
Frequency Tokens : 

4546     [(ketenagakerjaan, 14), (jaminan, 12), (bpjs, ...
4448     [(bpjs, 15), (ketenagakerjaan, 14), (pmi, 12),...
4951     [(khoirul, 7), (tewas, 4), (briptu, 3), (anam,...
10674    [(truk, 8), (kaltim, 4), (sopir, 4), (menabrak...
10694    [(truk, 17), (supriyadi, 6), (kecelakaan, 5), ...
Name: fdist, dtype: object


In [185]:
from gensim.models import Phrases
bigram = Phrases(new_kecelakaan['desc'], min_count=20)
for idx in range(len(new_kecelakaan['desc'])):
    for token in bigram[new_kecelakaan['desc'].iloc[idx]]:
        if '_' in token:
            # Token is a bigram, add to document.
            new_kecelakaan['desc'].iloc[idx].append(token)
            word1, word2 = token.split("_")
            must_remove = ('kereta')
            if word1 not in must_remove:
                new_kecelakaan['desc'].iloc[idx].remove(word1)
            if word2 not in must_remove:
                new_kecelakaan['desc'].iloc[idx].remove(word2)
            # print(token)

In [476]:
dictionary = corpora.Dictionary(new_kecelakaan['desc'])
dictionary.filter_extremes(no_below=35, no_above=0.5)
print(dictionary)

corpus = [dictionary.doc2bow(berita) for berita in new_kecelakaan['desc']]

Dictionary<1044 unique tokens: ['alam', 'apapun', 'badan', 'bentuk', 'bergerak']...>


In [477]:
# Creating the object for LDA model using gensim library
Lda = gensim.models.ldamodel.LdaModel

total_topics = 5 # jumlah topik yang akan di extract
number_words = 30 # jumlah kata per topik

In [478]:
import os
from gensim.test.utils import datapath
the_path = PATH + kecelakaan + "model/lda_model" + "_" + str(total_topics) + "_" + str(number_words)
if not os.path.exists(the_path):
    os.mkdir(the_path)
temp_file = datapath(the_path + "/lda_model")
#if new
# lda_model = Lda(corpus, num_topics=total_topics, id2word=dictionary, passes=50, random_state=1)
# lda_model.save(temp_file)
# load
from gensim import models
lda_model = models.ldamodel.LdaModel.load(temp_file)

lda_model.show_topics(num_topics=total_topics, num_words=number_words)

[(0,
  '0.032*"bus" + 0.029*"truk" + 0.025*"mobil" + 0.023*"warga" + 0.021*"mengalami_luka" + 0.019*"sopir" + 0.018*"kejadian" + 0.016*"penumpang" + 0.015*"menabrak" + 0.013*"mengalami" + 0.011*"luka" + 0.011*"tewas" + 0.011*"kendaraan" + 0.010*"selamat" + 0.010*"dikemudikan" + 0.010*"minibus" + 0.009*"surabaya" + 0.009*"akibat" + 0.008*"jawa" + 0.008*"diduga" + 0.008*"kondisi" + 0.008*"meninggal_dunia" + 0.008*"rumah" + 0.007*"akp" + 0.007*"polisi" + 0.006*"posisi" + 0.006*"semarang" + 0.006*"tol" + 0.006*"meninggal" + 0.006*"bambang"'),
 (1,
  '0.039*"kendaraan" + 0.038*"mobil" + 0.024*"truk" + 0.015*"arah" + 0.013*"pengemudi" + 0.012*"jalur" + 0.012*"lintas" + 0.012*"jakarta" + 0.010*"peristiwa" + 0.009*"kondisi" + 0.009*"korban_jiwa" + 0.007*"jaya" + 0.007*"rusak" + 0.007*"jalan_raya" + 0.007*"diduga" + 0.007*"kemacetan" + 0.006*"bogor" + 0.006*"pengendara" + 0.006*"tol" + 0.006*"kanan" + 0.006*"lubang" + 0.005*"pagi" + 0.005*"cianjur" + 0.005*"tni" + 0.005*"kecelakaan_beruntun" + 

In [479]:
# Word Count of Topic Keywords

from collections import Counter
topics = lda_model.show_topics(formatted=False, num_topics=total_topics, num_words=number_words)
# topic = lda_model.show_topics(num_topics=total_topics, num_words=number_words)
# print((topics[0]))
# print((topic[0]))
data_flat = [w for w_list in new_kecelakaan['desc'] for w in w_list]
counter = Counter(data_flat)

out = []
for i, topic in topics:
    for word, weight in topic:
        out.append([word, i , weight, counter[word]])

df_imp_wcount = pd.DataFrame(out, columns=['word', 'id', 'importance', 'word_count']) 
print(df_imp_wcount)

               word  id  importance  word_count
0               bus   0    0.032481        1088
1              truk   0    0.028739        1732
2             mobil   0    0.025130        2820
3             warga   0    0.022951        1664
4    mengalami_luka   0    0.020682         810
..              ...  ..         ...         ...
145           kanan   4    0.007097         449
146       pengemudi   4    0.007043         638
147      berinisial   4    0.006731         279
148          akibat   4    0.006432         640
149           sopir   4    0.006424         675

[150 rows x 4 columns]


In [375]:
def format_topics_sentences(ldamodel=None, corpus=corpus, texts=new_kecelakaan['desc']):
    # Init output
    sent_topics_df = pd.DataFrame()
    # print(len(ldamodel[corpus]))

    dom = []
    perc = []
    keywords = []
    # Get main topic in each document
    for i, row_list in enumerate(ldamodel[corpus]):
        row = row_list[0] if ldamodel.per_word_topics else row_list            
        row = sorted(row, key=lambda x: (x[1]), reverse=True)
        # print(len(row))

        # Get the Dominant topic, Perc Contribution and Keywords for each document
        for j, (topic_num, prop_topic) in enumerate(row):
            if j == 0:  # => dominant topic
                wp = ldamodel.show_topic(topic_num, topn=number_words)
                topic_keywords = ", ".join([word for word, prop in wp])
                dom.append(int(topic_num))
                perc.append(round(prop_topic,4))
                keywords.append(topic_keywords)
                # sent_topics_df = pd.concat([sent_topics_df, pd.DataFrame([pd.Series([int(topic_num), round(prop_topic,4), topic_keywords])])], ignore_index=True)
                # sent_topics_df = sent_topics_df.append(pd.Series([int(topic_num), round(prop_topic,4), topic_keywords]), ignore_index=True)
            else:
                break
    # print(len(sent_topics_df))
    sent_topics_df['Dominant_Topic'] = dom
    sent_topics_df['Perc_Contribution'] = perc
    sent_topics_df['Topic_Keywords'] = keywords
    # sent_topics_df.columns = ['Dominant_Topic', 'Perc_Contribution', 'Topic_Keywords']

    # Add original text to the end of the output
    # sent_topics_df['Texts']= texts
    # print(len(sent_topics_df))
    return(sent_topics_df)

In [480]:
df_topic_sents_keywords = format_topics_sentences(ldamodel=lda_model, corpus=corpus, texts=new_kecelakaan['desc'])
df_topic_sents_keywords['Texts'] = 0
df_topic_sents_keywords['Title'] = 0

In [481]:
df_dominant_topic = df_topic_sents_keywords.reset_index()
# texts = []
for i in range(len(new_kecelakaan['desc'])):
    # print(new_kecelakaan['desc'].iloc[i])
    # texts.append(new_kecelakaan['desc'].iloc[i])
    df_dominant_topic['Texts'].iloc[i] = new_kecelakaan['desc'].iloc[i]
    df_dominant_topic['Title'].iloc[i] = new_kecelakaan['title'].iloc[i]
# df_dominant_topic['Texts'] = texts
df_dominant_topic.columns = ['Document_No', 'Dominant_Topic', 'Topic_Perc_Contrib', 'Keywords', 'Text', 'Title']

# df_topic_sents_keywords['Texts'].isna().value_counts()
df_dominant_topic.head(5)
df_dominant_topic.tail(5)

Document_No  Dominant_Topic  Topic_Perc_Contrib  \
2097         2097               0              0.7521   
2098         2098               3              0.5777   
2099         2099               4              0.9873   
2100         2100               3              0.3887   
2101         2101               1              0.9921   

                                               Keywords  \
2097  bus, truk, mobil, warga, mengalami_luka, sopir...   
2098  kereta, kejadian, kereta_api, warga, api, tert...   
2099  motor, mobil, kejadian, menabrak, sepeda_motor...   
2100  kereta, kejadian, kereta_api, warga, api, tert...   
2101  kendaraan, mobil, truk, arah, pengemudi, jalur...   

                                                   Text  \
2097  [pengangkut, beton, kecelakaan, jakarta, tange...   
2098  [warga, jakarta, pasukan, oranye, petugas, pen...   
2099  [warga, kendal, bernama, rozikin, tewas, jalan...   
2100  [warga, rote, ndao, mct, milik, kimia, farma, ...   
2101  [buah, logistik, bantuan, gempa, puncak, cilot...   

                                                  Title  
2097  [truk, tronton, hantam, tiang, pembatas, jalan...  
2098  [pasukan, oranye, semudah, ancaman, tertabrak,...  
2099  [guru, kendal, tewas, terlindas, truk, semaran...  
2100  [kronologi, pasien, berkursi, roda, tewas, dit...  
2101  [truk, pengangkut, bantuan, korban, gempa, cia...

In [23]:
df_dominant_topic.to_csv(PATH + kecelakaan + 'df_dominant_topic.csv')

In [24]:
from datetime import datetime
now = datetime.now() # current date and time
date_time = now.strftime("%m-%d-%Y_%H-%M-%S")
print("date and time:",date_time)
LDAvis_html = 'ldavis_prepared_'+ str(total_topics)+"_"+str(number_words)+"_"+str(date_time)
LDAvis_prepared = pyLDAvis.gensim.prepare(lda_model, corpus, dictionary)
with open(PATH + kecelakaan + LDAvis_html, 'wb') as f:
        pickle.dump(LDAvis_prepared, f)
pyLDAvis.save_html(LDAvis_prepared, PATH + kecelakaan + LDAvis_html +'.html')

date and time: 06-24-2023_06-11-53


In [25]:
with open(PATH + kecelakaan + LDAvis_html, 'rb') as f:
    LDAvis_prepared = pickle.load(f)

In [381]:
lda_what_kecelakaan = []
word_topics = set(df_imp_wcount['word'].values)
for i in range(len(df_dominant_topic)):
    val = []
    for n, key in enumerate(word_topics):
        if key in df_dominant_topic['Text'].iloc[i]:
            val.append(key)
    lda_what_kecelakaan.append(val)

print(lda_what_kecelakaan)

[['kepala', 'keluarga', 'tim', 'meninggal_dunia', 'kerja', 'meninggal', 'terkait', 'langsung'], ['bernama', 'meninggal_dunia', 'kerja', 'terkait', 'informasi', 'mengalami'], ['kepala', 'keluarga', 'jenazah', 'tewas', 'meninggal', 'langsung'], ['sopir', 'menabrak', 'truk', 'tersangka', 'polisi', 'bernama', 'meninggal_dunia', 'pengemudi', 'kendaraan', 'diduga'], ['sopir', 'menabrak', 'truk', 'sepeda_motor', 'mengalami_luka', 'jenazah', 'dikendarai', 'kondisi', 'arah', 'bernama', 'kejadian', 'pagi', 'kepolisian', 'pengemudi', 'dikemudikan', 'tewas', 'meter', 'akibat', 'rumah_sakit', 'diduga'], ['sopir', 'kepala', 'menabrak', 'warga', 'mengalami_luka', 'bus', 'polres', 'mobil', 'laporan', 'bernama', 'bambang', 'meninggal_dunia', 'dikemudikan', 'pulang', 'pelajar', 'meninggal', 'surabaya', 'posisi', 'luka', 'langsung', 'peristiwa', 'rumah_sakit', 'kendaraan', 'akp', 'kanan', 'mengalami'], ['sopir', 'kepala', 'menabrak', 'warga', 'mengalami_luka', 'bus', 'sakit', 'polres', 'mobil', 'kondisi'

In [382]:
lda_title_what = []
word_topics = set(df_imp_wcount['word'].values)
for i in range(len(df_dominant_topic)):
    val = []
    for n, key in enumerate(word_topics):
        if key in df_dominant_topic['Title'].iloc[i]:
            val.append(key)
    lda_title_what.append(val)

print(lda_title_what)

[[], [], [], ['meninggal'], ['truk', 'tewas', 'motor'], ['mobil', 'pelajar', 'meninggal'], ['mobil', 'meninggal', 'selamat'], ['jalur', 'tewas', 'luka', 'jakarta'], ['meninggal'], ['truk', 'tewas'], ['tewas', 'pelajar'], ['kereta', 'api', 'tewas', 'pelajar'], ['tewas', 'motor', 'kendaraan'], [], ['warga', 'tewas', 'diduga'], ['kepala', 'pulang', 'tol', 'jakarta'], ['tewas', 'diduga'], ['sopir', 'diduga'], ['tewas', 'motor'], ['tni', 'tewas', 'pelajar', 'anggota'], ['tewas', 'motor'], ['pelajar', 'meninggal'], ['motor', 'peristiwa'], ['pengendara', 'tewas', 'motor'], ['kereta', 'api', 'tewas', 'pelajar', 'ditemukan'], ['saksi', 'polisi', 'pelaku'], ['kapal', 'tewas', 'ditemukan'], ['truk'], ['tewas', 'diduga'], ['tersangka', 'tewas', 'jaya'], ['tewas'], ['keluarga', 'tewas'], ['keluarga', 'jenazah'], ['truk', 'lintas', 'tol'], [], ['tersangka', 'tewas'], ['truk'], ['penumpang', 'kapal', 'selamat'], ['pengendara', 'tewas'], ['truk', 'kemacetan', 'tol', 'jakarta'], ['lintas', 'tewas'], ['

In [383]:
for n, word_list in enumerate(lda_title_what):
    val = []
    for word in word_list:
        if word in lda_what_kecelakaan[n]:
            continue
        val.append(word)
    lda_what_kecelakaan[n].extend(val)
    # if val:
    #     print(n)
    #     print(val)

print(lda_what_kecelakaan)

[['kepala', 'keluarga', 'tim', 'meninggal_dunia', 'kerja', 'meninggal', 'terkait', 'langsung'], ['bernama', 'meninggal_dunia', 'kerja', 'terkait', 'informasi', 'mengalami'], ['kepala', 'keluarga', 'jenazah', 'tewas', 'meninggal', 'langsung'], ['sopir', 'menabrak', 'truk', 'tersangka', 'polisi', 'bernama', 'meninggal_dunia', 'pengemudi', 'kendaraan', 'diduga', 'meninggal'], ['sopir', 'menabrak', 'truk', 'sepeda_motor', 'mengalami_luka', 'jenazah', 'dikendarai', 'kondisi', 'arah', 'bernama', 'kejadian', 'pagi', 'kepolisian', 'pengemudi', 'dikemudikan', 'tewas', 'meter', 'akibat', 'rumah_sakit', 'diduga', 'motor'], ['sopir', 'kepala', 'menabrak', 'warga', 'mengalami_luka', 'bus', 'polres', 'mobil', 'laporan', 'bernama', 'bambang', 'meninggal_dunia', 'dikemudikan', 'pulang', 'pelajar', 'meninggal', 'surabaya', 'posisi', 'luka', 'langsung', 'peristiwa', 'rumah_sakit', 'kendaraan', 'akp', 'kanan', 'mengalami'], ['sopir', 'kepala', 'menabrak', 'warga', 'mengalami_luka', 'bus', 'sakit', 'polre

In [384]:
idxs = []
idxs_tp = []
idxs_tn = []
idxs_lda = [] #not in lda words
total = 0
total_tp = 0
total_tn = 0
total_lda = 0
check_lda = ('mobil', 'motor', 'truk', 'bus', 'kereta', 'mengalami', 'pengendara_sepeda',
             'sepeda_motor', 'kapal', 'minibus', 'luka' , 'mengalami_luka',
             'meninggal', 'meninggal_dunia', 'pengemudi', 'kendaraan', 'polisi',
             'penumpang', 'tewas', 'pengendara', 'korban_jiwa', 'lintas', 'pelaku')
for i in range(len(lda_what_kecelakaan)):
    flag = True
    deflag = True
    ldaf = True
    for token in lda_what_kecelakaan[i]:
        if token in check_lda:
            flag = False
        if token in df_imp_wcount['word'].values:
            ldaf = False
    for token in df_dominant_topic['Text'].iloc[i]:
        if token in check_lda:
            deflag = False
    for token in df_dominant_topic['Title'].iloc[i]:
        if token in check_lda:
            deflag = False
    if flag != deflag:
        total += 1
        idxs.append(i)
    elif flag == deflag and flag == False:
        total_tp += 1
        idxs_tp.append(i)
    elif flag == deflag and flag == True:
        total_tn += 1
        idxs_tn.append(i)
    if ldaf:
        total_lda += 1
        idxs_lda.append(i)
print(len(df_dominant_topic))
print(total)
print(total_tp)
print(total_tn)
print(total_lda)


2102
0
2006
96
3


In [32]:
lda_check = []
for word in check_lda:
    if word not in df_imp_wcount['word'].values:
        lda_check.append(word)
print(lda_check)

[]


In [39]:
print(idxs_tn)

[32, 64, 88, 98, 100, 107, 115, 202, 216, 219, 236, 284, 293, 304, 325, 328, 368, 373, 383, 389, 390, 412, 413, 423, 465, 468, 490, 493, 497, 499, 500, 501, 506, 525, 530, 534, 546, 548, 589, 593, 628, 630, 632, 793, 863, 866, 885, 904, 923, 924, 940, 972, 977, 979, 980, 981, 982, 983, 984, 986, 987, 989, 1011, 1058, 1074, 1079, 1087, 1090, 1098, 1101, 1102, 1105, 1106, 1116, 1119, 1124, 1155, 1184, 1185, 1193, 1213, 1214, 1303, 1325, 1346, 1370, 1428, 1523, 1532, 1784, 1876, 1885, 1891, 1897, 1899, 2086]


In [40]:
# text  = preprocessing(old_kecelakaan['desc'][old_kecelakaan['desc'].str.find('hari') != -1].iloc[0])
# text
i = idxs_tn[0]
print(df_dominant_topic['Keywords'].iloc[i])
print(type(df_dominant_topic['Keywords'].iloc[i]))
print(df_dominant_topic['Text'].iloc[i])
print(type(df_dominant_topic['Text'].iloc[i]))
print(df_dominant_topic['Keywords'].iloc[i].split(", "))
print(lda_what_kecelakaan[i])


polisi, pelaku, kapal, tersangka, keluarga, warga, hasya, mengaku, anggota, kejadian, laporan, ditemukan, laut, diduga, rumah_sakit, mobil, kepolisian, mengalami, langsung, terkait, air, polres, bernama, jenazah, informasi, penumpang, suaminya, pasal, anaknya, pulang
<class 'str'>
['jenazah', 'korban', 'kecelakaan', 'helikopter', 'jakarta', 'prabowo', 'korban', 'kecelakaan', 'helikopter', 'diserahkan', 'udara', 'pondok', 'cabe', 'tangerang', 'rencananya', 'siang', 'diberangkatkan', 'rumah', 'keluarga', 'melaksanakan', 'upacara', 'penyerahan', 'jenazah', 'lanjutkan', 'persiapan', 'pengantaran', 'jenazah', 'keluarga', 'wartawan', 'jenazah', 'diserahkan', 'bripda', 'choirul', 'anam', 'briptu', 'lasminto', 'berdasarkan', 'pemantauan', 'tempo', 'korban', 'disalatkan', 'karangan', 'bunga', 'tersusun', 'rapih', 'bertuliskan', 'berdukacita', 'lheli', 'nbo', 'prosesi', 'upacara', 'pemberangkatan', 'jenazah', 'keluarga', 'aman', 'helikopter', 'polairud', 'milik', 'polri', 'diawaki', 'kapten', 'b

In [386]:
before_what_kecelakaan = old[old['berita_topik_id'] == 3]
before_what_kecelakaan = before_what_kecelakaan[['berita_title', 'qe_what', 'berita_desc']]
before_what_kecelakaan = before_what_kecelakaan.dropna(subset=['berita_desc'])
before_what_kecelakaan.sort_values('berita_desc', inplace=True)
before_what_kecelakaan.drop_duplicates(subset='berita_desc', keep=False, inplace=True)
# print(before_what_kecelakaan)
# print(before_what_kecelakaan['qe_what'].iloc[i])
# print(before_what_kecelakaan['berita_title'].iloc[i])
# print(before_what_kecelakaan['berita_desc'].iloc[i])

In [389]:
total_empty = 0
empty_val = []
idxs_total = []
idxs_total.extend(idxs_tp)
idxs_total.extend(idxs_tn)
idxs_total = set(idxs_total)
with open(PATH + kecelakaan + 'true_negative_' + str(total_topics) +'.txt', 'w', encoding='UTF8') as f:
    nl = "\n"
    dashes = '--------------------------------------'
    for x in idxs_total:
        f.write(dashes + nl)
        f.write(before_what_kecelakaan['berita_title'].iloc[x] + nl)
        f.write(str(before_what_kecelakaan['qe_what'].iloc[x]) + nl)
        f.write(str(lda_what_kecelakaan[x]) + nl)
        # print(before_what_kecelakaan['berita_title'].iloc[x])
        # print(before_what_kecelakaan['qe_what'].iloc[x])
        # print(lda_what_kecelakaan[x])

        if len(lda_what_kecelakaan[x])<5:
            total_empty += 1
            empty_val.append(x)

print(total_empty)
print(empty_val)


91
[41, 50, 88, 100, 107, 133, 137, 202, 203, 219, 241, 254, 268, 275, 279, 281, 288, 304, 327, 328, 382, 383, 423, 465, 468, 488, 489, 493, 500, 501, 506, 544, 561, 574, 588, 589, 596, 639, 691, 866, 869, 914, 924, 940, 972, 977, 979, 980, 981, 982, 983, 984, 986, 987, 988, 989, 991, 1001, 1079, 1082, 1090, 1105, 1106, 1116, 1123, 1124, 1156, 1185, 1192, 1194, 1214, 1222, 1278, 1296, 1326, 1415, 1420, 1428, 1430, 1594, 1607, 1696, 1716, 1802, 1876, 1892, 1897, 1899, 1912, 1984, 1987]


In [44]:
hitung = Counter()
for i in idxs_lda:
    hitung.update(lda_what_kecelakaan[i])
    # hitung.update(lda_title_what[i])
    print('--------------------------------------')
    print(before_what_kecelakaan['berita_title'].iloc[i])
    print(before_what_kecelakaan['berita_desc'].iloc[i])
    print(before_what_kecelakaan['qe_what'].iloc[i])
    print(lda_what_kecelakaan[i])
hitung

--------------------------------------
Alasan Punya 14 Anak Bikin Eks Presiden ACT Ahyudin Minta Dibebaskan
\-

Mantan Presiden Aksi Cepat Tanggap (ACT), Ahyudin, meminta hakim
membebaskannya. Ahyudin minta dibebaskan karena memiliki 14 anak.

"Terdakwa adalah tulang punggung puluhan keluarganya, memiliki 14 anak yang
masih kecil-kecil semua yang masih membutuhkan kasih sayang seorang bapak dan
juga biaya pendidikan serta kesehatan yang harus disiapkan oleh terdakwa,"
kata pengacara Ahyuddin, Irfan Junaedi saat membacakan pleidoi dalam sidang,
Selasa (3/1/2023) kemarin.

Karena itu, Irfan meminta kliennya dibebaskan. Irfan meminta hakim menerima
nota pembelaan atau pleidoi kliennya.

"Kami penasihat hukum terdakwa memohon dengan segala hormat kepada majelis
hakim Yang Mulia, yang memeriksa dan mengadili perkara a quo, kiranya berkenan
memutus yang amarnya menerima nota pembelaan (pleidoi) penasihat hukum
terdakwa menyatakan menolak dakwaan dan/atau tuntutan jaksa penuntut umum
secara k

Counter()

In [482]:
df_result_lda = df_dominant_topic[['Title', 'Text']]
df_result_lda['what_lda'] = lda_what_kecelakaan
df_result_lda['what_qe'] = 0
df_result_lda['title_old'] = 0
df_result_lda['desc_old'] = 0
for i in range(len(df_result_lda)):
    df_result_lda['what_qe'].iloc[i] = before_what_kecelakaan['qe_what'].iloc[i]
    df_result_lda['title_old'].iloc[i] = before_what_kecelakaan['berita_title'].iloc[i]
    df_result_lda['desc_old'].iloc[i] = before_what_kecelakaan['berita_desc'].iloc[i]

# df_result_lda.to_csv(PATH + kecelakaan + 'df_result_lda.csv')   
df_result_lda.to_excel(PATH + kecelakaan + 'df_result_lda.xlsx', index=None) 
df_result_lda
# print(before_what_kecelakaan['qe_what'].iloc[0])

Title  \
0     [korban, ledakan, sawahlunto, manfaat, jaminan...   
1     [bpjs, ketenagakerjaan, luncurkan, fitur, klai...   
2     [ahli, waris, terima, santunan, asabri, briptu...   
3     [penyidikan, kecelakaan, muara, rapak, balikpa...   
4     [truk, oleng, tabrak, motor, tiang, listrik, b...   
...                                                 ...   
2097  [truk, tronton, hantam, tiang, pembatas, jalan...   
2098  [pasukan, oranye, semudah, ancaman, tertabrak,...   
2099  [guru, kendal, tewas, terlindas, truk, semaran...   
2100  [kronologi, pasien, berkursi, roda, tewas, dit...   
2101  [truk, pengangkut, bantuan, korban, gempa, cia...   

                                                   Text  \
0     [badan, penyelenggara, tim, layanan, lct, jemp...   
1     [badan, penyelenggara, meluncurkan, fitur, ber...   
2     [briptu, muh, mekanik, teknisi, tewas, kecelak...   
3     [kaltim, turunan, muara, rapak, balikpapan, ti...   
4     [kejadian, pasir, kedawung, nglegok, blitar, p...   
...                                                 ...   
2097  [pengangkut, beton, kecelakaan, jakarta, tange...   
2098  [warga, jakarta, pasukan, oranye, petugas, pen...   
2099  [warga, kendal, bernama, rozikin, tewas, jalan...   
2100  [warga, rote, ndao, mct, milik, kimia, farma, ...   
2101  [buah, logistik, bantuan, gempa, puncak, cilot...   

                                               what_lda  \
0     [kepala, keluarga, tim, meninggal_dunia, kerja...   
1     [bernama, meninggal_dunia, kerja, terkait, inf...   
2     [kepala, keluarga, jenazah, tewas, meninggal, ...   
3     [sopir, menabrak, truk, tersangka, polisi, ber...   
4     [sopir, menabrak, truk, sepeda_motor, mengalam...   
...                                                 ...   
2097  [sopir, kepala, truk, mengalami_luka, arah, ke...   
2098  [pengendara, warga, tim, kemacetan, kejadian, ...   
2099  [kepala, pengendara, warga, sepeda_motor, meng...   
2100  [sopir, keluarga, menabrak, warga, sepeda_moto...   
2101  [korban_jiwa, menabrak, truk, bogor, jalur, me...   

                                                what_qe  \
0     kecelakaan, orang, korban, meninggal, hasil, k...   
1     kecelakaan, akibat, orang, meninggal, mengalam...   
2     kecelakaan, orang, meninggal, langsung, iptu, ...   
3     truk, salah, korban, rs, pengemudi, pemeriksaa...   
4     tertabrak, truk, pemotor, korban, kejadian, al...   
...                                                 ...   
2097  kejadian, kecelakaan, kendaraan, tol, pengemud...   
2098  kejadian, kendaraan, pengendara, kemacetan, ko...   
2099  kejadian, kecelakaan, kendaraan, pengendara, l...   
2100  kejadian, kecelakaan, akibat, tertabrak, lokas...   
2101  kecelakaan, penanganan, kendaraan, berlawanan,...   

                                              title_old  \
0     10 Korban Ledakan di Sawahlunto Dapat Manfaat ...   
1     BPJS Ketenagakerjaan Luncurkan Fitur e-Klaim u...   
2     Ahli Waris Terima Santunan dari Asabri, Briptu...   
3     Penyidikan Kasus Kecelakaan Muara Rapak Balikp...   
4     Truk Oleng Tabrak Motor dan Tiang Listrik di B...   
...                                                 ...   
2097  Truk Tronton Hantam Tiang dan Pembatas Jalan T...   
2098  Jadi Pasukan Oranye Tak Semudah Kelihatannya, ...   
2099  Guru Asal Kabupaten Kendal Tewas Terlindas Tru...   
2100  Kronologi Pasien Berkursi Roda Tewas Ditabrak ...   
2101  Truk Pengangkut Bantuan untuk Korban Gempa Cia...   

                                               desc_old  
0      Badan Penyelenggara Jaminan Sosial (BPJS) Ket...  
1      Badan Penyelenggara Jaminan Sosial (BPJS) Ket...  
2      Briptu Muh Khoirul Anam, mekanik atau teknisi...  
3      Ditlantas Polda Kaltim melakukan olah Tempat ...  
4      Dua orang tewas di tempat kejadian dalam kece...  
...                                                 ...  
2097  \- Truk tronton pengangkut beton mengalami kec...  
2098  \- Warga Jakarta mana tidak mengeta

# Kesehatan

In [154]:
old_kesehatan = old[old['berita_topik_id'] == 4]
old_kesehatan = old_kesehatan[['berita_title', 'berita_date', 'berita_desc', 'berita_source']]
old_kesehatan.rename(columns = {'berita_title':'title', 'berita_date':'date', 'berita_desc':'desc', 'berita_source':'source'}, inplace=True)
print(old_kesehatan.shape)
old_kesehatan.head(2)

(1309, 4)


title  \
5250  Ramalan Zodiak Aries Hari Ini, 2 Desember 2022...   
5251  Ramalan Zodiak Sagitarius Besok, 6 Desember 20...   

                              date  \
5250  Jumat, 02 Des 2022 08:35 WIB   
5251  Senin, 05 Des 2022 14:55 WIB   

                                                   desc              source  
5250  \- Simak ramalan zodiak Aries hari ini, 2 Dese...  www.tribunnews.com  
5251  \- Inilah ramalan zodiak Sagitarius untuk beso...  www.tribunnews.com

## Preprocess

In [155]:
from keybert import KeyBERT
from sentence_transformers import SentenceTransformer
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.metrics.pairwise import cosine_similarity

In [156]:
# previous way

# nltk.download('punkt')
# nltk.download('stopwords')

excluded_words = ["tempat", "waktu", "hari"]
# for lda ----
excluded_words = []
# ------------
NLTK_StopWords = stopwords.words('indonesian')
# print(NLTK_StopWords)
NLTK_StopWords.extend(["detik", "detikjatim", "detikjateng", "detikjabar", "detiksulsel", "detiksumbar", "detikbali",
                      "detikpapua", "detiksulteng", "detikmaluku", "detjatim", "detikcom", "allahumma", "aamiin", "allah", "bismillah"])
NLTK_StopWords.extend(["yg", "dg", "rt", "dgn", "ny", "d", 'klo',
                       'kalo', 'amp', 'biar', 'bikin', 'bilang',
                       'gak', 'ga', 'krn', 'nya', 'nih', 'sih',
                       'si', 'tau', 'tdk', 'tuh', 'utk', 'ya',
                       'jd', 'jgn', 'sdh', 'aja', 'n', 't',
                       'nyg', 'hehe', 'pen', 'u', 'nan', 'loh', 'rt',
                       '&amp', 'yah'])
# txt_stopword = pd.read_csv(PATH + kesehatan + "stopwords.txt", names= ["stopwords"], header = None)
# NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
# for lda ----
txt_stopword = pd.read_csv(PATH + kesehatan + "stopwords_add_v1.txt", names= ["stopwords"], header = None)
NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
# txt_stopword = pd.read_csv(PATH + kesehatan + "stopwords_add_v2.txt", names= ["stopwords"], header = None)
# NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
# txt_stopword = pd.read_csv(PATH + kesehatan + "stopwords_add_v3.txt", names= ["stopwords"], header = None)
# NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
# ------------
# convert stopword string to list & append additional stopword
# NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))

NLTK_StopWords = set(NLTK_StopWords)

In [157]:
def preprocessing(berita):
        s = str(berita)
        s = s.lower()
        s = s.replace('\n', ' ')
        s = s.replace('\r', ' ')
        # s = re.sub(r'[^a-zA-Z0-9\s]', ' ', s)
        # for lda ----
        s = re.sub(r'[^a-zA-Z\s]', ' ', s)
        # ------------
        tokens = [token for token in s.split(" ") if token != ""]
        T = [t for t in tokens if (
            (t in excluded_words) or (t not in NLTK_StopWords))]
        return T

In [158]:
old_kesehatan = old_kesehatan.dropna(subset=['desc'])
old_kesehatan.sort_values('desc', inplace=True)
old_kesehatan.drop_duplicates(subset='desc', keep=False, inplace=True)
df_train, df_test = train_test_split(old_kesehatan,test_size=0.1)
print(len(df_train))

old_kesehatan.head()

1178


title  \
11114  Antisipasi Cuaca Ekstrem, BPBD Tangerang Siapk...   
5810   Wapres Ma'ruf Amin: Pandemi Menguak Kelemahan ...   
5873   Detik-detik Istri di Bandung Barat Disiram Air...   
5271       5 Penyakit yang Kerap Dijumpai di Pengungsian   
5310     Ketahui Penyakit ISPA, Gejala dan Pencegahannya   

                                date  \
11114    Rabu, 28 Des 2022 13:59 WIB   
5810    Sabtu, 10 Des 2022 10:06 WIB   
5873    Jumat, 02 Des 2022 19:38 WIB   
5271   Minggu, 27 Nov 2022 12:13 WIB   
5310    Jumat, 02 Des 2022 04:49 WIB   

                                                    desc          source  
11114    \r\nSebagai bentuk antisipasi situasi buruk ...  www.kompas.com  
5810     \r\nWakil Presiden Ma'ruf Amin menyatakan, a...  www.kompas.com  
5873     \r\n\- Cekcok rumah tangga terjadi di Kampun...  www.kompas.com  
5271    -Gempa yang melanda Cianjur, Jawa Barat, pada...    www.tempo.co  
5310    -Korban Gempa Cianjur, Jawa Barat, yang menem...    www.tempo.co

In [159]:
for x in range(0, old_kesehatan.shape[0]):
    text = preprocessing(old_kesehatan.iloc[x, -2])
    old_kesehatan.iloc[x, -2] = (' '.join(text))

for x in range(0, old_kesehatan.shape[0]):
    text = preprocessing(old_kesehatan.iloc[x, -4])
    old_kesehatan.iloc[x, -4] = (' '.join(text)) 
old_kesehatan.head()

title  \
11114  antisipasi cuaca ekstrem bpbd tangerang siapka...   
5810   wapres ma ruf amin pandemi menguak kelemahan s...   
5873   istri bandung disiram air keras suaminya diung...   
5271                 penyakit kerap dijumpai pengungsian   
5310          ketahui penyakit ispa gejala pencegahannya   

                                date  \
11114    Rabu, 28 Des 2022 13:59 WIB   
5810    Sabtu, 10 Des 2022 10:06 WIB   
5873    Jumat, 02 Des 2022 19:38 WIB   
5271   Minggu, 27 Nov 2022 12:13 WIB   
5310    Jumat, 02 Des 2022 04:49 WIB   

                                                    desc          source  
11114  bentuk antisipasi situasi buruk akibat cuaca e...  www.kompas.com  
5810   wakil presiden ma ruf amin kabar pandemi covid...  www.kompas.com  
5873   cekcok rumah tangga kampung pos wetan rw kerta...  www.kompas.com  
5271   gempa melanda cianjur jawa menyebabkan ribuan ...    www.tempo.co  
5310   korban gempa cianjur jawa menempati tenda peng...    www.tempo.co

## LDA

In [160]:
import gensim
from gensim import corpora
from collections import Counter
import pyLDAvis.gensim
import pickle 
import pyLDAvis
from nltk.tokenize import word_tokenize 
from nltk.probability import FreqDist

def remove_number(text):
    return  re.sub(r"\d+", "", text)

In [161]:
new_kesehatan = old_kesehatan[['title', 'desc']]
new_kesehatan['desc'] = new_kesehatan['desc'].apply(remove_number)
new_kesehatan['desc'] = new_kesehatan['desc'].apply(word_tokenize)
new_kesehatan['desc'] = [[token for token in doc if len(token) > 2] for doc in new_kesehatan['desc']]
new_kesehatan['title'] = new_kesehatan['title'].apply(remove_number)
new_kesehatan['title'] = new_kesehatan['title'].apply(word_tokenize)
new_kesehatan['title'] = [[token for token in doc if len(token) > 2] for doc in new_kesehatan['title']]
new_kesehatan['fdist'] = new_kesehatan['desc'].apply(FreqDist)

print(len(new_kesehatan))
print(new_kesehatan.head(2))

print('Frequency Tokens : \n') 
print(new_kesehatan['fdist'].head().apply(lambda x : x.most_common()))

1309
                                                   title  \
11114  [antisipasi, cuaca, ekstrem, bpbd, tangerang, ...   
5810   [wapres, ruf, amin, pandemi, menguak, kelemaha...   

                                                    desc  \
11114  [bentuk, antisipasi, situasi, buruk, akibat, c...   
5810   [wakil, presiden, ruf, amin, kabar, pandemi, c...   

                                                   fdist  
11114  {'bentuk': 1, 'antisipasi': 4, 'situasi': 2, '...  
5810   {'wakil': 1, 'presiden': 1, 'ruf': 8, 'amin': ...  
Frequency Tokens : 

11114    [(cuaca, 6), (ekstrem, 6), (bpbd, 6), (posko, ...
5810     [(kesehatan, 12), (ruf, 8), (digital, 7), (tek...
5873     [(dinda, 6), (cekcok, 4), (rumah, 4), (tangga,...
5271     [(penyakit, 17), (pengungsian, 11), (akibat, 6...
5310     [(ispa, 15), (gejala, 6), (penyakit, 5), (pern...
Name: fdist, dtype: object


In [162]:
from gensim.models import Phrases
bigram = Phrases(new_kesehatan['desc'], min_count=20)
for idx in range(len(new_kesehatan['desc'])):
    for token in bigram[new_kesehatan['desc'].iloc[idx]]:
        if '_' in token:
            # Token is a bigram, add to document.
            new_kesehatan['desc'].iloc[idx].append(token)
            word1, word2 = token.split("_")
            must_remove = ('bpjs', 'ginjal')
            if word1 not in must_remove:
                new_kesehatan['desc'].iloc[idx].remove(word1)
            if word2 not in must_remove:
                new_kesehatan['desc'].iloc[idx].remove(word2)
            # print(token)

In [468]:
dictionary = corpora.Dictionary(new_kesehatan['desc'])
dictionary.filter_extremes(no_below=35, no_above=0.5)
print(dictionary)

corpus = [dictionary.doc2bow(berita) for berita in new_kesehatan['desc']]

Dictionary<881 unique tokens: ['air', 'akibat', 'antisipasi', 'badan', 'bantuan']...>


In [469]:
# Creating the object for LDA model using gensim library
Lda = gensim.models.ldamodel.LdaModel

total_topics = 5 # jumlah topik yang akan di extract
number_words = 30 # jumlah kata per topik

In [470]:
import os
from gensim.test.utils import datapath
the_path = PATH + kesehatan + "model/lda_model" + "_" + str(total_topics) + "_" + str(number_words)
if not os.path.exists(the_path):
    os.mkdir(the_path)
temp_file = datapath(the_path + "/lda_model")
#if new
# lda_model = Lda(corpus, num_topics=total_topics, id2word=dictionary, passes=50, random_state=1)
# lda_model.save(temp_file)
# load
from gensim import models
lda_model = models.ldamodel.LdaModel.load(temp_file)

lda_model.show_topics(num_topics=total_topics, num_words=number_words)

[(0,
  '0.034*"korban" + 0.022*"warga" + 0.019*"rumah" + 0.012*"kondisi" + 0.012*"pelaku" + 0.011*"tim" + 0.010*"vaksin" + 0.010*"jalan" + 0.010*"rumah_sakit" + 0.010*"cianjur" + 0.009*"puskesmas" + 0.009*"bantuan" + 0.009*"ditemukan" + 0.009*"hewan" + 0.008*"langsung" + 0.008*"virus" + 0.007*"kepala" + 0.007*"keluarga" + 0.007*"pengungsi" + 0.007*"bayi" + 0.006*"sakit" + 0.006*"vaksinasi" + 0.006*"mengaku" + 0.006*"mengalami" + 0.006*"penyakit" + 0.006*"petugas" + 0.006*"tenda" + 0.006*"penanganan" + 0.006*"posko" + 0.006*"dosis"'),
 (1,
  '0.021*"tubuh" + 0.021*"penyakit" + 0.013*"kulit" + 0.012*"memiliki" + 0.011*"manfaat" + 0.011*"gejala" + 0.010*"membantu" + 0.010*"makanan" + 0.010*"darah" + 0.010*"jenis" + 0.009*"menyebabkan" + 0.009*"meningkatkan" + 0.009*"tanaman" + 0.008*"buah" + 0.008*"kondisi" + 0.008*"air" + 0.007*"infeksi" + 0.007*"mengalami" + 0.007*"vitamin" + 0.007*"obat" + 0.007*"mencegah" + 0.007*"mengandung" + 0.006*"penyebab" + 0.006*"sehat" + 0.006*"kandungan" + 0.

In [472]:
# Word Count of Topic Keywords

from collections import Counter
topics = lda_model.show_topics(formatted=False, num_topics=total_topics, num_words=number_words)
# topic = lda_model.show_topics(num_topics=total_topics, num_words=number_words)
# print((topics[0]))
# print((topic[0]))
data_flat = [w for w_list in new_kesehatan['desc'] for w in w_list]
counter = Counter(data_flat)

out = []
for i, topic in topics:
    for word, weight in topic:
        out.append([word, i , weight, counter[word]])

df_imp_wcount = pd.DataFrame(out, columns=['word', 'id', 'importance', 'word_count']) 
print(df_imp_wcount)

                      word  id  importance  word_count
0                   korban   0    0.034375         768
1                    warga   0    0.022314         595
2                    rumah   0    0.019148         443
3                  kondisi   0    0.012113         744
4                   pelaku   0    0.011597         236
..                     ...  ..         ...         ...
145                   juta   4    0.007326         200
146  kementerian_kesehatan   4    0.007324         201
147               keluarga   4    0.007045         396
148                   izin   4    0.006806         131
149                   jaya   4    0.006654         132

[150 rows x 4 columns]


In [314]:
def format_topics_sentences(ldamodel=None, corpus=corpus, texts=new_kesehatan['desc']):
    # Init output
    sent_topics_df = pd.DataFrame()
    # print(len(ldamodel[corpus]))

    dom = []
    perc = []
    keywords = []
    # Get main topic in each document
    for i, row_list in enumerate(ldamodel[corpus]):
        row = row_list[0] if ldamodel.per_word_topics else row_list            
        row = sorted(row, key=lambda x: (x[1]), reverse=True)
        # print(len(row))

        # Get the Dominant topic, Perc Contribution and Keywords for each document
        for j, (topic_num, prop_topic) in enumerate(row):
            if j == 0:  # => dominant topic
                wp = ldamodel.show_topic(topic_num, topn=number_words)
                topic_keywords = ", ".join([word for word, prop in wp])
                dom.append(int(topic_num))
                perc.append(round(prop_topic,4))
                keywords.append(topic_keywords)
                # sent_topics_df = pd.concat([sent_topics_df, pd.DataFrame([pd.Series([int(topic_num), round(prop_topic,4), topic_keywords])])], ignore_index=True)
                # sent_topics_df = sent_topics_df.append(pd.Series([int(topic_num), round(prop_topic,4), topic_keywords]), ignore_index=True)
            else:
                break
    # print(len(sent_topics_df))
    sent_topics_df['Dominant_Topic'] = dom
    sent_topics_df['Perc_Contribution'] = perc
    sent_topics_df['Topic_Keywords'] = keywords
    # sent_topics_df.columns = ['Dominant_Topic', 'Perc_Contribution', 'Topic_Keywords']

    # Add original text to the end of the output
    # sent_topics_df['Texts']= texts
    # print(len(sent_topics_df))
    return(sent_topics_df)

In [473]:
df_topic_sents_keywords = format_topics_sentences(ldamodel=lda_model, corpus=corpus, texts=new_kesehatan['desc'])
df_topic_sents_keywords['Texts'] = 0
df_topic_sents_keywords['Title'] = 0

In [474]:
df_dominant_topic = df_topic_sents_keywords.reset_index()
# texts = []
for i in range(len(new_kesehatan['desc'])):
    # print(new_kecelakaan['desc'].iloc[i])
    # texts.append(new_kecelakaan['desc'].iloc[i])
    df_dominant_topic['Texts'].iloc[i] = new_kesehatan['desc'].iloc[i]
    df_dominant_topic['Title'].iloc[i] = new_kesehatan['title'].iloc[i]
# df_dominant_topic['Texts'] = texts
df_dominant_topic.columns = ['Document_No', 'Dominant_Topic', 'Topic_Perc_Contrib', 'Keywords', 'Text', 'Title']

# df_topic_sents_keywords['Texts'].isna().value_counts()
df_dominant_topic.head(5)
df_dominant_topic.tail(5)

Document_No  Dominant_Topic  Topic_Perc_Contrib  \
1304         1304               0              0.8114   
1305         1305               0              0.4405   
1306         1306               1              0.9396   
1307         1307               3              0.8639   
1308         1308               0              0.8786   

                                               Keywords  \
1304  korban, warga, rumah, kondisi, pelaku, tim, va...   
1305  korban, warga, rumah, kondisi, pelaku, tim, va...   
1306  tubuh, penyakit, kulit, memiliki, manfaat, gej...   
1307  indonesia, program, pasien, bpjs, pemerintah, ...   
1308  korban, warga, rumah, kondisi, pelaku, tim, va...   

                                                   Text  \
1304  [konten, opini, laporan, buatan, blogger, taya...   
1305  [nasal, vaccine, hidung, mengantongi, izin, in...   
1306  [sindroma, kental, kondisi, normal, keseimbang...   
1307  [kil, ketua, mpr, lestari, moerdijat, menghadi...   
1308  [tua, mpr, mengapresiasi, gerakan, keadilan, b...   

                                                  Title  
1304  [curug, mantras, wisata, alam, purbalingga, me...  
1305    [vaksin, hidung, covid, vaksin, booster, india]  
1306                [mengenal, sindroma, darah, kental]  
1307  [lestari, moerdijat, informasi, kanker, payudara]  
1308  [bamsoet, apresiasi, tim, medis, gerak, sukses...

In [37]:
df_dominant_topic.to_csv(PATH + kesehatan + 'df_dominant_topic.csv')

In [38]:
from datetime import datetime
now = datetime.now() # current date and time
date_time = now.strftime("%m-%d-%Y_%H-%M-%S")
print("date and time:",date_time)
LDAvis_html = 'ldavis_prepared_'+ str(total_topics)+"_"+str(number_words)+"_"+str(date_time)
LDAvis_prepared = pyLDAvis.gensim.prepare(lda_model, corpus, dictionary)
with open(PATH + kesehatan + LDAvis_html, 'wb') as f:
        pickle.dump(LDAvis_prepared, f)
pyLDAvis.save_html(LDAvis_prepared, PATH + kesehatan + LDAvis_html +'.html')

date and time: 06-24-2023_06-43-16


In [39]:
with open(PATH + kesehatan + LDAvis_html, 'rb') as f:
    LDAvis_prepared = pickle.load(f)

In [170]:
lda_what_kesehatan = []
word_topics = set(df_imp_wcount['word'].values)
for i in range(len(df_dominant_topic)):
    val = []
    for n, key in enumerate(word_topics):
        if key in df_dominant_topic['Text'].iloc[i]:
            val.append(key)
    lda_what_kesehatan.append(val)

print(lda_what_kesehatan)

[['kepala', 'penanganan', 'kondisi', 'pengungsi', 'mudah', 'daerah', 'bantuan', 'terkait', 'posko', 'informasi', 'air', 'kegiatan'], ['memiliki', 'pasien', 'kementerian_kesehatan', 'penanganan', 'meningkatkan', 'indonesia', 'sistem', 'bantuan', 'layanan', 'sehat', 'acara', 'pemerintah', 'penyakit', 'data'], ['uang', 'pelaku', 'korban', 'langsung', 'tubuh', 'air', 'mengalami'], ['kepala', 'pasien', 'and', 'warga', 'tulang', 'pelayanan', 'penanganan', 'infeksi', 'laporan', 'bayi', 'pengungsi', 'menyebabkan', 'gejala', 'sehat', 'posko', 'rumah', 'tubuh', 'air', 'penyakit', 'penyebab', 'tenda', 'data', 'akut', 'mengalami', 'cianjur'], ['virus', 'warga', 'disebabkan', 'sakit', 'kondisi', 'puskesmas', 'warna', 'mencegah', 'gejala', 'kulit', 'sehat', 'tubuh', 'penyakit', 'tenda', 'akut', 'mengalami', 'cianjur'], ['uang', 'indonesia', 'daerah', 'sosial'], ['keluarga', 'memiliki', 'pasien', 'kementerian_kesehatan', 'tim', 'membantu', 'pasal', 'ginjal', 'keluarga_korban', 'obat', 'pemeriksaan', 

In [317]:
lda_title_what = []
word_topics = set(df_imp_wcount['word'].values)
for i in range(len(df_dominant_topic)):
    val = []
    for n, key in enumerate(word_topics):
        if key in df_dominant_topic['Title'].iloc[i]:
            val.append(key)
    lda_title_what.append(val)

print(lda_title_what)

[['warga', 'posko'], ['sistem'], ['kulit', 'korban', 'tubuh', 'air'], ['penyakit'], ['gejala', 'penyakit'], [], ['keluarga', 'pasien', 'ginjal', 'akut'], ['bpjs'], ['hewan'], ['ginjal', 'gejala', 'akut'], ['pemeriksaan', 'persen'], ['usia'], ['warga'], [], ['keluarga'], ['keluarga'], ['manfaat', 'tubuh'], ['juta'], ['covid'], ['covid'], ['covid'], ['covid'], ['sehat', 'makanan'], [], ['covid'], ['vaksinasi', 'covid'], ['sakit', 'pelaku', 'mengaku'], [], ['kulit'], ['pelayanan'], ['perusahaan', 'ginjal', 'akut'], ['pasien', 'ginjal', 'akut'], ['keluarga', 'ginjal', 'korban', 'akut'], ['pemerintah'], [], ['kepala', 'bpom', 'ginjal', 'akut'], ['penanganan'], ['ginjal', 'akut'], ['keluarga', 'perusahaan', 'ginjal', 'korban', 'pemerintah', 'akut'], ['ginjal', 'akut'], ['ginjal', 'akut'], ['bpom', 'ginjal', 'akut'], ['bpom', 'ginjal', 'akut'], ['ginjal', 'akut'], ['korban', 'jakarta', 'cianjur'], ['warga', 'malam', 'pemerintah', 'ppkm'], ['kondisi'], ['pasien', 'penanganan'], ['keluarga', 'o

In [318]:
for n, word_list in enumerate(lda_title_what):
    val = []
    for word in word_list:
        if word in lda_what_kesehatan[n]:
            continue
        val.append(word)
    lda_what_kesehatan[n].extend(val)
    # if val:
    #     print(n)
    #     print(val)

print(lda_what_kesehatan)

[['kepala', 'penanganan', 'kondisi', 'pengungsi', 'mudah', 'daerah', 'bantuan', 'terkait', 'posko', 'informasi', 'air', 'kegiatan', 'warga'], ['memiliki', 'pasien', 'kementerian_kesehatan', 'penanganan', 'meningkatkan', 'indonesia', 'sistem', 'bantuan', 'layanan', 'sehat', 'acara', 'pemerintah', 'penyakit', 'data'], ['uang', 'pelaku', 'korban', 'langsung', 'tubuh', 'air', 'mengalami', 'kulit'], ['kepala', 'pasien', 'and', 'warga', 'tulang', 'pelayanan', 'penanganan', 'infeksi', 'laporan', 'bayi', 'pengungsi', 'menyebabkan', 'gejala', 'sehat', 'posko', 'rumah', 'tubuh', 'air', 'penyakit', 'penyebab', 'tenda', 'data', 'akut', 'mengalami', 'cianjur'], ['virus', 'warga', 'disebabkan', 'sakit', 'kondisi', 'puskesmas', 'warna', 'mencegah', 'gejala', 'kulit', 'sehat', 'tubuh', 'penyakit', 'tenda', 'akut', 'mengalami', 'cianjur'], ['uang', 'indonesia', 'daerah', 'sosial'], ['keluarga', 'memiliki', 'pasien', 'kementerian_kesehatan', 'tim', 'membantu', 'pasal', 'ginjal', 'keluarga_korban', 'obat

In [366]:
idxs = []
idxs_tp = []
idxs_tn = []
idxs_lda = [] #not in lda words
total = 0
total_tp = 0
total_tn = 0
total_lda = 0
check_lda = ('penyakit', 'rumah_sakit', 'pasien', 'covid', 'tubuh', 'gejala', 'sakit', 'puskesmas',
             'virus', 'infeksi', 'bpjs', 'vaksin', 'kandungan', 'dosis', 'mengalami', 'kendaraan', 'polisi',
             'penumpang', 'pelaku', 'kondisi', 'korban', 'sehat', 'keluarga', 'program', 'dokter',
             'ginjal', 'gagal_ginjal', 'layanan', 'obat', 'laporan', 'selamat')
for i in range(len(lda_what_kesehatan)):
    flag = True
    deflag = True
    ldaf = True
    for token in lda_what_kesehatan[i]:
        if token in check_lda:
            flag = False
        if token in df_imp_wcount['word'].values:
            ldaf = False
    for token in df_dominant_topic['Text'].iloc[i]:
        if token in check_lda:
            deflag = False
    for token in df_dominant_topic['Title'].iloc[i]:
        if token in check_lda:
            deflag = False
    if flag != deflag:
        total += 1
        idxs.append(i)
    elif flag == deflag and flag == False:
        total_tp += 1
        idxs_tp.append(i)
    elif flag == deflag and flag == True:
        total_tn += 1
        idxs_tn.append(i)
    if ldaf:
        total_lda += 1
        idxs_lda.append(i)
print(len(df_dominant_topic))
print(total)
print(total_tp)
print(total_tn)
print(total_lda)


1309
0
1201
108
0


In [58]:
lda_check = []
for word in check_lda:
    if word not in df_imp_wcount['word'].values:
        lda_check.append(word)
print(lda_check)

[]


In [47]:
print(idxs_tn)

[0, 1, 5, 6, 7, 10, 12, 14, 16, 17, 18, 19, 20, 21, 22, 23, 24, 28, 29, 30, 33, 34, 35, 36, 39, 40, 41, 42, 44, 45, 47, 49, 50, 52, 53, 54, 56, 57, 59, 61, 63, 64, 65, 66, 69, 71, 76, 80, 83, 85, 88, 89, 90, 91, 92, 95, 97, 99, 100, 101, 103, 108, 110, 113, 118, 120, 121, 122, 124, 125, 126, 127, 128, 129, 134, 136, 137, 140, 141, 143, 146, 151, 152, 153, 155, 157, 158, 161, 164, 166, 169, 170, 171, 172, 174, 176, 177, 178, 182, 183, 184, 185, 186, 187, 188, 190, 191, 194, 195, 196, 198, 199, 200, 201, 202, 203, 206, 207, 208, 211, 212, 214, 218, 219, 220, 221, 222, 223, 224, 225, 226, 227, 229, 230, 231, 232, 233, 234, 235, 236, 237, 238, 239, 240, 241, 243, 246, 247, 248, 249, 250, 251, 255, 257, 258, 259, 260, 263, 265, 270, 271, 272, 273, 274, 275, 276, 277, 278, 279, 280, 283, 284, 286, 288, 289, 290, 291, 292, 293, 294, 296, 298, 299, 301, 306, 310, 311, 312, 313, 314, 315, 316, 318, 319, 320, 321, 322, 323, 324, 325, 327, 328, 329, 330, 332, 333, 334, 335, 337, 338, 339, 340, 34

In [ ]:
# text  = preprocessing(old_kecelakaan['desc'][old_kecelakaan['desc'].str.find('hari') != -1].iloc[0])
# text
i = idxs_tn[0]
print(df_dominant_topic['Keywords'].iloc[i])
print(type(df_dominant_topic['Keywords'].iloc[i]))
print(df_dominant_topic['Text'].iloc[i])
print(type(df_dominant_topic['Text'].iloc[i]))
print(df_dominant_topic['Keywords'].iloc[i].split(", "))
print(lda_what_kecelakaan[i])


polisi, pelaku, kapal, tersangka, keluarga, warga, hasya, mengaku, anggota, kejadian, laporan, ditemukan, laut, diduga, rumah_sakit, mobil, kepolisian, mengalami, langsung, terkait, air, polres, bernama, jenazah, informasi, penumpang, suaminya, pasal, anaknya, pulang
<class 'str'>
['jenazah', 'korban', 'kecelakaan', 'helikopter', 'jakarta', 'prabowo', 'korban', 'kecelakaan', 'helikopter', 'diserahkan', 'udara', 'pondok', 'cabe', 'tangerang', 'rencananya', 'siang', 'diberangkatkan', 'rumah', 'keluarga', 'melaksanakan', 'upacara', 'penyerahan', 'jenazah', 'lanjutkan', 'persiapan', 'pengantaran', 'jenazah', 'keluarga', 'wartawan', 'jenazah', 'diserahkan', 'bripda', 'choirul', 'anam', 'briptu', 'lasminto', 'berdasarkan', 'pemantauan', 'tempo', 'korban', 'disalatkan', 'karangan', 'bunga', 'tersusun', 'rapih', 'bertuliskan', 'berdukacita', 'lheli', 'nbo', 'prosesi', 'upacara', 'pemberangkatan', 'jenazah', 'keluarga', 'aman', 'helikopter', 'polairud', 'milik', 'polri', 'diawaki', 'kapten', 'b

In [368]:
before_what_kesehatan = old[old['berita_topik_id'] == 4]
before_what_kesehatan = before_what_kesehatan[['berita_title', 'qe_what', 'berita_desc']]
before_what_kesehatan = before_what_kesehatan.dropna(subset=['berita_desc'])
before_what_kesehatan.sort_values('berita_desc', inplace=True)
before_what_kesehatan.drop_duplicates(subset='berita_desc', keep=False, inplace=True)
# print(before_what_kesehatan)
# print(before_what_kesehatan['qe_what'].iloc[i])
# print(before_what_kesehatan['berita_title'].iloc[i])
# print(before_what_kesehatan['berita_desc'].iloc[i])

In [370]:
total_empty = 0
empty_val = []
idxs_total = []
idxs_total.extend(idxs_tp)
idxs_total.extend(idxs_tn)
idxs_total = set(idxs_total)
with open(PATH + kesehatan + 'true_negative_' + str(total_topics) +'.txt', 'w', encoding='UTF8') as f:
    nl = "\n"
    dashes = '--------------------------------------'
    for x in idxs_total:
        f.write(dashes + nl)
        f.write(before_what_kesehatan['berita_title'].iloc[x] + nl)
        f.write(str(before_what_kesehatan['qe_what'].iloc[x]) + nl)
        f.write(str(lda_what_kesehatan[x]) + nl)
        # print(before_what_kecelakaan['berita_title'].iloc[x])
        # print(before_what_kecelakaan['qe_what'].iloc[x])
        # print(lda_what_kecelakaan[x])

        if len(lda_what_kesehatan[x])<5:
            total_empty += 1
            empty_val.append(x)

print(total_empty)
print(empty_val)


47
[5, 183, 212, 356, 366, 374, 375, 395, 486, 508, 525, 540, 554, 619, 637, 644, 647, 723, 730, 832, 918, 938, 941, 943, 946, 952, 953, 978, 1007, 1010, 1052, 1053, 1057, 1078, 1096, 1122, 1123, 1128, 1155, 1176, 1226, 1230, 1255, 1277, 1284, 1285, 1293]


In [62]:
hitung = Counter()
for i in idxs_tn:
    hitung.update(lda_what_kesehatan[i])
    # hitung.update(lda_title_what[i])
    print('--------------------------------------')
    print(before_what_kesehatan['berita_title'].iloc[i])
    # print(before_what_kesehatan['berita_desc'].iloc[i])
    print(before_what_kesehatan['qe_what'].iloc[i])
    print(lda_what_kesehatan[i])
hitung

--------------------------------------
Berziarah ke Makam Sunan Giri, Pelajar MTSN 1 Kediri Meninggal Tertabrak Mobil di Area Parkir
kecelakaan, kendaraan, tertabrak, orang, meninggal, terlibat, pemeriksaan, mengalami, luka, laju, dikemudikan, melaju, langsung, menabrak, pengangkut, bernomor, polisi, benturan, peristiwa, trauma, menderita, mobilnya, memarkir, memar, terparkir, menghajar, menyeruduk, mobil, api, bom, io, dikemudikannya, celaka
['indonesia', 'sosial', 'daerah', 'uang']
--------------------------------------
Dirlantas Polda Metro Buka Suara Kasus Mahasiswa UI Tewas Tertabrak Pajero
kejadian, kecelakaan, pengendara, tertabrak, orang, korban, motor, hasil, dikendarai, keterangan, diduga, polisi, sepeda, benturan, jatuh, berbenturan, kesal, meregang, tewas, nyawa, mengendarai, mobil, api, kendarai, celaka
['ginjal', 'tim', 'akut', 'perusahaan', 'gagal_ginjal', 'tindak_pidana']
--------------------------------------
Fakta Penting Kasus Mahasiswa UI Tewas Tertabrak Jadi Tersan

Counter({'indonesia': 45,
         'terkait': 36,
         'kepala': 36,
         'jawa': 28,
         'memiliki': 27,
         'negara': 27,
         'mengaku': 26,
         'pemerintah': 26,
         'jakarta': 26,
         'kegiatan': 25,
         'kerja': 23,
         'jokowi': 23,
         'daerah': 22,
         'acara': 22,
         'jalan': 21,
         'rumah': 19,
         'proses': 19,
         'pendidikan': 19,
         'hukum': 18,
         'langsung': 18,
         'informasi': 17,
         'malam': 17,
         'uang': 15,
         'nasional': 15,
         'izin': 14,
         'air': 14,
         'warga': 14,
         'natal': 14,
         'tim': 13,
         'tindak_pidana': 13,
         'juta': 13,
         'korupsi': 13,
         'ibadah': 13,
         'semoga': 12,
         'kementerian_kesehatan': 12,
         'peserta': 12,
         'bantuan': 12,
         'protokol_kesehatan': 12,
         'gereja': 12,
         'jenis': 11,
         'perempuan': 11,
         'perse

In [475]:
df_result_lda = df_dominant_topic[['Title', 'Text']]
df_result_lda['what_lda'] = lda_what_kesehatan
df_result_lda['what_qe'] = 0
df_result_lda['title_old'] = 0
df_result_lda['desc_old'] = 0
for i in range(len(df_result_lda)):
    df_result_lda['what_qe'].iloc[i] = before_what_kesehatan['qe_what'].iloc[i]
    df_result_lda['title_old'].iloc[i] = before_what_kesehatan['berita_title'].iloc[i]
    df_result_lda['desc_old'].iloc[i] = before_what_kesehatan['berita_desc'].iloc[i]

# df_result_lda.to_csv(PATH + kesehatan + 'df_result_lda.csv')   
df_result_lda.to_excel(PATH + kesehatan + 'df_result_lda.xlsx', index=None) 
df_result_lda
# print(before_what_kesehatan['qe_what'].iloc[0])

Title  \
0     [antisipasi, cuaca, ekstrem, bpbd, tangerang, ...   
1     [wapres, ruf, amin, pandemi, menguak, kelemaha...   
2     [istri, bandung, disiram, air, keras, suaminya...   
3              [penyakit, kerap, dijumpai, pengungsian]   
4      [ketahui, penyakit, ispa, gejala, pencegahannya]   
...                                                 ...   
1304  [curug, mantras, wisata, alam, purbalingga, me...   
1305    [vaksin, hidung, covid, vaksin, booster, india]   
1306                [mengenal, sindroma, darah, kental]   
1307  [lestari, moerdijat, informasi, kanker, payudara]   
1308  [bamsoet, apresiasi, tim, medis, gerak, sukses...   

                                                   Text  \
0     [bentuk, antisipasi, situasi, buruk, akibat, c...   
1     [kabar, menguak, kelemahan, sistem, berjalan, ...   
2     [cekcok, kampung, pos, wetan, kertamulya, pada...   
3     [melanda, menyebabkan, ribuan, rumah, warga, h...   
4     [menempati, tenda, pengungsian, terjangkir, pe...   
...                                                 ...   
1304  [konten, opini, laporan, buatan, blogger, taya...   
1305  [nasal, vaccine, hidung, mengantongi, izin, in...   
1306  [sindroma, kental, kondisi, normal, keseimbang...   
1307  [kil, ketua, mpr, lestari, moerdijat, menghadi...   
1308  [tua, mpr, mengapresiasi, gerakan, keadilan, b...   

                                               what_lda  \
0     [kepala, penanganan, kondisi, pengungsi, mudah...   
1     [memiliki, pasien, kementerian_kesehatan, pena...   
2     [uang, pelaku, korban, langsung, tubuh, air, m...   
3     [kepala, pasien, and, warga, tulang, pelayanan...   
4     [virus, warga, disebabkan, sakit, kondisi, pus...   
...                                                 ...   
1304  [kepala, memiliki, warga, tanaman, kondisi, la...   
1305  [izin, virus, membantu, dosis, infeksi, mudah,...   
1306  [memiliki, pasien, disebabkan, obat, pemeriksa...   
1307  [pasien, penanganan, meningkatkan, indonesia, ...   
1308  [warga, tim, membantu, penanganan, bayi, bantu...   

                                                what_qe  \
0     kesehatan, kegiatan, akibat, dinas, angka, men...   
1     penyakit, kesehatan, angka, meningkatkan, usus...   
2     korban, angka, rumah, anak, luka, melepuh, lep...   
3     penyakit, kesehatan, akibat, orang, kematian, ...   
4     penyakit, korban, kesehatan, gejala, orang, an...   
...                                                 ...   
1304  desa, orang, angka, menyebut, rumah, anak, men...   
1305  orang, angka, dunia, luka, klinis, penularan, ...   
1306  penyakit, penyumbatan, gejala, menderita, akib...   
1307  penyakit, orang, angka, pencegahan, meningkatk...   
1308  korban, meninggal, kesehatan, dinas, orang, ru...   

                                              title_old  \
0     Antisipasi Cuaca Ekstrem, BPBD Tangerang Siapk...   
1     Wapres Ma'ruf Amin: Pandemi Menguak Kelemahan ...   
2     Detik-detik Istri di Bandung Barat Disiram Air...   
3         5 Penyakit yang Kerap Dijumpai di Pengungsian   
4       Ketahui Penyakit ISPA, Gejala dan Pencegahannya   
...                                                 ...   
1304  Curug Mantras, Wisata Alam di Purbalingga yang...   
1305  Vaksin Hidung untuk Covid-19 Akan Jadi Vaksin ...   
1306                     Mengenal Sindroma Darah Kental   
1307  Lestari Moerdijat: Masyarakat Perlu Informasi ...   
1308  Bamsoet Apresiasi Tim Medis Gerak BS Sukses Op...   

                                               desc_old  
0       \r\nSebagai bentuk antisipasi situasi buruk ...  
1       \r\nWakil Presiden Ma'ruf Amin menyatakan, a...  
2       \r\n\- Cekcok rumah tangga terjadi di Kampun...  
3      -Gempa yang melanda Cianjur, Jawa Barat, pada...  
4      -Korban Gempa Cianjur, Jawa Barat, yang menem...  
...                                                 ...  
1304  _Konten ini merupakan opini/laporan buatan blo...  
1305  _Nasal vaccine_ atau vaksin hidung 

# Kriminalitas

In [106]:
old_kriminalitas = old[old['berita_topik_id'] == 5]
old_kriminalitas = old_kriminalitas[['berita_title', 'berita_date', 'berita_desc', 'berita_source']]
old_kriminalitas.rename(columns = {'berita_title':'title', 'berita_date':'date', 'berita_desc':'desc', 'berita_source':'source'}, inplace=True)
print(old_kriminalitas.shape)
old_kriminalitas.head(2)

(2479, 4)


title  \
6469  Wali Kota Blitar Ungkap Sumber Uang Rp 400 Jut...   
6470  Saat Mobil Perampok Masuk ke Rumah Dinas Wali ...   

                             date  \
6469  Rabu, 14 Des 2022 13:20 WIB   
6470  Rabu, 14 Des 2022 12:47 WIB   

                                                   desc              source  
6469  Perampok menggondol uang Rp 400 juta dari ruma...  www.tribunnews.com  
6470  Seorang pria membukakan pintu gerbang utama Ru...  www.tribunnews.com

## Preprocess

In [107]:
from keybert import KeyBERT
from sentence_transformers import SentenceTransformer
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.metrics.pairwise import cosine_similarity

In [109]:
# previous way

# nltk.download('punkt')
# nltk.download('stopwords')

excluded_words = ["tempat", "waktu", "hari"]
# for lda ----
excluded_words = []
# ------------
NLTK_StopWords = stopwords.words('indonesian')
# print(NLTK_StopWords)
NLTK_StopWords.extend(["detik", "detikjatim", "detikjateng", "detikjabar", "detiksulsel", "detiksumbar", "detikbali",
                      "detikpapua", "detiksulteng", "detikmaluku", "detjatim", "detikcom", "allahumma", "aamiin", "allah", "bismillah"])
NLTK_StopWords.extend(["yg", "dg", "rt", "dgn", "ny", "d", 'klo',
                       'kalo', 'amp', 'biar', 'bikin', 'bilang',
                       'gak', 'ga', 'krn', 'nya', 'nih', 'sih',
                       'si', 'tau', 'tdk', 'tuh', 'utk', 'ya',
                       'jd', 'jgn', 'sdh', 'aja', 'n', 't',
                       'nyg', 'hehe', 'pen', 'u', 'nan', 'loh', 'rt',
                       '&amp', 'yah'])
# txt_stopword = pd.read_csv(PATH + kriminalitas + "stopwords.txt", names= ["stopwords"], header = None)
# NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
# for lda ----
txt_stopword = pd.read_csv(PATH + kriminalitas + "stopwords_add_v1.txt", names= ["stopwords"], header = None)
NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
# txt_stopword = pd.read_csv(PATH + kriminalitas + "stopwords_add_v2.txt", names= ["stopwords"], header = None)
# NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
# txt_stopword = pd.read_csv(PATH + kriminalitas + "stopwords_add_v3.txt", names= ["stopwords"], header = None)
# NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
# ------------
# convert stopword string to list & append additional stopword
# NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))

NLTK_StopWords = set(NLTK_StopWords)

In [110]:
def preprocessing(berita):
        s = str(berita)
        s = s.lower()
        s = s.replace('\n', ' ')
        s = s.replace('\r', ' ')
        # s = re.sub(r'[^a-zA-Z0-9\s]', ' ', s)
        # for lda ----
        s = re.sub(r'[^a-zA-Z\s]', ' ', s)
        # ------------
        tokens = [token for token in s.split(" ") if token != ""]
        T = [t for t in tokens if (
            (t in excluded_words) or (t not in NLTK_StopWords))]
        return T

In [111]:
old_kriminalitas = old_kriminalitas.dropna(subset=['desc'])
old_kriminalitas.sort_values('desc', inplace=True)
old_kriminalitas.drop_duplicates(subset='desc', keep=False, inplace=True)
df_train, df_test = train_test_split(old_kriminalitas,test_size=0.1)
print(len(df_train))

old_kriminalitas.head()

2231


title  \
6795  BERITA FOTO: Kuat Ma'ruf Mengaku Diminta Ferdy...   
6872  Terungkap, Identitas Mayat Wanita Terikat Kabe...   
6618  Seorang WNA Asal Timur Tengah Jadi Salah Satu ...   
6505  Cerita Wali Kota Blitar Soal Perampokan: Istri...   
6486  Kemendikbudristek - Polri Kerjasama Cegah Tind...   

                               date  \
6795  Selasa, 06 Des 2022 06:05 WIB   
6872   Senin, 19 Des 2022 15:09 WIB   
6618   Kamis, 22 Des 2022 14:39 WIB   
6505  Selasa, 13 Des 2022 16:18 WIB   
6486  Selasa, 13 Des 2022 19:50 WIB   

                                                   desc          source  
6795    \r\n\- Hal itu disampaikan Kuat saat dihadir...  www.kompas.com  
6872    \r\n\- Identitas mayat wanita yang ditemukan...  www.kompas.com  
6618    \r\n\- Pria warga negara asing (WNA) asal Ti...  www.kompas.com  
6505   - Wali Kota Blitar Santoso menceritakan detik...    www.tempo.co  
6486   -Kementerian Pendidikan Kebudayaan Riset dan ...    www.tempo.co

In [112]:
for x in range(0, old_kriminalitas.shape[0]):
    text = preprocessing(old_kriminalitas.iloc[x, -2])
    old_kriminalitas.iloc[x, -2] = (' '.join(text))

for x in range(0, old_kriminalitas.shape[0]):
    text = preprocessing(old_kriminalitas.iloc[x, -4])
    old_kriminalitas.iloc[x, -4] = (' '.join(text)) 
old_kriminalitas.head()

title  \
6795  berita foto kuat ma ruf mengaku ferdy sambo be...   
6872  terungkap identitas mayat wanita terikat kabel...   
6618           wna pembunuh perempuan bertato kupu kupu   
6505  cerita wali blitar perampokan istri diancam di...   
6486  kemendikbudristek polri kerjasama cegah tindak...   

                               date  \
6795  Selasa, 06 Des 2022 06:05 WIB   
6872   Senin, 19 Des 2022 15:09 WIB   
6618   Kamis, 22 Des 2022 14:39 WIB   
6505  Selasa, 13 Des 2022 16:18 WIB   
6486  Selasa, 13 Des 2022 19:50 WIB   

                                                   desc          source  
6795  kuat dihadirkan jaksa penuntut jpu saksi pembu...  www.kompas.com  
6872  identitas mayat wanita ditemukan tepi sungai b...  www.kompas.com  
6618  pria warga negara asing wna ditangkap polisi m...  www.kompas.com  
6505  wali blitar santoso menceritakan dirampok istr...    www.tempo.co  
6486  kementerian pendidikan kebudayaan riset teknol...    www.tempo.co

## LDA

In [113]:
import gensim
from gensim import corpora
from collections import Counter
import pyLDAvis.gensim
import pickle 
import pyLDAvis
from nltk.tokenize import word_tokenize 
from nltk.probability import FreqDist

def remove_number(text):
    return  re.sub(r"\d+", "", text)

In [114]:
new_kriminalitas = old_kriminalitas[['title', 'desc']]
new_kriminalitas['desc'] = new_kriminalitas['desc'].apply(remove_number)
new_kriminalitas['desc'] = new_kriminalitas['desc'].apply(word_tokenize)
new_kriminalitas['desc'] = [[token for token in doc if len(token) > 2] for doc in new_kriminalitas['desc']]
new_kriminalitas['title'] = new_kriminalitas['title'].apply(remove_number)
new_kriminalitas['title'] = new_kriminalitas['title'].apply(word_tokenize)
new_kriminalitas['title'] = [[token for token in doc if len(token) > 2] for doc in new_kriminalitas['title']]
new_kriminalitas['fdist'] = new_kriminalitas['desc'].apply(FreqDist)

print(len(new_kriminalitas))
print(new_kriminalitas.head(2))

print('Frequency Tokens : \n') 
print(new_kriminalitas['fdist'].head().apply(lambda x : x.most_common()))

2479
                                                  title  \
6795  [berita, foto, kuat, ruf, mengaku, ferdy, samb...   
6872  [terungkap, identitas, mayat, wanita, terikat,...   

                                                   desc  \
6795  [kuat, dihadirkan, jaksa, penuntut, jpu, saksi...   
6872  [identitas, mayat, wanita, ditemukan, tepi, su...   

                                                  fdist  
6795  {'kuat': 24, 'dihadirkan': 1, 'jaksa': 1, 'pen...  
6872  {'identitas': 2, 'mayat': 6, 'wanita': 2, 'dit...  
Frequency Tokens : 

6795    [(kuat, 24), (yosua, 14), (pembunuhan, 13), (r...
6872    [(mayat, 6), (ciri, 6), (korban, 6), (barito, ...
6618    [(tangerang, 7), (korban, 5), (warga, 4), (kup...
6505    [(santoso, 9), (pelaku, 8), (uang, 6), (istri,...
6486    [(warisan, 10), (budaya, 10), (kebendaan, 9), ...
Name: fdist, dtype: object


In [115]:
from gensim.models import Phrases
bigram = Phrases(new_kriminalitas['desc'], min_count=20)
for idx in range(len(new_kriminalitas['desc'])):
    for token in bigram[new_kriminalitas['desc'].iloc[idx]]:
        if '_' in token:
            # Token is a bigram, add to document.
            new_kriminalitas['desc'].iloc[idx].append(token)
            word1, word2 = token.split("_")
            must_remove = ('kereta')
            if word1 not in must_remove:
                new_kriminalitas['desc'].iloc[idx].remove(word1)
            if word2 not in must_remove:
                new_kriminalitas['desc'].iloc[idx].remove(word2)
            # print(token)

In [458]:
dictionary = corpora.Dictionary(new_kriminalitas['desc'])
dictionary.filter_extremes(no_below=35, no_above=0.5)
print(dictionary)

corpus = [dictionary.doc2bow(berita) for berita in new_kriminalitas['desc']]

Dictionary<1347 unique tokens: ['berbohong', 'bharada', 'brigadir', 'cerita', 'crops']...>


In [459]:
# Creating the object for LDA model using gensim library
Lda = gensim.models.ldamodel.LdaModel

total_topics = 3 # jumlah topik yang akan di extract
number_words = 40 # jumlah kata per topik

In [460]:
import os
from gensim.test.utils import datapath
the_path = PATH + kriminalitas + "model/lda_model" + "_" + str(total_topics) +  "_" + str(number_words)
if not os.path.exists(the_path):
    os.mkdir(the_path)
temp_file = datapath(the_path + "/lda_model")
#if new
# lda_model = Lda(corpus, num_topics=total_topics, id2word=dictionary, passes=50, random_state=1)
# lda_model.save(temp_file)
# load
from gensim import models
lda_model = models.ldamodel.LdaModel.load(temp_file)

lda_model.show_topics(num_topics=total_topics, num_words=number_words)

[(0,
  '0.030*"tersangka" + 0.018*"pelaku" + 0.016*"pembunuhan" + 0.014*"polisi" + 0.014*"keluarga" + 0.009*"pemerkosaan" + 0.009*"membunuh" + 0.007*"diduga" + 0.007*"pasal" + 0.007*"terkait" + 0.006*"perempuan" + 0.005*"langsung" + 0.005*"mengaku" + 0.005*"motif" + 0.005*"rumah" + 0.005*"tindak_pidana" + 0.005*"laporan" + 0.005*"meninggal" + 0.005*"proses" + 0.005*"rekonstruksi" + 0.004*"penyidik" + 0.004*"ketiga" + 0.004*"ayah" + 0.004*"kepolisian" + 0.004*"kejadian" + 0.004*"pidana" + 0.004*"perkara" + 0.004*"magelang" + 0.004*"pembunuhan_berencana" + 0.004*"dugaan" + 0.004*"informasi" + 0.004*"racun" + 0.004*"meninggal_dunia" + 0.004*"uang" + 0.004*"menyebut" + 0.004*"penjara" + 0.004*"ibunya" + 0.004*"kali" + 0.004*"sesuai" + 0.004*"keterangan"'),
 (1,
  '0.065*"pelaku" + 0.016*"polisi" + 0.016*"warga" + 0.016*"rumah" + 0.009*"langsung" + 0.009*"pencurian" + 0.008*"ditemukan" + 0.008*"kejadian" + 0.008*"motor" + 0.007*"jalan" + 0.007*"rumah_dinas" + 0.007*"masuk" + 0.006*"kondisi"

In [461]:
# Word Count of Topic Keywords

from collections import Counter
topics = lda_model.show_topics(formatted=False, num_topics=total_topics, num_words=number_words)
# topic = lda_model.show_topics(num_topics=total_topics, num_words=number_words)
# print((topics[0]))
# print((topic[0]))
data_flat = [w for w_list in new_kriminalitas['desc'] for w in w_list]
counter = Counter(data_flat)

out = []
for i, topic in topics:
    for word, weight in topic:
        out.append([word, i , weight, counter[word]])

df_imp_wcount = pd.DataFrame(out, columns=['word', 'id', 'importance', 'word_count']) 
print(df_imp_wcount)

               word  id  importance  word_count
0         tersangka   0    0.029913        1763
1            pelaku   0    0.017770        7165
2        pembunuhan   0    0.015980        1742
3            polisi   0    0.013828        2381
4          keluarga   0    0.013565         822
..              ...  ..         ...         ...
115       peristiwa   2    0.005208         942
116        magelang   2    0.004826         535
117           mulia   2    0.004821         557
118  brigadir_yosua   2    0.004807         551
119         terkait   2    0.004570         975

[120 rows x 4 columns]


In [335]:
def format_topics_sentences(ldamodel=None, corpus=corpus, texts=new_kriminalitas['desc']):
    # Init output
    sent_topics_df = pd.DataFrame()
    # print(len(ldamodel[corpus]))

    dom = []
    perc = []
    keywords = []
    # Get main topic in each document
    for i, row_list in enumerate(ldamodel[corpus]):
        row = row_list[0] if ldamodel.per_word_topics else row_list            
        row = sorted(row, key=lambda x: (x[1]), reverse=True)
        # print(len(row))

        # Get the Dominant topic, Perc Contribution and Keywords for each document
        for j, (topic_num, prop_topic) in enumerate(row):
            if j == 0:  # => dominant topic
                wp = ldamodel.show_topic(topic_num, topn=number_words)
                topic_keywords = ", ".join([word for word, prop in wp])
                dom.append(int(topic_num))
                perc.append(round(prop_topic,4))
                keywords.append(topic_keywords)
                # sent_topics_df = pd.concat([sent_topics_df, pd.DataFrame([pd.Series([int(topic_num), round(prop_topic,4), topic_keywords])])], ignore_index=True)
                # sent_topics_df = sent_topics_df.append(pd.Series([int(topic_num), round(prop_topic,4), topic_keywords]), ignore_index=True)
            else:
                break
    # print(len(sent_topics_df))
    sent_topics_df['Dominant_Topic'] = dom
    sent_topics_df['Perc_Contribution'] = perc
    sent_topics_df['Topic_Keywords'] = keywords
    # sent_topics_df.columns = ['Dominant_Topic', 'Perc_Contribution', 'Topic_Keywords']

    # Add original text to the end of the output
    # sent_topics_df['Texts']= texts
    # print(len(sent_topics_df))
    return(sent_topics_df)

In [462]:
df_topic_sents_keywords = format_topics_sentences(ldamodel=lda_model, corpus=corpus, texts=new_kriminalitas['desc'])
df_topic_sents_keywords['Texts'] = 0
df_topic_sents_keywords['Title'] = 0

In [463]:
df_dominant_topic = df_topic_sents_keywords.reset_index()
# texts = []
for i in range(len(new_kriminalitas['desc'])):
    # print(new_kriminalitas['desc'].iloc[i])
    # texts.append(new_kriminalitas['desc'].iloc[i])
    df_dominant_topic['Texts'].iloc[i] = new_kriminalitas['desc'].iloc[i]
    df_dominant_topic['Title'].iloc[i] = new_kriminalitas['title'].iloc[i]
# df_dominant_topic['Texts'] = texts
df_dominant_topic.columns = ['Document_No', 'Dominant_Topic', 'Topic_Perc_Contrib', 'Keywords', 'Text', 'Title']

# df_topic_sents_keywords['Texts'].isna().value_counts()
df_dominant_topic.head(5)
df_dominant_topic.tail(5)

Document_No  Dominant_Topic  Topic_Perc_Contrib  \
2474         2474               1              0.9920   
2475         2475               1              0.9967   
2476         2476               0              0.9847   
2477         2477               1              0.9872   
2478         2478               1              0.5965   

                                               Keywords  \
2474  pelaku, polisi, warga, rumah, langsung, pencur...   
2475  pelaku, polisi, warga, rumah, langsung, pencur...   
2476  tersangka, pelaku, pembunuhan, polisi, keluarg...   
2477  pelaku, polisi, warga, rumah, langsung, pencur...   
2478  pelaku, polisi, warga, rumah, langsung, pencur...   

                                                   Text  \
2474  [warga, jawa, tolong, perampokan, trimo, warga...   
2475  [warga, melintas, ciomas, bogor, berhati, hati...   
2476  [diutus, tsamud, menaati, ajaran, kisah, shale...   
2477  [nasib, sial, dialami, jalan, sodanco, jawa, d...   
2478  [konten, opini, laporan, buatan, blogger, taya...   

                                                  Title  
2474  [perampokan, rumah, dinas, wali, blitar, saksi...  
2475  [waspada, melintas, ciomas, bogor, emak, emak,...  
2476  [kisah, shaleh, perjuangannya, mengajak, tsamu...  
2477  [netizen, heran, rumah, sekelas, wali, blitar,...  
2478  [candi, brahu, peninggalan, majapahit, selamat...

In [136]:
df_dominant_topic.to_csv(PATH + kriminalitas + 'df_dominant_topic.csv')

In [137]:
from datetime import datetime
now = datetime.now() # current date and time
date_time = now.strftime("%m-%d-%Y_%H-%M-%S")
print("date and time:",date_time)
LDAvis_html = 'ldavis_prepared_'+ str(total_topics)+"_"+str(number_words)+"_"+str(date_time)
LDAvis_prepared = pyLDAvis.gensim.prepare(lda_model, corpus, dictionary)
with open(PATH + kriminalitas + LDAvis_html, 'wb') as f:
        pickle.dump(LDAvis_prepared, f)
pyLDAvis.save_html(LDAvis_prepared, PATH + kriminalitas + LDAvis_html +'.html')

date and time: 06-24-2023_07-48-29


In [ ]:
with open(PATH + kriminalitas + LDAvis_html, 'rb') as f:
    LDAvis_prepared = pickle.load(f)

In [464]:
lda_what_kriminalitas = []
word_topics = set(df_imp_wcount['word'].values)
for i in range(len(df_dominant_topic)):
    val = []
    for n, key in enumerate(word_topics):
        if key in df_dominant_topic['Text'].iloc[i]:
            val.append(key)
    lda_what_kriminalitas.append(val)

print(lda_what_kriminalitas)

[['perintah', 'pembunuhan', 'pasal_kuhp', 'yosua', 'kali', 'saksi', 'santoso', 'hakim', 'ferdy_sambo', 'eliezer', 'persidangan', 'brigadir', 'putri_candrawathi', 'kuhp', 'kuat_ruf', 'rumah_dinas', 'ricky_rizal', 'sambo', 'richard_eliezer', 'peristiwa', 'pembunuhan_berencana', 'kuat', 'terdakwa', 'magelang'], ['keluarga', 'pembunuhan', 'warga', 'saksi', 'polres', 'mobil', 'penyelidikan', 'polisi', 'kondisi', 'pelaku', 'dugaan', 'jalan', 'berinisial', 'terkait', 'kuat', 'ditemukan', 'keterangan'], ['pembunuhan', 'warga', 'pria', 'kali', 'perempuan', 'saksi', 'jasad', 'polsek', 'polisi', 'kondisi', 'pelaku', 'dugaan', 'meninggal_dunia', 'kepolisian', 'ditangkap', 'informasi', 'langsung', 'ketiga', 'jakarta', 'membunuh', 'ditemukan'], ['uang', 'kamar', 'santoso', 'kondisi', 'pelaku', 'istri', 'wali_blitar', 'rumah_dinas', 'peristiwa', 'mengaku'], ['tindak_pidana', 'pencurian', 'masuk', 'pelaku', 'terkait', 'polri', 'informasi', 'jakarta'], ['tim', 'blitar', 'saksi', 'santoso', 'polres', 'p

In [465]:
lda_title_what = []
word_topics = set(df_imp_wcount['word'].values)
for i in range(len(df_dominant_topic)):
    val = []
    for n, key in enumerate(word_topics):
        if key in df_dominant_topic['Title'].iloc[i]:
            val.append(key)
    lda_title_what.append(val)

print(lda_title_what)

[['sambo', 'kuat', 'mengaku'], ['wanita', 'diduga'], ['perempuan'], ['blitar', 'istri'], ['pencurian', 'pidana', 'polri'], ['blitar', 'saksi', 'polisi', 'terkait', 'rumah'], ['uang', 'saudara', 'pelaku'], ['pria', 'ditangkap'], ['blitar', 'polisi'], ['polisi'], ['pemerkosaan'], ['pria', 'penjara', 'masuk', 'mengaku'], ['pembunuhan', 'perempuan', 'ditemukan', 'diduga'], ['istri'], ['blitar', 'rumah'], ['blitar', 'rumah'], ['pria'], ['pembunuhan', 'brigadir'], ['keluarga', 'pembunuhan', 'pencurian', 'polisi'], ['pencurian'], ['jaksa', 'pencurian', 'motif', 'rumah'], ['putri', 'pemerkosaan', 'sambo'], ['pembunuhan', 'yosua', 'brigadir'], ['pemerkosaan', 'masuk', 'kejadian', 'sambo', 'magelang'], ['pemerkosaan', 'sambo'], ['pembunuhan', 'pasal', 'saksi', 'putri', 'ahli'], ['pembunuhan', 'saksi', 'putri', 'motif', 'pidana', 'ahli', 'sambo', 'sidang'], ['pembunuhan', 'yosua', 'eliezer', 'brigadir', 'richard'], ['pencurian', 'perkara', 'polisi', 'dugaan'], ['perempuan', 'pemerkosaan'], ['pemb

In [466]:
for n, word_list in enumerate(lda_title_what):
    val = []
    for word in word_list:
        if word in lda_what_kriminalitas[n]:
            continue
        val.append(word)
    lda_what_kriminalitas[n].extend(val)
    # if val:
    #     print(n)
    #     print(val)

print(lda_what_kriminalitas)

[['perintah', 'pembunuhan', 'pasal_kuhp', 'yosua', 'kali', 'saksi', 'santoso', 'hakim', 'ferdy_sambo', 'eliezer', 'persidangan', 'brigadir', 'putri_candrawathi', 'kuhp', 'kuat_ruf', 'rumah_dinas', 'ricky_rizal', 'sambo', 'richard_eliezer', 'peristiwa', 'pembunuhan_berencana', 'kuat', 'terdakwa', 'magelang', 'mengaku'], ['keluarga', 'pembunuhan', 'warga', 'saksi', 'polres', 'mobil', 'penyelidikan', 'polisi', 'kondisi', 'pelaku', 'dugaan', 'jalan', 'berinisial', 'terkait', 'kuat', 'ditemukan', 'keterangan', 'wanita', 'diduga'], ['pembunuhan', 'warga', 'pria', 'kali', 'perempuan', 'saksi', 'jasad', 'polsek', 'polisi', 'kondisi', 'pelaku', 'dugaan', 'meninggal_dunia', 'kepolisian', 'ditangkap', 'informasi', 'langsung', 'ketiga', 'jakarta', 'membunuh', 'ditemukan'], ['uang', 'kamar', 'santoso', 'kondisi', 'pelaku', 'istri', 'wali_blitar', 'rumah_dinas', 'peristiwa', 'mengaku', 'blitar'], ['tindak_pidana', 'pencurian', 'masuk', 'pelaku', 'terkait', 'polri', 'informasi', 'jakarta', 'pidana'],

In [341]:
idxs = []
idxs_tp = []
idxs_tn = []
idxs_lda = [] #not in lda words
total = 0
total_tp = 0
total_tn = 0
total_lda = 0
check_lda = ('mobil', 'motor', 'ferdy_sambo', 'sambo', 'yosua', 'putri_candrawathi', 'eliezer',
             'meninggal', 'meninggal_dunia', 'polisi', 'pembunuhan', 'membunuh', 'brigadir_yosua',
             'pelaku', 'saksi', 'pemerkosaan', 'dugaan', 'tindak_pidana', 'racun', 'pencurian',
             'kejadian', 'pidana')
for i in range(len(lda_what_kriminalitas)):
    flag = True
    deflag = True
    ldaf = True
    for token in lda_what_kriminalitas[i]:
        if token in check_lda:
            flag = False
        if token in df_imp_wcount['word'].values:
            ldaf = False
    for token in df_dominant_topic['Text'].iloc[i]:
        if token in check_lda:
            deflag = False
    for token in df_dominant_topic['Title'].iloc[i]:
        if token in check_lda:
            deflag = False
    if flag != deflag:
        total += 1
        idxs.append(i)
    elif flag == deflag and flag == False:
        total_tp += 1
        idxs_tp.append(i)
    elif flag == deflag and flag == True:
        total_tn += 1
        idxs_tn.append(i)
    if ldaf:
        total_lda += 1
        idxs_lda.append(i)
print(len(df_dominant_topic))
print(total)
print(total_tp)
print(total_tn)
print(total_lda)


2479
0
2456
23
0


In [127]:
lda_check = []
for word in check_lda:
    if word not in df_imp_wcount['word'].values:
        lda_check.append(word)
print(lda_check)

[]


In [96]:
print(idxs_tn)

[0, 10, 14, 21, 23, 61, 76, 86, 108, 113, 174, 195, 197, 203, 211, 212, 213, 214, 215, 217, 218, 220, 221, 222, 223, 225, 227, 228, 229, 241, 242, 246, 247, 248, 251, 253, 254, 255, 256, 257, 258, 259, 260, 261, 262, 263, 264, 266, 268, 269, 273, 274, 275, 276, 281, 285, 286, 287, 288, 289, 321, 322, 326, 328, 331, 339, 340, 348, 349, 352, 364, 365, 369, 374, 376, 377, 380, 382, 383, 384, 385, 387, 388, 389, 391, 393, 394, 397, 400, 401, 402, 403, 404, 407, 409, 410, 411, 412, 413, 414, 415, 416, 417, 418, 422, 423, 424, 425, 427, 428, 429, 431, 433, 434, 436, 437, 439, 440, 441, 442, 443, 445, 446, 447, 448, 454, 455, 456, 460, 461, 462, 465, 466, 472, 476, 477, 478, 482, 490, 494, 497, 503, 516, 546, 547, 550, 566, 569, 570, 571, 573, 574, 575, 576, 578, 579, 581, 582, 583, 584, 585, 586, 587, 588, 589, 590, 591, 593, 594, 595, 596, 598, 599, 603, 604, 606, 607, 608, 610, 611, 612, 613, 614, 615, 616, 617, 618, 619, 620, 621, 622, 625, 626, 641, 642, 644, 646, 647, 654, 655, 658, 659

In [98]:
# text  = preprocessing(old_kecelakaan['desc'][old_kecelakaan['desc'].str.find('hari') != -1].iloc[0])
# text
i = idxs_tn[0]
print(df_dominant_topic['Keywords'].iloc[i])
print(type(df_dominant_topic['Keywords'].iloc[i]))
print(df_dominant_topic['Text'].iloc[i])
print(type(df_dominant_topic['Text'].iloc[i]))
print(df_dominant_topic['Keywords'].iloc[i].split(", "))
print(lda_what_kriminalitas[i])


ferdy_sambo, sambo, yosua, putri_candrawathi, eliezer, kuat_ruf, terdakwa, hakim, putri, saudara, richard_eliezer, ricky_rizal, kuat, brigadir, saksi, sidang, pembunuhan_berencana, yosua_hutabarat, richard, pasal_kuhp, mengaku, jakarta, ricky, pengadilan_negeri, pembunuhan, jaksa, pembunuhan_brigadir, rumah, keterangan, jaksel
<class 'str'>
['saksi', 'bharada', 'memintanya', 'berbohong', 'kali', 'diperiksa', 'provos', 'pembunuhan', 'crops', 'nyebqcuebjjvvcc', 'engtjtu', 'pembunuhan', 'wat', 'cerita', 'diperiksa', 'cerita', 'magelang', 'separuh', 'menirukan', 'percakapannya', 'sambo', 'menemuinya', 'kantor', 'provos', 'sambo', 'pengamanan', 'mestinya', 'pembunuhan', 'crops', 'smnrleiszivkbtmicmmxc', 'pembunuhan', 'sambo', 'gitu', 'wat', 'ngapain', 'habis', 'tutup', 'tutup', 'pintu', 'habis', 'tutup', 'balkon', 'ketemu', 'dapur', 'papar', 'menirukan', 'percakapannya', 'balkon', 'tiarap', 'menirukan', 'perintah', 'sambo', 'mendengar', 'perintah', 'kebohongan', 'kebohongan', 'menutupi', 's

In [129]:
before_what_kriminalitas = old[old['berita_topik_id'] == 5]
before_what_kriminalitas = before_what_kriminalitas[['berita_title', 'qe_what', 'berita_desc']]
before_what_kriminalitas = before_what_kriminalitas.dropna(subset=['berita_desc'])
before_what_kriminalitas.sort_values('berita_desc', inplace=True)
before_what_kriminalitas.drop_duplicates(subset='berita_desc', keep=False, inplace=True)
# print(before_what_kriminalitas)
# print(before_what_kriminalitas['qe_what'].iloc[i])
# print(before_what_kriminalitas['berita_title'].iloc[i])
# print(before_what_kriminalitas['berita_desc'].iloc[i])

In [344]:
total_empty = 0
empty_val = []
idxs_total = []
idxs_total.extend(idxs_tp)
idxs_total.extend(idxs_tn)
idxs_total = set(idxs_total)
with open(PATH + kriminalitas + 'true_negative_' + str(total_topics) +'.txt', 'w', encoding='UTF8') as f:
    nl = "\n"
    dashes = '--------------------------------------'
    for x in idxs_total:
        f.write(dashes + nl)
        f.write(before_what_kriminalitas['berita_title'].iloc[x] + nl)
        f.write(str(before_what_kriminalitas['qe_what'].iloc[x]) + nl)
        f.write(str(lda_what_kriminalitas[x]) + nl)
        # print(before_what_kriminalitas['berita_title'].iloc[x])
        # print(before_what_kriminalitas['qe_what'].iloc[x])
        # print(lda_what_kriminalitas[x])

        if len(lda_what_kriminalitas[x])<3:
            total_empty += 1
            empty_val.append(x)

print(total_empty)
print(empty_val)


5
[198, 639, 914, 1535, 1958]


In [156]:
hitung = Counter()
for i in idxs_tn:
    hitung.update(lda_what_kriminalitas[i])
    # hitung.update(lda_title_what[i])
    print('--------------------------------------')
    print(before_what_kriminalitas['berita_title'].iloc[i])
    # print(before_what_kriminalitas['berita_desc'].iloc[i])
    print(before_what_kriminalitas['qe_what'].iloc[i])
    print(lda_what_kriminalitas[i])
hitung

--------------------------------------
Aksi Perampok Sergap Rumah Dinas, Wali Kota Blitar: Jangan Dikaitkan dengan Politik, Ini bagi Saya Musibah
polisi, rumah, kali, langsung, uang, 1, kegiatan, kriminal, forensik, investigasi, musibah, utang, perampokan, kamp, dirampas, gang, reskrim, perampok
['langsung', 'rumah_dinas', 'diduga', 'mengaku', 'tim', 'hilang', 'kali', 'blitar', 'terkait', 'wali_blitar', 'peristiwa', 'santoso', 'motif', 'proses', 'uang', 'kepolisian', 'rumah']
--------------------------------------
Pengacara Keluarga Iwan Boedi: Ada 2 Nelayan Hilang di Sekitar Lokasi Terbunuhnya Korban
korban, desa, rumah, fir, 1, perlindungan, hukum, ormas
['jalan', 'diduga', 'mengaku', 'ditemukan', 'hilang', 'keluarga', 'informasi', 'rumah', 'kejadian']
--------------------------------------
11 Napi di Jabar Bebas Saat Hari Natal
bersangkutan, anak, langsung, langkah, warga, 1, kegiatan, pidana, pidananya, kemasyarakatan, narapidana, pencurian, vonis, gang, ormas, napi
['langsung', 'k

Counter({'mengaku': 10,
         'rumah': 10,
         'jalan': 10,
         'langsung': 8,
         'terkait': 8,
         'rumah_dinas': 6,
         'pria': 6,
         'diduga': 5,
         'hilang': 5,
         'blitar': 5,
         'uang': 5,
         'keluarga': 5,
         'masuk': 5,
         'menyebut': 5,
         'kali': 4,
         'wali_blitar': 4,
         'peristiwa': 4,
         'santoso': 4,
         'proses': 4,
         'kejadian': 4,
         'polres': 4,
         'kondisi': 4,
         'istri': 4,
         'tim': 3,
         'pidana': 3,
         'penjara': 3,
         'kuhp': 3,
         'petugas': 3,
         'jakarta': 3,
         'warga': 3,
         'milik': 3,
         'perkara': 3,
         'kepolisian': 2,
         'ditemukan': 2,
         'informasi': 2,
         'kamar': 2,
         'pasal': 2,
         'persidangan': 2,
         'hakim': 2,
         'pasal_kuhp': 2,
         'perempuan': 2,
         'berinisial': 2,
         'perintah': 2,
         'yosu

In [467]:
df_result_lda = df_dominant_topic[['Title', 'Text']]
df_result_lda['what_lda'] = lda_what_kriminalitas
df_result_lda['what_qe'] = 0
df_result_lda['title_old'] = 0
df_result_lda['desc_old'] = 0
for i in range(len(df_result_lda)):
    df_result_lda['what_qe'].iloc[i] = before_what_kriminalitas['qe_what'].iloc[i]
    df_result_lda['title_old'].iloc[i] = before_what_kriminalitas['berita_title'].iloc[i]
    df_result_lda['desc_old'].iloc[i] = before_what_kriminalitas['berita_desc'].iloc[i]

# df_result_lda.to_csv(PATH + kriminalitas + 'df_result_lda.csv')   
df_result_lda.to_excel(PATH + kriminalitas + 'df_result_lda.xlsx', index=None) 
df_result_lda
# print(before_what_kriminalitas['qe_what'].iloc[0])

Title  \
0     [berita, foto, kuat, ruf, mengaku, ferdy, samb...   
1     [terungkap, identitas, mayat, wanita, terikat,...   
2       [wna, pembunuh, perempuan, bertato, kupu, kupu]   
3     [cerita, wali, blitar, perampokan, istri, dian...   
4     [kemendikbudristek, polri, kerjasama, cegah, t...   
...                                                 ...   
2474  [perampokan, rumah, dinas, wali, blitar, saksi...   
2475  [waspada, melintas, ciomas, bogor, emak, emak,...   
2476  [kisah, shaleh, perjuangannya, mengajak, tsamu...   
2477  [netizen, heran, rumah, sekelas, wali, blitar,...   
2478  [candi, brahu, peninggalan, majapahit, selamat...   

                                                   Text  \
0     [saksi, bharada, memintanya, berbohong, kali, ...   
1     [identitas, ditemukan, tepi, sungai, barito, k...   
2     [pria, ditangkap, polisi, membunuh, bernama, e...   
3     [santoso, menceritakan, dirampok, istri, kamar...   
4     [kementerian, pendidikan, kebudayaan, riset, t...   
...                                                 ...   
2474  [warga, jawa, tolong, perampokan, trimo, warga...   
2475  [warga, melintas, ciomas, bogor, berhati, hati...   
2476  [diutus, tsamud, menaati, ajaran, kisah, shale...   
2477  [nasib, sial, dialami, jalan, sodanco, jawa, d...   
2478  [konten, opini, laporan, buatan, blogger, taya...   

                                               what_lda  \
0     [perintah, pembunuhan, pasal_kuhp, yosua, kali...   
1     [keluarga, pembunuhan, warga, saksi, polres, m...   
2     [pembunuhan, warga, pria, kali, perempuan, sak...   
3     [uang, kamar, santoso, kondisi, pelaku, istri,...   
4     [tindak_pidana, pencurian, masuk, pelaku, terk...   
...                                                 ...   
2474  [warga, saksi, santoso, mobil, masuk, pelaku, ...   
2475  [uang, warga, kali, perempuan, pencurian, perk...   
2476  [perintah, pembunuhan, kali, saudara, milik, j...   
2477  [uang, blitar, santoso, polres, pelaku, kejadi...   
2478  [pencurian, kondisi, proses, laporan, jalan, h...   

                                                what_qe  \
0     rumah, lantas, kali, anak, 1, terdakwa, pembun...   
1     pelaku, korban, mobil, keterangan, polres, war...   
2     pelaku, polisi, korban, kali, langsung, polres...   
3     pelaku, rumah, uang, 1, kalung, perampokan, pe...   
4     pelaku, kejahatan, anak, uang, tingkatkan, 1, ...   
...                                                 ...   
2474  pelaku, kota, rumah, mobil, uang, warga, 1, pe...   
2475  pelaku, kejahatan, polisi, korban, rumah, kete...   
2476  keterangan, kali, fir, anak, uang, 1, perlindu...   
2477  pelaku, kota, rumah, uang, 1, perampokan, dira...   
2478  desa, kota, lantas, kali, anak, langsung, uang...   

                                              title_old  \
0     BERITA FOTO: Kuat Ma'ruf Mengaku Diminta Ferdy...   
1     Terungkap, Identitas Mayat Wanita Terikat Kabe...   
2     Seorang WNA Asal Timur Tengah Jadi Salah Satu ...   
3     Cerita Wali Kota Blitar Soal Perampokan: Istri...   
4     Kemendikbudristek - Polri Kerjasama Cegah Tind...   
...                                                 ...   
2474  Perampokan di Rumah Dinas Wali Kota Blitar, Sa...   
2475  Waspada Melintas di Ciomas Bogor, Emak-emak Ke...   
2476  Kisah Nabi Shaleh dan Perjuangannya Mengajak K...   
2477  Netizen Heran Rumah Sekelas Wali Kota Blitar B...   
2478  Candi Brahu, Peninggalan Majapahit yang Selama...   

                                               desc_old  
0       \r\n\- Hal itu disampaikan Kuat saat dihadir...  
1       \r\n\- Identitas mayat wanita yang ditemukan...  
2       \r\n\- Pria warga negara asing (WNA) asal Ti...  
3      - Wali Kota Blitar Santoso menceritakan detik...  
4      -Kementerian Pendidikan Kebudayaan Riset dan ...  
...                                                 ...  
2474  \- Warga sekitar Rumah Dinas Wali Kota Blitar,...  
2475  \- Warga yang melintas di wilayah K

# Olahraga

In [7]:
old_olahraga = old[old['berita_topik_id'] == 6]
old_olahraga = old_olahraga[['berita_title', 'berita_date', 'berita_desc', 'berita_source']]
old_olahraga.rename(columns = {'berita_title':'title', 'berita_date':'date', 'berita_desc':'desc', 'berita_source':'source'}, inplace=True)
print(old_olahraga.shape)
old_olahraga.head(2)

(489, 4)


title  \
8660  Klub Dewa United Basketball Resmi Pindah Kanda...   
8661  Jadwal BWF World Tour Finals 2022, Debut Fajar...   

                              date  \
8660  Senin, 19 Des 2022 23:37 WIB   
8661  Kamis, 01 Des 2022 13:42 WIB   

                                                   desc              source  
8660  _KlubDewa United Basketball Resmi Pindah Kanda...  www.tribunnews.com  
8661  Simak jadwal lengkap perhelatan BWF World Tour...  www.tribunnews.com

## Preprocess

In [8]:
from keybert import KeyBERT
from sentence_transformers import SentenceTransformer
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.metrics.pairwise import cosine_similarity

In [9]:
# previous way

# nltk.download('punkt')
# nltk.download('stopwords')

excluded_words = ["tempat", "waktu", "hari"]
# for lda ----
excluded_words = []
# ------------
NLTK_StopWords = stopwords.words('indonesian')
# print(NLTK_StopWords)
NLTK_StopWords.extend(["detik", "detikjatim", "detikjateng", "detikjabar", "detiksulsel", "detiksumbar", "detikbali",
                      "detikpapua", "detiksulteng", "detikmaluku", "detjatim", "detikcom", "allahumma", "aamiin", "allah", "bismillah"])
NLTK_StopWords.extend(["yg", "dg", "rt", "dgn", "ny", "d", 'klo',
                       'kalo', 'amp', 'biar', 'bikin', 'bilang',
                       'gak', 'ga', 'krn', 'nya', 'nih', 'sih',
                       'si', 'tau', 'tdk', 'tuh', 'utk', 'ya',
                       'jd', 'jgn', 'sdh', 'aja', 'n', 't',
                       'nyg', 'hehe', 'pen', 'u', 'nan', 'loh', 'rt',
                       '&amp', 'yah'])
# txt_stopword = pd.read_csv(PATH + olahraga + "stopwords.txt", names= ["stopwords"], header = None)
# NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
# for lda ----
txt_stopword = pd.read_csv(PATH + olahraga + "stopwords_add_v1.txt", names= ["stopwords"], header = None)
NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
# txt_stopword = pd.read_csv(PATH + olahraga + "stopwords_add_v2.txt", names= ["stopwords"], header = None)
# NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
# txt_stopword = pd.read_csv(PATH + olahraga + "stopwords_add_v3.txt", names= ["stopwords"], header = None)
# NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))
# ------------
# convert stopword string to list & append additional stopword
# NLTK_StopWords.extend(txt_stopword["stopwords"][0].split(' '))

NLTK_StopWords = set(NLTK_StopWords)

In [10]:
def preprocessing(berita):
        s = str(berita)
        s = s.lower()
        s = s.replace('\n', ' ')
        s = s.replace('\r', ' ')
        # s = re.sub(r'[^a-zA-Z0-9\s]', ' ', s)
        # for lda ----
        s = re.sub(r'[^a-zA-Z\s]', ' ', s)
        # ------------
        tokens = [token for token in s.split(" ") if token != ""]
        T = [t for t in tokens if (
            (t in excluded_words) or (t not in NLTK_StopWords))]
        return T

In [26]:
old_olahraga = old_olahraga.dropna(subset=['desc'])
old_olahraga.sort_values('desc', inplace=True)
old_olahraga.drop_duplicates(subset='desc', keep=False, inplace=True)
df_train = joblib.load(prebandingan_path + olahraga[:-1] + '_train_unpreprocessed.pkl')
df_test = joblib.load(prebandingan_path + olahraga[:-1] + '_test_unpreprocessed.pkl')
df_train = df_train[['berita_title', 'berita_date', 'berita_desc', 'berita_source']]
df_train.rename(columns = {'berita_title':'title', 'berita_date':'date', 'berita_desc':'desc', 'berita_source':'source'}, inplace=True)
df_test = df_test[['berita_title', 'berita_date', 'berita_desc', 'berita_source']]
df_test.rename(columns = {'berita_title':'title', 'berita_date':'date', 'berita_desc':'desc', 'berita_source':'source'}, inplace=True)
print(len(df_train))
print(len(df_test))

df_test.head()

440
49


title  \
11446                 Tottenham Vs Villa Masih Tanpa Gol   
8767   Momen Iptu Umbaran Saat Nyamar Jadi Wartawan, ...   
8825   PSM Makassar Vs PSIS di Liga 1: Adu Kepiawaian...   
8857   Profil Hakim Ziyech, Bawa Timnas Maroko Ukir S...   
11435         Brentford Vs Liverpool: Si Merah Kalah 1-3   

                                date  \
11446  Minggu, 01 Jan 2023 21:54 WIB   
8767    Sabtu, 17 Des 2022 19:26 WIB   
8825   Minggu, 18 Des 2022 08:40 WIB   
8857     Rabu, 14 Des 2022 16:47 WIB   
11435  Selasa, 03 Jan 2023 02:31 WIB   

                                                    desc         source  
11446  \-\r\n\r\nLaga Tottenham Hotspur vs Aston Vill...  www.detik.com  
8767   \-\r\n\r\nIptu Umbaran menjadi sorotan publik ...  www.detik.com  
8825   \-\r\n\r\nDuel gelandang asal Jepang bakal ter...  www.detik.com  
8857   \-\r\n\r\nHakim Ziyech bersinar bersama timnas...  www.detik.com  
11435  \-\r\n\r\nLiverpool membuka tahun 2023 dengan ...  www.detik.com

In [29]:
for x in range(0, old_olahraga.shape[0]):
    text = preprocessing(old_olahraga.iloc[x, -2])
    old_olahraga.iloc[x, -2] = (' '.join(text))

for x in range(0, old_olahraga.shape[0]):
    text = preprocessing(old_olahraga.iloc[x, -4])
    old_olahraga.iloc[x, -4] = (' '.join(text))

for x in range(0, df_train.shape[0]):
    text = preprocessing(df_train.iloc[x, -2])
    df_train.iloc[x, -2] = (' '.join(text))

for x in range(0, df_train.shape[0]):
    text = preprocessing(df_train.iloc[x, -4])
    df_train.iloc[x, -4] = (' '.join(text))

for x in range(0, df_test.shape[0]):
    text = preprocessing(df_test.iloc[x, -2])
    df_test.iloc[x, -2] = (' '.join(text))

for x in range(0, df_test.shape[0]):
    text = preprocessing(df_test.iloc[x, -4])
    df_test.iloc[x, -4] = (' '.join(text))
    
# df_test.head()

## LDA

In [30]:
import gensim
from gensim import corpora
from collections import Counter
import pyLDAvis.gensim
import pickle 
import pyLDAvis
from nltk.tokenize import word_tokenize 
from nltk.probability import FreqDist

def remove_number(text):
    return  re.sub(r"\d+", "", text)

In [14]:
new_olahraga = old_olahraga[['title', 'desc']]
new_olahraga['desc'] = new_olahraga['desc'].apply(remove_number)
new_olahraga['desc'] = new_olahraga['desc'].apply(word_tokenize)
new_olahraga['desc'] = [[token for token in doc if len(token) > 2] for doc in new_olahraga['desc']]
new_olahraga['title'] = new_olahraga['title'].apply(remove_number)
new_olahraga['title'] = new_olahraga['title'].apply(word_tokenize)
new_olahraga['title'] = [[token for token in doc if len(token) > 2] for doc in new_olahraga['title']]
new_olahraga['fdist'] = new_olahraga['desc'].apply(FreqDist)

print(len(new_olahraga))
print(new_olahraga.head(2))

print('Frequency Tokens : \n') 
print(new_olahraga['fdist'].head().apply(lambda x : x.most_common()))

489
                                                   title  \
11404  [indonesia, ungguli, filipina, sepak, bola, ba...   
8770   [sidang, ferdy, sambo, kemarin, hakim, cerita,...   

                                                    desc  \
11404  [sepak, bola, indonesia, dibilang, berjaya, ti...   
8770   [ferdy, sambo, kemarin, saksi, terdakwa, pembu...   

                                                   fdist  
11404  {'sepak': 2, 'bola': 14, 'indonesia': 6, 'dibi...  
8770   {'ferdy': 20, 'sambo': 21, 'kemarin': 1, 'saks...  
Frequency Tokens : 

11404    [(filipina, 23), (basket, 21), (bola, 14), (ol...
8770     [(sambo, 21), (ferdy, 20), (putri, 11), (yosua...
8671     [(messi, 13), (riquelme, 8), (maradona, 5), (a...
11403    [(messi, 14), (ballon, 11), (dunia, 9), (piala...
8662     [(super, 32), (open, 21), (bwf, 12), (world, 1...
Name: fdist, dtype: object


In [15]:
from gensim.models import Phrases
bigram = Phrases(new_olahraga['desc'], min_count=20)
for idx in range(len(new_olahraga['desc'])):
    for token in bigram[new_olahraga['desc'].iloc[idx]]:
        if '_' in token:
            # Token is a bigram, add to document.
            new_olahraga['desc'].iloc[idx].append(token)
            word1, word2 = token.split("_")
            must_remove = ('kereta')
            if word1 not in must_remove:
                new_olahraga['desc'].iloc[idx].remove(word1)
            if word2 not in must_remove:
                new_olahraga['desc'].iloc[idx].remove(word2)
            # print(token)

In [16]:
dictionary = corpora.Dictionary(new_olahraga['desc'])
dictionary.filter_extremes(no_below=35, no_above=0.5)
print(dictionary)

corpus = [dictionary.doc2bow(berita) for berita in new_olahraga['desc']]

Dictionary<237 unique tokens: ['babak', 'basket', 'bermain', 'dilansir', 'dunia']...>


In [17]:
# Creating the object for LDA model using gensim library
Lda = gensim.models.ldamodel.LdaModel

total_topics = 4 # jumlah topik yang akan di extract
number_words = 25 # jumlah kata per topik

In [18]:
import os
from gensim.test.utils import datapath
the_path = PATH + olahraga + "model/lda_model" + "_" + str(total_topics) + "_" + str(number_words)
if not os.path.exists(the_path):
    os.mkdir(the_path)
temp_file = datapath(the_path + "/lda_model")
#if new
# lda_model = Lda(corpus, num_topics=total_topics, id2word=dictionary, passes=50, random_state=1)
# lda_model.save(temp_file)
# load
from gensim import models
lda_model = models.ldamodel.LdaModel.load(temp_file)

lda_model.show_topics(num_topics=total_topics, num_words=number_words)

[(0,
  '0.097*"psm" + 0.044*"psm_makassar" + 0.030*"pertandingan" + 0.027*"liga" + 0.026*"pelatih" + 0.025*"borneo" + 0.025*"wasit" + 0.021*"melawan" + 0.020*"madura_united" + 0.017*"bernardo_tavares" + 0.016*"bernardo" + 0.016*"bagus" + 0.016*"bermain" + 0.015*"lawan" + 0.015*"poin" + 0.014*"juku_eja" + 0.013*"kali" + 0.012*"kalah" + 0.012*"lini" + 0.012*"gol" + 0.011*"wiljan_pluim" + 0.011*"tavares" + 0.010*"paparnya" + 0.010*"meraih_kemenangan" + 0.010*"posisi"'),
 (1,
  '0.083*"argentina" + 0.083*"piala_dunia" + 0.052*"prancis" + 0.041*"maroko" + 0.035*"dunia" + 0.029*"messi" + 0.026*"gol" + 0.024*"jepang" + 0.022*"berhasil" + 0.022*"babak" + 0.021*"timnas" + 0.020*"negara" + 0.020*"lionel_messi" + 0.019*"qatar" + 0.018*"kali" + 0.017*"menang" + 0.017*"final" + 0.017*"skor" + 0.016*"grup" + 0.015*"juara" + 0.013*"inggris" + 0.012*"portugal" + 0.012*"final_piala" + 0.011*"spanyol" + 0.011*"kemenangan"'),
 (2,
  '0.102*"menit" + 0.047*"gawang" + 0.046*"gol" + 0.037*"babak" + 0.025*"k

In [19]:
# Word Count of Topic Keywords

from collections import Counter
topics = lda_model.show_topics(formatted=False, num_topics=total_topics, num_words=number_words)
# topic = lda_model.show_topics(num_topics=total_topics, num_words=number_words)
# print((topics[0]))
# print((topic[0]))
data_flat = [w for w_list in new_olahraga['desc'] for w in w_list]
counter = Counter(data_flat)

out = []
for i, topic in topics:
    for word, weight in topic:
        out.append([word, i , weight, counter[word]])

df_imp_wcount = pd.DataFrame(out, columns=['word', 'id', 'importance', 'word_count']) 
print(df_imp_wcount)

            word  id  importance  word_count
0            psm   0    0.096719         670
1   psm_makassar   0    0.044337         307
2   pertandingan   0    0.030149         566
3           liga   0    0.026538         402
4        pelatih   0    0.026184         403
..           ...  ..         ...         ...
95        timnas   3    0.011649         213
96         atlet   3    0.011325          91
97        negara   3    0.011187         201
98       terbaik   3    0.011099         115
99        basket   3    0.011077          89

[100 rows x 4 columns]


In [71]:
# xx = set(df_imp_wcount['word'].values)
# len(xx)

In [20]:
def format_topics_sentences(ldamodel=None, corpus=corpus, texts=new_olahraga['desc']):
    # Init output
    sent_topics_df = pd.DataFrame()
    # print(len(ldamodel[corpus]))

    dom = []
    perc = []
    keywords = []
    # Get main topic in each document
    for i, row_list in enumerate(ldamodel[corpus]):
        row = row_list[0] if ldamodel.per_word_topics else row_list            
        row = sorted(row, key=lambda x: (x[1]), reverse=True)
        # print(len(row))

        # Get the Dominant topic, Perc Contribution and Keywords for each document
        for j, (topic_num, prop_topic) in enumerate(row):
            if j == 0:  # => dominant topic
                wp = ldamodel.show_topic(topic_num, topn=number_words)
                topic_keywords = ", ".join([word for word, prop in wp])
                dom.append(int(topic_num))
                perc.append(round(prop_topic,4))
                keywords.append(topic_keywords)
                # sent_topics_df = pd.concat([sent_topics_df, pd.DataFrame([pd.Series([int(topic_num), round(prop_topic,4), topic_keywords])])], ignore_index=True)
                # sent_topics_df = sent_topics_df.append(pd.Series([int(topic_num), round(prop_topic,4), topic_keywords]), ignore_index=True)
            else:
                break
    # print(len(sent_topics_df))
    sent_topics_df['Dominant_Topic'] = dom
    sent_topics_df['Perc_Contribution'] = perc
    sent_topics_df['Topic_Keywords'] = keywords
    # sent_topics_df.columns = ['Dominant_Topic', 'Perc_Contribution', 'Topic_Keywords']

    # Add original text to the end of the output
    # sent_topics_df['Texts']= texts
    # print(len(sent_topics_df))
    return(sent_topics_df)

In [21]:
df_topic_sents_keywords = format_topics_sentences(ldamodel=lda_model, corpus=corpus, texts=new_olahraga['desc'])
df_topic_sents_keywords['Texts'] = 0
df_topic_sents_keywords['Title'] = 0

In [22]:
df_dominant_topic = df_topic_sents_keywords.reset_index()
# texts = []
for i in range(len(new_olahraga['desc'])):
    # print(new_olahraga['desc'].iloc[i])
    # texts.append(new_olahraga['desc'].iloc[i])
    df_dominant_topic['Texts'].iloc[i] = new_olahraga['desc'].iloc[i]
    df_dominant_topic['Title'].iloc[i] = new_olahraga['title'].iloc[i]
# df_dominant_topic['Texts'] = texts
df_dominant_topic.columns = ['Document_No', 'Dominant_Topic', 'Topic_Perc_Contrib', 'Keywords', 'Text', 'Title']

# df_topic_sents_keywords['Texts'].isna().value_counts()
df_dominant_topic.head(5)
df_dominant_topic.tail(5)

Document_No  Dominant_Topic  Topic_Perc_Contrib  \
484          484               3              0.9690   
485          485               1              0.6162   
486          486               3              0.9206   
487          487               3              0.9664   
488          488               3              0.7705   

                                              Keywords  \
484  indonesia, sepak_bola, olahraga, pertandingan,...   
485  argentina, piala_dunia, prancis, maroko, dunia...   
486  indonesia, sepak_bola, olahraga, pertandingan,...   
487  indonesia, sepak_bola, olahraga, pertandingan,...   
488  indonesia, sepak_bola, olahraga, pertandingan,...   

                                                  Text  \
484  [pemain, veteran, goh, liu, ying, sambut, keha...   
485  [bergulir, keseruan, kejutan, laga, laga, pemb...   
486  [daftar, tim, pesertaliga, futsal, profesional...   
487  [klubdewa, basketball, resmi, pindah, kandang,...   
488  [tiketindonesia, dijual, besok, daftar, harga,...   

                                                 Title  
484  [goh, liu, ying, sambut, nova, widianto, harap...  
485                       [nonton, pesta, sepak, bola]  
486  [daftar, tim, peserta, liga, futsal, profesion...  
487  [klub, dewa, united, basketball, resmi, pindah...  
488  [tiket, indonesia, masters, dijual, besok, daf...

In [425]:
df_dominant_topic.to_csv(PATH + olahraga + 'df_dominant_topic.csv')

In [74]:
from datetime import datetime
now = datetime.now() # current date and time
date_time = now.strftime("%m-%d-%Y_%H-%M-%S")
print("date and time:",date_time)
LDAvis_html = 'ldavis_prepared_'+ str(total_topics)+"_"+str(number_words)+"_"+str(date_time)
LDAvis_prepared = pyLDAvis.gensim.prepare(lda_model, corpus, dictionary)
with open(PATH + olahraga + LDAvis_html, 'wb') as f:
        pickle.dump(LDAvis_prepared, f)
pyLDAvis.save_html(LDAvis_prepared, PATH + olahraga + LDAvis_html +'.html')

date and time: 06-24-2023_08-22-27


In [ ]:
with open(PATH + olahraga + LDAvis_html, 'rb') as f:
    LDAvis_prepared = pickle.load(f)

In [23]:
lda_what_olahraga = []
word_topics = set(df_imp_wcount['word'].values)
for i in range(len(df_dominant_topic)):
    val = []
    for n, key in enumerate(word_topics):
        if key in df_dominant_topic['Text'].iloc[i]:
            val.append(key)
    lda_what_olahraga.append(val)

print(lda_what_olahraga)

[['lawan', 'kalah', 'bermain', 'gol', 'timnas', 'liga', 'sepak_bola', 'basket', 'babak', 'indonesia', 'skor', 'negara', 'melawan', 'final', 'olahraga', 'kemenangan', 'dunia', 'pertandingan', 'lapangan'], ['bermain', 'jakarta', 'kali', 'lapangan'], ['messi', 'lawan', 'bermain', 'gol', 'timnas', 'liga', 'babak', 'klub', 'argentina', 'kali', 'piala_dunia', 'terbaik', 'dunia', 'lionel_messi', 'umpan'], ['messi', 'mencetak_gol', 'gol', 'argentina', 'berhasil', 'kali', 'piala_dunia', 'posisi', 'prancis', 'final_piala', 'final', 'qatar', 'memiliki', 'terbaik', 'dunia', 'lionel_messi'], ['turnamen', 'nama', 'indonesia', 'posisi', 'poin', 'final', 'terbaik', 'lapangan'], ['kompetisi', 'nama', 'jakarta', 'basket', 'indonesia', 'berhasil', 'kali', 'negara', 'nasional', 'memiliki', 'olahraga', 'dunia', 'pertandingan'], ['spanyol', 'latihan', 'sepak_bola', 'basket', 'inggris', 'argentina', 'piala_dunia', 'prancis', 'memiliki', 'olahraga', 'dunia'], ['jakarta', 'basket', 'indonesia', 'kali', 'atlet'

In [24]:
lda_title_what = []
word_topics = set(df_imp_wcount['word'].values)
for i in range(len(df_dominant_topic)):
    val = []
    for n, key in enumerate(word_topics):
        if key in df_dominant_topic['Title'].iloc[i]:
            val.append(key)
    lda_title_what.append(val)

print(lda_title_what)

[['basket', 'indonesia'], [], ['messi'], ['messi'], ['turnamen'], ['basket', 'indonesia'], [], ['jakarta', 'lapangan'], ['permainan'], [], ['olahraga', 'pertandingan', 'lapangan'], [], [], [], [], ['lapangan'], ['terbaik'], [], ['kalah'], ['dunia'], ['dunia'], [], [], ['terbaik', 'dunia'], ['kompetisi', 'dunia'], [], ['pelatih'], [], [], ['tavares', 'pelatih', 'bernardo', 'psm'], [], ['timnas', 'bernardo', 'psm'], ['menang'], ['penalti'], ['messi', 'juara', 'dunia'], [], [], ['turnamen', 'jakarta', 'basket'], [], ['klub', 'kerja'], ['wasit', 'pelatih', 'psm'], [], ['stadion', 'jakarta'], [], ['kemenangan'], ['wasit', 'pelatih', 'kalah'], ['messi', 'argentina'], ['menang', 'argentina'], ['messi', 'argentina', 'final', 'dunia'], ['argentina', 'prancis'], ['messi', 'argentina', 'juara', 'dunia'], ['menang', 'messi', 'argentina', 'final', 'dunia'], ['argentina', 'maroko', 'prancis', 'final', 'dunia'], ['messi', 'argentina', 'dunia'], ['messi', 'argentina'], ['messi', 'dunia'], ['argentina'

In [25]:
for n, word_list in enumerate(lda_title_what):
    val = []
    for word in word_list:
        if word in lda_what_olahraga[n]:
            continue
        val.append(word)
    lda_what_olahraga[n].extend(val)
    # if val:
    #     print(n)
    #     print(val)

print(lda_what_olahraga)

[['lawan', 'kalah', 'bermain', 'gol', 'timnas', 'liga', 'sepak_bola', 'basket', 'babak', 'indonesia', 'skor', 'negara', 'melawan', 'final', 'olahraga', 'kemenangan', 'dunia', 'pertandingan', 'lapangan'], ['bermain', 'jakarta', 'kali', 'lapangan'], ['messi', 'lawan', 'bermain', 'gol', 'timnas', 'liga', 'babak', 'klub', 'argentina', 'kali', 'piala_dunia', 'terbaik', 'dunia', 'lionel_messi', 'umpan'], ['messi', 'mencetak_gol', 'gol', 'argentina', 'berhasil', 'kali', 'piala_dunia', 'posisi', 'prancis', 'final_piala', 'final', 'qatar', 'memiliki', 'terbaik', 'dunia', 'lionel_messi'], ['turnamen', 'nama', 'indonesia', 'posisi', 'poin', 'final', 'terbaik', 'lapangan'], ['kompetisi', 'nama', 'jakarta', 'basket', 'indonesia', 'berhasil', 'kali', 'negara', 'nasional', 'memiliki', 'olahraga', 'dunia', 'pertandingan'], ['spanyol', 'latihan', 'sepak_bola', 'basket', 'inggris', 'argentina', 'piala_dunia', 'prancis', 'memiliki', 'olahraga', 'dunia'], ['jakarta', 'basket', 'indonesia', 'kali', 'atlet'

In [26]:
idxs = []
idxs_tp = []
idxs_tn = []
idxs_lda = [] #not in lda words
total = 0
total_tp = 0
total_tn = 0
total_lda = 0
check_lda = ('dunia', 'sepak_bola')
for i in range(len(lda_what_olahraga)):
    flag = True
    deflag = True
    ldaf = True
    for token in lda_what_olahraga[i]:
        if token in check_lda:
            flag = False
        if token in df_imp_wcount['word'].values:
            ldaf = False
    for token in df_dominant_topic['Text'].iloc[i]:
        if token in check_lda:
            deflag = False
    for token in df_dominant_topic['Title'].iloc[i]:
        if token in check_lda:
            deflag = False
    if flag != deflag:
        total += 1
        idxs.append(i)
    elif flag == deflag and flag == False:
        total_tp += 1
        idxs_tp.append(i)
    elif flag == deflag and flag == True:
        total_tn += 1
        idxs_tn.append(i)
    if ldaf:
        total_lda += 1
        idxs_lda.append(i)
print(len(df_dominant_topic))
print(total)
print(total_tp)
print(total_tn)
print(total_lda)


489
0
279
210
2


In [31]:
lda_check = []
for word in check_lda:
    if word not in df_imp_wcount['word'].values:
        lda_check.append(word)
print(lda_check)

[]


In [32]:
print(idxs_tn)

[1, 4, 7, 16, 17, 18, 21, 22, 26, 27, 31, 32, 33, 36, 37, 38, 44, 46, 47, 57, 58, 61, 62, 63, 64, 67, 71, 72, 73, 77, 78, 79, 82, 83, 89, 90, 92, 95, 96, 99, 100, 103, 104, 105, 106, 107, 108, 122, 123, 126, 129, 130, 131, 133, 134, 135, 136, 137, 139, 140, 141, 142, 144, 145, 148, 149, 150, 151, 157, 158, 159, 164, 165, 166, 169, 170, 174, 179, 186, 188, 190, 191, 192, 193, 199, 206, 210, 211, 212, 216, 217, 218, 219, 220, 221, 222, 223, 226, 227, 251, 252, 254, 255, 256, 257, 259, 262, 263, 264, 265, 266, 267, 268, 269, 270, 271, 272, 274, 276, 277, 279, 280, 282, 283, 284, 285, 286, 287, 288, 289, 290, 291, 292, 293, 294, 295, 297, 302, 303, 304, 305, 306, 308, 310, 312, 313, 314, 315, 317, 325, 327, 329, 331, 350, 351, 352, 353, 356, 361, 362, 363, 365, 366, 372, 390, 391, 409, 412, 414, 417, 421, 423, 425, 428, 429, 430, 431, 432, 433, 434, 435, 438, 441, 446, 448, 449, 451, 457, 459, 460, 461, 462, 465, 466, 467, 468, 469, 470, 472, 474, 475, 477, 478, 479, 481, 482, 483, 484, 48

In [32]:
# text  = preprocessing(old_kecelakaan['desc'][old_kecelakaan['desc'].str.find('hari') != -1].iloc[0])
# text
i = idxs_tn[0]
print(df_dominant_topic['Keywords'].iloc[i])
print(type(df_dominant_topic['Keywords'].iloc[i]))
print(df_dominant_topic['Text'].iloc[i])
print(type(df_dominant_topic['Text'].iloc[i]))
print(df_dominant_topic['Keywords'].iloc[i].split(", "))
print(lda_what_olahraga[i])


indonesia, sepak_bola, olahraga, pertandingan, liga, pelatih, lapangan, memiliki, klub, stadion, sepakbola, dunia, jakarta, kompetisi, bermain, nama, latihan, nasional, turnamen, kerja, timnas, atlet, negara, terbaik, basket
<class 'str'>
['ferdy', 'sambo', 'kemarin', 'saksi', 'terdakwa', 'pembunuhan', 'brigadir', 'yosua', 'richard', 'eliezer', 'ricky', 'rizal', 'kuat', 'ruf', 'ferdy', 'terdakwa', 'sidang', 'dipimpin', 'hakim', 'wahyu', 'iman', 'santoso', 'ferdy', 'sambo', 'menceritakan', 'kronologi', 'pembunuhan', 'brigadir', 'nofriansyah', 'yosua', 'hutabarat', 'sesuai', 'versinya', 'wahyu', 'menganggap', 'keterangan', 'ferdy', 'sambo', 'masuk', 'akal', 'wahyu', 'memperingatkan', 'ferdy', 'sambo', 'diperiksa', 'saksi', 'terdakwa', 'kesaksian', 'ferdy', 'sambo', 'rangkaian', 'tindakan', 'berkaitan', 'terdakwa', 'richard', 'eliezer', 'ricky', 'rizal', 'kuat', 'maruf', 'perhatikan', 'cerita', 'saudara', 'nggak', 'masuk', 'diakal', 'bukti', 'bukti', 'nggak', 'masuk', 'akal', 'wahyu', 'pe

In [27]:
before_what_olahraga = old[old['berita_topik_id'] == 6]
before_what_olahraga = before_what_olahraga[['berita_title', 'qe_what', 'berita_desc']]
before_what_olahraga = before_what_olahraga.dropna(subset=['berita_desc'])
before_what_olahraga.sort_values('berita_desc', inplace=True)
before_what_olahraga.drop_duplicates(subset='berita_desc', keep=False, inplace=True)
print(before_what_olahraga)
# print(before_what_olahraga['qe_what'].iloc[i])
# print(before_what_olahraga['berita_title'].iloc[i])
# print(before_what_olahraga['berita_desc'].iloc[i])

                                            berita_title  \
11404  Indonesia Ungguli Filipina di Sepak Bola, Baga...   
8770   Sidang Ferdy Sambo Kemarin, Hakim Sebut Cerita...   
8671   Ini Deretan 4 Pesepakbola Legendaris yang Memb...   
11403  Deretan Pesepakbola yang Mendukung Messi Menju...   
8662   Jadwal Badminton BWF 2023: Ada 30 Turnamen Sup...   
...                                                  ...   
8768   Goh Liu Ying Sambut Nova Widianto, Harapan Bar...   
8970   Cuma Rp 1.000 Bisa Nonton Pesta Sepak Bola 202...   
8666   Daftar Tim Peserta Liga Futsal Profesional Ind...   
8660   Klub Dewa United Basketball Resmi Pindah Kanda...   
8667   Tiket Indonesia Masters 2023 Mulai Dijual Beso...   

                                                 qe_what  \
11404  bertanding, dunia, aksi, pemain, pendidikan, h...   
8770   bulutangkis, mantan, aksi, mi, s, w, arena, ta...   
8671   dunia, mantan, langsung, berlatih, pemain, sep...   
11403  penghargaan, dunia, mantan, pema

In [28]:
total_empty = 0
empty_val = []
idxs_total = []
idxs_total.extend(idxs_tp)
idxs_total.extend(idxs_tn)
idxs_total = set(idxs_total)

with open(PATH + olahraga + 'true_negative_' + str(total_topics) +'.txt', 'w', encoding='UTF8') as f:
    nl = "\n"
    dashes = '--------------------------------------'
    for x in idxs_total:
        f.write(dashes + nl)
        f.write(before_what_olahraga['berita_title'].iloc[x] + nl)
        f.write(str(before_what_olahraga['qe_what'].iloc[x]) + nl)
        f.write(str(lda_what_olahraga[x]) + nl)
        # print(before_what_kecelakaan['berita_title'].iloc[x])
        # print(before_what_kecelakaan['qe_what'].iloc[x])
        # print(lda_what_kecelakaan[x])

        if len(lda_what_olahraga[x])<3:
            total_empty += 1
            empty_val.append(x)

print(total_empty)
print(empty_val)


7
[101, 166, 223, 352, 400, 403, 404]


In [35]:
hitung = Counter()
for i in idxs_tp:
    hitung.update(lda_what_olahraga[i])
    # hitung.update(lda_title_what[i])
    # print('--------------------------------------')
    # print(before_what_olahraga['berita_title'].iloc[i])
    # print(before_what_olahraga['berita_desc'].iloc[i])
    # print(before_what_olahraga['qe_what'].iloc[i])
    # print(lda_what_olahraga[i])
hitung

Counter({'sepak_bola': 213,
         'dunia': 152,
         'pertandingan': 131,
         'piala_dunia': 120,
         'indonesia': 107,
         'memiliki': 101,
         'kali': 98,
         'bermain': 95,
         'pelatih': 89,
         'gol': 88,
         'babak': 86,
         'liga': 81,
         'berhasil': 77,
         'lapangan': 75,
         'melawan': 72,
         'sepakbola': 67,
         'menang': 65,
         'timnas': 62,
         'skor': 62,
         'argentina': 61,
         'juara': 60,
         'negara': 59,
         'klub': 58,
         'stadion': 58,
         'lawan': 57,
         'prancis': 55,
         'qatar': 55,
         'kemenangan': 54,
         'kompetisi': 54,
         'menit': 54,
         'terbaik': 53,
         'final': 49,
         'permainan': 49,
         'gawang': 49,
         'psm': 49,
         'poin': 49,
         'psm_makassar': 49,
         'mencetak_gol': 48,
         'kalah': 47,
         'olahraga': 46,
         'nasional': 46,
         'pos

# Create Comparison

In [457]:
# df_result_lda = df_dominant_topic[['Title', 'Text']]
df_result_lda['what_lda'] = lda_what_olahraga
df_result_lda['what_qe'] = 0
# df_result_lda['title_old'] = 0
df_result_lda['desc_old'] = 0
for i in range(len(df_result_lda)):
    df_result_lda['what_qe'].iloc[i] = before_what_olahraga['qe_what'].iloc[i]
    # df_result_lda['title_old'].iloc[i] = before_what_olahraga['berita_title'].iloc[i]
    df_result_lda['desc_old'].iloc[i] = before_what_olahraga['berita_desc'].iloc[i]

# df_result_lda.to_csv(PATH + olahraga + 'df_result_lda.csv')   
df_result_lda.to_excel(PATH + olahraga + 'df_result_lda.xlsx', index=None) 
df_result_lda
# print(before_what_olahraga['qe_what'].iloc[0])

Title  \
0    [indonesia, ungguli, filipina, sepak, bola, ba...   
1    [sidang, ferdy, sambo, kemarin, hakim, cerita,...   
2    [deretan, pesepakbola, legendaris, membimbing,...   
3    [deretan, pesepakbola, mendukung, messi, menju...   
4    [jadwal, badminton, bwf, turnamen, super, majo...   
..                                                 ...   
484  [goh, liu, ying, sambut, nova, widianto, harap...   
485                       [nonton, pesta, sepak, bola]   
486  [daftar, tim, peserta, liga, futsal, profesion...   
487  [klub, dewa, united, basketball, resmi, pindah...   
488  [tiket, indonesia, masters, dijual, besok, daf...   

                                                  Text  \
0    [indonesia, dibilang, berjaya, timnas, indones...   
1    [ferdy, sambo, kemarin, saksi, terdakwa, pembu...   
2    [perjalanan, pemain, terbaik, lepas, pemain, l...   
3    [berhasil, mengalahkan, prancis, melengkapi, t...   
4    [jadwal, badminton, dirilis, badminton, federa...   
..                                                 ...   
484  [pemain, veteran, goh, liu, ying, sambut, keha...   
485  [bergulir, keseruan, kejutan, laga, laga, pemb...   
486  [daftar, tim, pesertaliga, futsal, profesional...   
487  [klubdewa, basketball, resmi, pindah, kandang,...   
488  [tiketindonesia, dijual, besok, daftar, harga,...   

                                              what_lda  \
0    [gol, lapangan, sepak_bola, basket, dunia, mel...   
1                   [lapangan, kali, bermain, jakarta]   
2    [klub, gol, lionel_messi, argentina, dunia, ka...   
3    [prancis, gol, lionel_messi, argentina, memili...   
4    [lapangan, final, terbaik, indonesia, nama, po...   
..                                                 ...   
484            [indonesia, bermain, turnamen, pelatih]   
485  [gol, lapangan, lionel_messi, argentina, sepak...   
486  [klub, liga, unggul, terbaik, kompetisi, indon...   
487   [memiliki, basket, bagus, atlet, olahraga, klub]   
488  [dunia, kali, pertandingan, babak, final, indo...   

                                               what_qe  \
0    bertanding, dunia, aksi, pemain, pendidikan, h...   
1    bulutangkis, mantan, aksi, mi, s, w, arena, ta...   
2    dunia, mantan, langsung, berlatih, pemain, sep...   
3    penghargaan, dunia, mantan, pemain, sepakbola,...   
4    bulutangkis, turnamen, kekuatan, ganda, putra,...   
..                                                 ...   
484  turnamen, langsung, veteran, pemain, pensiun, ...   
485  dunia, aksi, program, olahraga, sepakbola, per...   
486  tampil, langsung, menduduki, kompetisi, acara,...   
487  atlet, langsung, olahraga, mi, s, w, ry, indus...   
488  bulutangkis, turnamen, dunia, langsung, aksi, ...   

                                             title_old  \
0    Indonesia Ungguli Filipina di Sepak Bola, Baga...   
1    Sidang Ferdy Sambo Kemarin, Hakim Sebut Cerita...   
2    Ini Deretan 4 Pesepakbola Legendaris yang Memb...   
3    Deretan Pesepakbola yang Mendukung Messi Menju...   
4    Jadwal Badminton BWF 2023: Ada 30 Turnamen Sup...   
..                                                 ...   
484  Goh Liu Ying Sambut Nova Widianto, Harapan Bar...   
485  Cuma Rp 1.000 Bisa Nonton Pesta Sepak Bola 202...   
486  Daftar Tim Peserta Liga Futsal Profesional Ind...   
487  Klub Dewa United Basketball Resmi Pindah Kanda...   
488  Tiket Indonesia Masters 2023 Mulai Dijual Beso...   

                                              desc_old  
0     \- Dalam sepak bola, Indonesia bisa dibilang ...  
1     \- Ferdy Sambo kemarin menjadi saksi untuk ti...  
2     \- Perjalanan  menjadi pemain terbaik di duni...  
3     \- Setelah berhasil mengalahkan Prancis di fi...  
4    Berikut jadwal badminton 2023 yang dirilis ole...  
..                                                 ...  
484  \- Pemain veteran Goh Liu Ying sambut kehadira...  
485  \- Pesta sepak bola 2022 telah bergulir. Sejum...  
486  _Daftar Tim PesertaLiga Futsal Profesional Ind

In [456]:
# df_imp_wcount[df_imp_wcount['word'] == 'bulutangkis']